In [1]:
from alpha_vantage.timeseries import TimeSeries
from pprint import pprint
from selenium import webdriver
from bs4 import BeautifulSoup
import edgar
import time
from pathlib import Path
import pandas as pd
import os
import re
from datetime import datetime
from datetime import date
import json
import requests
import calendar
import sys
import string
import shutil
import ast
from io import StringIO
from contextlib import redirect_stdout
import glob
import spacy
import torch
import classy_classification

In [2]:
def getTrainDataForSenTag():
    rfile = "../../Summary/DATA/SENTAG/TDATA.json"
    data = None
    with open(rfile, encoding="utf-8") as f:
        data = json.load(f)
    return data

In [3]:
def getModelForSenTag():
    data = getTrainDataForSenTag()
    if not data:
        return None
    nlp = spacy.blank("en")
    sentag = nlp.add_pipe(
        "text_categorizer", 
        config={
            "data": data, 
            "model": "sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2",
            "device": "cpu"
        }
    )
    return(nlp)

In [4]:
nlp = getModelForSenTag()

Ignore MatMul due to non constant B: /[MatMul_68]
Ignore MatMul due to non constant B: /[MatMul_73]
Ignore MatMul due to non constant B: /[MatMul_162]
Ignore MatMul due to non constant B: /[MatMul_167]
Ignore MatMul due to non constant B: /[MatMul_256]
Ignore MatMul due to non constant B: /[MatMul_261]
Ignore MatMul due to non constant B: /[MatMul_350]
Ignore MatMul due to non constant B: /[MatMul_355]
Ignore MatMul due to non constant B: /[MatMul_444]
Ignore MatMul due to non constant B: /[MatMul_449]
Ignore MatMul due to non constant B: /[MatMul_538]
Ignore MatMul due to non constant B: /[MatMul_543]
Ignore MatMul due to non constant B: /[MatMul_632]
Ignore MatMul due to non constant B: /[MatMul_637]
Ignore MatMul due to non constant B: /[MatMul_726]
Ignore MatMul due to non constant B: /[MatMul_731]
Ignore MatMul due to non constant B: /[MatMul_820]
Ignore MatMul due to non constant B: /[MatMul_825]
Ignore MatMul due to non constant B: /[MatMul_914]
Ignore MatMul due to non constant

In [5]:
# Predict paragraph tag using few shot model
def getSenTag(nlp, pg):
    cats = nlp(pg)._.cats
    maxVal = max(cats, key=cats.get)
    return maxVal

In [6]:
key='8NBLCOTKI465W93V'
secKey = "d76154d8c11c709dbdaaa8cdf25c2b69424847ba85f2a569742d588d0d53c8b0"
tblCnt = 0

In [7]:
ts = TimeSeries(key=key, output_format='pandas')
#data, meta_data = ts.get_intraday(symbol='MSFT',interval='1min', outputsize='full')
data, meta_data = ts.get_intraday(symbol='MSFT',interval='1min')
pprint(data.head(2))

                     1. open  2. high  3. low  4. close  5. volume
date                                                              
2024-01-22 19:59:00   396.53   396.56   396.5    396.56      437.0
2024-01-22 19:58:00   396.53   396.56   396.5    396.51      113.0


In [8]:
from alpha_vantage.sectorperformance import SectorPerformances
import matplotlib.pyplot as plt

sp = SectorPerformances(key=key, output_format='pandas')
data, meta_data = sp.get_sector()
data['Rank A: Real-Time Performance'].plot(kind='bar')
plt.title('Real Time Performance (%) per Sector')
plt.tight_layout()
plt.grid()
plt.show()

ValueError: Error getting data from the api, no return was given.

In [9]:
import requests
url = 'https://www.alphavantage.co/query?function=GLOBAL_QUOTE&symbol=IBM&apikey=demo'
print(url)

https://www.alphavantage.co/query?function=GLOBAL_QUOTE&symbol=IBM&apikey=demo


In [10]:
r = requests.get(url)
output = r.json()

In [11]:
print(output["Global Quote"]["05. price"])

172.8300


In [12]:
import pandas as pd
from io import StringIO
url = 'https://www.alphavantage.co/query?function=EARNINGS_CALENDAR&symbol=MSFT&horizon=3month&apikey=8NBLCOTKI465W93V'
r = requests.get(url)
content = r.text
print(str(content))

symbol,name,reportDate,fiscalDateEnding,estimate,currency



In [13]:
def getOrgProfile(org):
    try:
        url = "https://www.alphavantage.co/query?function=OVERVIEW&symbol="+org+"&apikey=8NBLCOTKI465W93V"
        r = requests.get(url)
        data = r.json()
        return data
    except Exception as e:
        print(e)
        return None

In [14]:
def getQtrsFrmRpt(org, edate, fynd):
    #print(edate)
    dateObj = datetime.strptime(edate, '%Y-%m-%d')
    #print(dateObj.month)
    emonth = dateObj.month
    eyr = dateObj.year
    k = 1
    qend = fynd
    qstart = 0
    year = eyr
    #print(year)
    qtrs = dict()
    while(k!=5):
        #print(k)
        qstart = (qend + 1)%12
        qend = (qend + 3)%12
        if qstart == 0:
            qstart = 12
        if qend == 0:
            qend = 12
        if((emonth >= qstart and emonth <= qend) or (qstart > qend and (emonth >= qstart or emonth <= qend))):
            #print("CQTR:", "Q"+str(k))
            qtrs["CQTR"] = "Q"+str(k)
            qtrs["GQTR"] = "Q"+str(k) # Guidance qtr is same as current qtr
            qtrs["CYR"] = str(year)
            qtrs["GYR"] = str(year) # Guidance year same as current year
            eqtr = (k-1)%4
            if(eqtr == 0):
                eqtr = 4
            nqtr = (k+1)%4
            if(nqtr == 0):
                nqtr = 4
            pqtr = (k-2)%4
            if(pqtr == 0):
                pqtr = 4
            qtrs["EQTR"] = "Q"+str(eqtr)
            qtrs["PQTR"] = "Q"+str(pqtr)
            #print("EQTR:", "Q"+str(eqtr))
            #print("PQTR:", "Q"+str(pqtr))
            #print("NQTR:", "Q"+str(nqtr))
        #print("Q"+str(k), "START", qstart)
        #print("Q"+str(k), "END", qend)
        qtr = "Q"+str(k)
        if (qtr not in qtrs):
            qtrs[qtr] = dict()
        qtrs[qtr]["START"] = qstart
        qtrs[qtr]["SM"] = calendar.month_abbr[qstart].upper()
        qtrs[qtr]["END"] = qend
        qtrs[qtr]["EM"] = calendar.month_abbr[qend].upper()
        #print("Q"+str(k), "YEAR", year)
        k = k + 1
    
    #print(eyr)   
    if("EQTR" in qtrs and "CQTR" in qtrs and "PQTR" in qtrs):
        eqtrEnd = qtrs[qtrs["EQTR"]]["END"]
        cqtrEnd = qtrs[qtrs["CQTR"]]["END"]
        pqtrEnd = qtrs[qtrs["PQTR"]]["END"]
        #print(eqtrEnd, cqtrEnd, pqtrEnd)
        qtrs["EYR"] = str(eyr)
        qtrs["PYR"] = str(eyr)
        #print(eqtrEnd, cqtrEnd, qtrs[qtrs["CQTR"]]["START"], qtrs[qtrs["CQTR"]]["END"])
        if(eqtrEnd > cqtrEnd):
            if(qtrs[qtrs["CQTR"]]["START"] > qtrs[qtrs["CQTR"]]["END"] and emonth > fynd):
                gyr = year + 1
                qtrs["GYR"] = str(gyr)
                qtrs["EYR"] = str(gyr - 1)
            else:
                qtrs["EYR"] = str(eyr - 1)
                qtrs["PYR"] = str(eyr - 1)
        if(pqtrEnd > eqtrEnd):
            qtrs["PYR"] = str(int(qtrs["EYR"]) - 1)
    if(emonth <= fynd):
        qtrs["CFYR"] = str(year)
    else:
        qtrs["CFYR"] = str(year + 1)
    qtrs["FYR"] = qtrs["CFYR"]
    if(qtrs[qtrs["EQTR"]]["END"] <= fynd and qtrs["EQTR"] > qtrs["CQTR"]):
        qtrs["FYR"] = str(int(qtrs["FYR"]) - 1)
    qtrs["EFYR"] = qtrs["FYR"]
    qtrs["PFYR"] = qtrs["FYR"]
    if(qtrs["PQTR"] > qtrs["EQTR"]):
        qtrs["PFYR"] = str(int(qtrs["FYR"]) - 1)
    qtrs["GFYR"] = qtrs["CFYR"]
    #qtrs["EYR"] = qtrs["FYR"]
    #qtrs["CYR"] = qtrs["CFYR"]
    #qtrs["PYR"] = qtrs["FYR"]
    qtrs["CYR"] = qtrs["GYR"]
    #print(qtrs)
    return (qtrs)

In [15]:
content = str(content)
f = StringIO(content)
#col_list = ["symbol"]
tbl = pd.read_csv(f, nrows=1)
#print(tbl)
#print(tbl["reportDate"][0])
print (len(tbl["reportDate"]))
if len(tbl["reportDate"]) > 0:
    dateStr = tbl["reportDate"][0]
    print(dateStr)

0


In [16]:
import datetime
dateStr = datetime.datetime.strptime(dateStr, "%Y-%m-%d").date()
d = dateStr.strftime("%b %d")
print("Output 3:", d)

NameError: name 'dateStr' is not defined

In [17]:
#qtrs = [[1,3],[4,6],[7,9],[10,12]]
months = 12
qtr_len = 3
qtr_no = int(months/qtr_len)
qtrs = list()
start = 0
for i in range(qtr_no):
    qtr = list()
    start = 1 + start
    end = start + 2
    qtr.append(start)
    qtr.append(end)
    qtrs.append(qtr)
    start = end

print(qtrs)
month = 10
for o in qtrs:
    #print (o)
    if month >= o[0] and month <= o[1]:
        print(o)
        break

[[1, 3], [4, 6], [7, 9], [10, 12]]
[10, 12]


In [18]:
def millify(num):
    num = float('{:.3g}'.format(num))
    magnitude = 0
    while abs(num) >= 1000:
        magnitude += 1
        num /= 1000.0
    return '{}{}'.format('{:f}'.format(num).rstrip('0').rstrip('.'), ['', 'K', 'MN', 'BN', 'TN'][magnitude])

In [19]:
def get_qtrs():
    months = 12
    qtr_len = 3
    qtr_no = int(months/qtr_len)
    qtrs = list()
    start = 0
    for i in range(qtr_no):
        qtr = list()
        start = 1 + start
        end = start + 2
        qtr.append(start)
        qtr.append(end)
        qtrs.append(qtr)
        start = end
    return qtrs

In [20]:
def get_qtr_range(month, qtrs):
    #print(month)
    for o in qtrs:
        if month >= o[0] and month <= o[1]:
            return o

In [21]:
def get_stock_earningDate_detail(stock):
    url = 'https://www.alphavantage.co/query?function=EARNINGS_CALENDAR&symbol=' + stock + '&horizon=3month&apikey=8NBLCOTKI465W93V'
    try:
        r = requests.get(url)
        content = r.text
        #print(str(content))
        return content
    except e:
        print(e)
        return None
    return None

In [22]:
indate = get_stock_earningDate_detail("NET")
print(indate)

symbol,name,reportDate,fiscalDateEnding,estimate,currency
NET,Cloudflare Inc - Class A,2024-02-07,2023-12-31,0.12,USD



In [23]:
import sys
from colorama import Fore, init, Back, Style
import openpyxl
import re

path = "../../Summary/stocks.xlsx"
wb_obj = openpyxl.load_workbook(path.strip())
# from the active attribute 
sheet_obj = wb_obj.active
sheet_obj

<Worksheet "12-Sep-2020">

In [24]:
max_column=sheet_obj.max_column
max_row=sheet_obj.max_row
max_column, max_row

(12, 58)

In [25]:
data = sheet_obj.cell(1,2)
print(data.value)

Quantity


In [26]:
path = "../../Summary/stocks_csv.csv"
d = pd.read_csv(path)
d["Ticker"]

0       NIO
1      ABBV
2       EPD
3       ENB
4      KNSL
       ... 
111    ENPH
112    PANW
113    AMAT
114    ISRG
115     NaN
Name: Ticker, Length: 116, dtype: object

In [27]:
from datetime import datetime
qtrs = get_qtrs()
print(qtrs)
month = datetime.now().month
year = datetime.now().year
print(month, year)
qtr = get_qtr_range(month, qtrs)
qtr

[[1, 3], [4, 6], [7, 9], [10, 12]]
1 2024


[1, 3]

In [28]:
import math
months = ["0", "JAN", "FEB", "MAR", "APR", "MAY", "JUN", "JUL", "AUG", "SEP", "OCT", "NOV", "DEC"]
print(months[qtr[0]], months[qtr[1]])
cell = months[qtr[0]]+"-"+months[qtr[1]]+" "+ str(year)
#cell = months[7]+"-"+months[9]+" "+ str(year)
print(cell)
if cell not in d:
    d[cell] = None
    d.to_csv(path, index=False)
print(d[cell][3])
#if math.isnan(d[cell][3]):
#    print("Hello")

for index, value in enumerate(d[cell]):
    #print(index, value)
    #print(type(value))
    if type(value) is str:
        print(value)

JAN MAR
JAN-MAR 2024
09-Feb
28-Feb
02-Feb
01-Feb
09-Feb
14-Feb
19-Mar
02-Feb
14-Feb
01-Feb
05-Mar
07-Mar
20-Feb
26-Feb
07-Feb
05-Feb
13-Feb
05-Mar
12-Mar
23-Jan
13-Feb
20-Feb
13-Feb
06-Feb
26-Feb
29-Feb
26-Feb
13-Feb
05-Feb
20-Feb
21-Feb
21-Feb
20-Feb
06-Feb
20-Feb
14-Feb
20-Feb
05-Feb
30-Jan
13-Feb
12-Feb
19-Feb
26-Feb
26-Feb
15-Mar
26-Feb
26-Feb
15-Feb
26-Feb
14-Feb
29-Jan
31-Jan
19-Feb
05-Feb
21-Feb
12-Feb
20-Feb
14-Feb
15-Feb
14-Feb
28-Feb
07-Mar
12-Feb
14-Feb
21-Feb
14-Feb
14-Feb
26-Feb
30-Jan
26-Feb
28-Feb
27-Mar
21-Feb
20-Feb
21-Feb
05-Feb
14-Feb
21-Feb
29-Jan
07-Feb
13-Feb
31-Jan
23-Jan
13-Mar
21-Mar
28-Feb
01-Mar
12-Feb
07-Feb
12-Feb
20-Feb
20-Feb
14-Mar
06-Feb
21-Feb
26-Feb
26-Mar
06-Mar
05-Feb
31-Jan
13-Feb
28-Feb
26-Mar
07-Feb
28-Feb
29-Feb
05-Feb
12-Jan - DN (169.0500)
26-Feb
18-Feb
29-Feb
05-Feb
19-Feb
14-Feb
23-Jan


In [29]:
def get_dateStr(dateStr):
    dateStr = datetime.strptime(dateStr, "%Y-%m-%d").date()
    month = dateStr.month
    dStr = dateStr.strftime("%d-%b")
    return month, dStr

In [30]:
def get_month(dateStr):
    dateStr = datetime.strptime(dateStr, "%Y-%m-%d").date()
    month = dateStr.month
    #print(month)
    return month

In [31]:
def is_currentQtr(month):
    qtrs = get_qtrs()
    currMonth = datetime.now().month
    qtr = get_qtr_range(currMonth, qtrs)
    earningQtr = get_qtr_range(month, qtrs)
    if qtr == earningQtr:
        return True
    return False

In [32]:
status = is_currentQtr(7)
print(status)

False


In [33]:
from datetime import timedelta
print(d[cell][0])
content = d[cell][0]
if "(" not in content:
    print(True)
    #data = content.split(" ")
    #dateStr = (data[0].strip() + "-" + str(year))
    dateStr = (content.strip() + "-" + str(year))
    print(dateStr)
    dateS = datetime.strptime(dateStr, "%d-%b-%Y").date()
    nextDate = dateS + timedelta(days=1)
    print(str(dateS), str(nextDate))
    date = str(dateS)
    nextDate = str(nextDate)
    #month = date.month
    #dStr = date.strftime("%Y-%m-%d")
    #nStr = nextDate.strftime("%Y-%m-%d")
    #print(dStr)
    #return month, dStr



28-Feb
True
28-Feb-2024
2024-02-28 2024-02-29


In [34]:
url = "https://www.alphavantage.co/query?function=TIME_SERIES_DAILY_ADJUSTED&symbol=NIO&apikey=8NBLCOTKI465W93V"
r = requests.get(url)
output = r.json()

#curr = output.get("Time Series (Daily)").get('2021-04-30').get("5. adjusted close")
#prev = output.get("Time Series (Daily)").get('2021-04-29').get("5. adjusted close")
if(output):
    curr = output.get("Time Series (Daily)").get(nextDate).get("5. adjusted close")
    prev = output.get("Time Series (Daily)").get(date).get("5. adjusted close")
    print(curr, prev)
    diff = float(curr) - float(prev)
    print(diff)
    if (diff > 0):
        print("UP")
    elif (diff < 0):
        print(" - DN" + " (" + curr + ")")
    else:
        print("NC")

AttributeError: 'NoneType' object has no attribute 'get'

In [35]:
from datetime import datetime
from datetime import timedelta
import dateutil

def is_earningReport(title, earningDate, newsDate):
    #print(earningDate, newsDate)
    temp = earningDate
    if newsDate != temp:
        temp = temp + timedelta(days=1)
        if newsDate != temp:
            temp = earningDate
            temp = temp + timedelta(days=-1)
            if newsDate != temp:
                return False
    
    words1 = ["Announces", "Delivered", "Reports", "Releases", "Increase", "Raises", "Subscribers", "Update", "Performance"]
    words2 = ["Earnings", "Provides", "Results", "Billable", "Revenue", "Revenues", "Financials", "Income", "Letter", "Profitability", "Diluted EPS"]
    if any(word.upper() in title.upper() for word in words1) and any(word.upper() in title.upper() for word in words2):
        #print(True)
        return True
    return False

In [36]:
def get_newsMarketTime(hour):
    if (hour > 12):
        return "AH"
    else:
        return "PM"

In [37]:
def get_newsDate(l):
    #print(l)
    interval = l.split(" ")
    num = interval[0]
    dateStr = datetime.now()
    newsDate = None
    #print(dateStr)
    if num == "yesterday":
        newsDate = dateStr + timedelta(days=-1)
        newsDate = newsDate + timedelta(hours=-12.30) #For US time
    elif interval[1] == "days":
        newsDate = dateStr + timedelta(days=-int(interval[0]))
        newsDate = newsDate + timedelta(hours=-12.30) #For US time
        #print(newsDate)
    elif interval[1] == "hours":
        newsDate = dateStr + timedelta(hours=-int(interval[0]))
        newsDate = newsDate + timedelta(hours=-12.30) #For US time
        #print(newsDate)
    elif interval[1] == "months":
        a_month = dateutil.relativedelta.relativedelta(months=int(interval[0]))
        newsDate = dateStr - a_month
    else:
        newsDate = dateStr
        newsDate = newsDate + timedelta(hours=-9.30) #For US Eastern time
        #print(newsDate)
    return newsDate

In [38]:
def get_cell(d):
    qtrs = get_qtrs()
    #print(qtrs)
    month = datetime.now().month
    year = datetime.now().year
    #print(month, year)
    qtr = get_qtr_range(month, qtrs)
    #print(qtr)

    months = ["0", "JAN", "FEB", "MAR", "APR", "MAY", "JUN", "JUL", "AUG", "SEP", "OCT", "NOV", "DEC"]
    #print(months[qtr[0]], months[qtr[1]])
    cell = months[qtr[0]]+"-"+months[qtr[1]]+" "+ str(year)
    
    if cell not in d:
        d[cell] = None
        d.to_csv(path, index=False)
    return cell

In [39]:
import traceback
def getElement(element, source, fromSrc):
    try:
        elem = list()
        soup = BeautifulSoup(source, "html.parser")
        
        if(element == "PREVELEM"):
            cnt = -1
            if(fromSrc == "HH"):
                for t in soup.find_all("div", class_="caas-table"):
                    cnt = cnt + 1
                    if t and t.previous_element:
                        #print("PREVIOUS ELEMENT "+str(cnt), t.previous_element)
                        #print("\n")
                        elem.append(str(t.previous_element).upper())
                    else:
                        elem.append("NONE")
                return(elem)
            else:
                for t in soup.find_all("table"):
                    cnt = cnt + 1
                    if t:
                        sib = t.previous_siblings
                        sibp = t.parent.previous_siblings
                        es = ""
                        for s in sib:
                            if(s and s.name):
                                #print(s)
                                #print(s.text)
                                es = es + " " + str(" ".join(s.strings).upper())
                                break
                        for r in sibp:
                            if(r and r.name):
                                #print(s)
                                #print(s.text)
                                es = es + " " + str(" ".join(r.strings).upper())
                                break
                        elem.append(es)
                        #print("PREVIOUS ELEMENT "+str(cnt), t.previous_element)
                        #print("\n")
                    else:
                        elem.append("NONE")
                return(elem)
    except Exception as e:
        print(e)
        print(traceback.format_exc())
        return None
    return None

In [40]:
import numpy as np
def findHeaders(table, match):
    hj = -1
    hstart = -1
    hend = -1
    #match = [str(cyr), str(pyr), str(nyr), nbr1, nbr2, nbr3]
    headers = list()
    nomatch = ["Financial Highlights"]
    
    mmatch = list()
    mmatch.append("AMOUNT (MILLIONS)")
    mmatch.append("MARGIN")
    mmatch.append("AMOUNT")
    mmatch.append("AMOUNT ($ MILLIONS)")
    mmatch.append("AMOUNT ($ BILLIONS)")
    mmatch.append("MARGIN (%)")
    
    #print("TABLE BEFORE FINDING HEADER", table)
    #print("Matching Criterions\n", match)
    
    for i in range(0,len(table)):
        for j in range(1,len(table.columns)):
            cell = table.iloc[i,j]
            #print(len(str(cell).split(" ")), cell)
            if((len(str(cell).split(" ")) < 10) and ((any(qtr.upper() in str(cell).upper() for qtr in match) and not any(qtr.upper() in str(cell).upper() for qtr in nomatch)) or (i != 0 and len(headers) > 0 and any(qtr.upper() == str(cell).upper() for qtr in mmatch)))):
                #print("HEADER CELL CENTER", i, j)
                hj = i
                k = i
                hstart = -1
                hend = -1
                metric = table.iloc[k,0]
                # Multiple Headers may present inside single table
                if(len(headers) > 0):
                    #print(metric, k)
                    #hstart = i
                    #print(cell)
                    #print("MATCHHHHHHHHHHH", match)
                    #while((str(metric) == "nan" or str(metric) == cell or not any(qtr in str(cellm) for qtr in match)) and k>=0):
                    while((str(metric) == "nan" or str(metric) == cell) and k>=0):
                        hstart = k 
                        #print("HSTART", hstart)
                        k = k - 1
                        #print(metric, k)
                        if(k>=0):
                            metric = table.iloc[k,0]
                        else:
                            break
                    #if(hstart > 0):
                    #    print("NEW HsTARTTTTT", hstart)
                # Header always start from 0 index
                else:
                    hstart = 0
                if(i+1 < len(table)):
                    k = i+1
                    hend = i
                    metric = table.iloc[k,0]
                    while((str(metric) == "nan" or "THOUSANDS" in str(metric).upper() or "MILLIONS" in str(metric).upper()) and "REVENUE" not in str(metric).upper()):
                        hend = k 
                        #print("HEND", hend)
                        k = k + 1
                        if(k < len(table)):
                            metric = table.iloc[k,0]
                        else:
                            break
                else:
                    hend = i
                #print("HEADER BOUNDARY", hstart, hend)
                if(hstart > -1 and hend > -1):
                    hstr = str(hstart) + ":" + str(hend)
                    if(hstr not in headers):
                        headers.append(hstr)
                    break
    
    for i in range(0,len(table)):
        for j in range(1,len(table.columns)):
            cell = table.iloc[i,j]
            if(table.iloc[i,0] == cell):
                #print(cell)
                table.iloc[i,j] = np.nan
    print("HEADERSSSSSSSSS", headers)            
    return headers,table

In [41]:
def dedupHeaderColumns(header, report):
    mstr = None
    mindex = -1
    lvalidx = -1
    lvalsum = -1
    mdict = dict()
    
    # Check for columns where special character like $ present, need to preserve these columns in header
    rd = report.where(report=="$")
    rd = rd.dropna(axis=1, how="all")
    #print("SPECIAL COLUMNS NEED TO BE PRESERVED")
    #print(rd.columns)
    
    for i,v in enumerate(header.columns):
        #print(i,v)
        #print(header[v].astype(str).values)
        l = " ".join((header[v].astype(str).values))
        #print(l)
        # Find out which consecutive duplicate columns need to be removed
        if not mstr:
            mstr = l
            mindex = i
        else:
            if(l == mstr):
                if(lvalsum == -1):
                    lvalsum = report[v].isna().sum()
                    lvalidx = v
                if mindex not in mdict:
                    mdict[mindex] = list()
                    if(header.columns[i-1] not in rd.columns and v not in rd.columns):
                        if(report[header.columns[i-1]].isna().sum() > lvalsum):
                            mdict[mindex].append(header.columns[i-1])
                        else:
                            mdict[mindex].append(v)
                            lvalsum = report[v].isna().sum()
                            lvalidx = v
                    elif v in rd.columns and header.columns[i-1] in rd.columns:
                        mdict[mindex].append(v)
                        lvalsum = -2
                        lvalidx = header.columns[i-1]
                    elif v in rd.columns and header.columns[i-1] not in rd.columns:
                        mdict[mindex].append(header.columns[i-1])
                        lvalsum = -2
                        lvalidx = v
                    else:
                        mdict[mindex].append(v)
                        lvalsum = -2
                        lvalidx = header.columns[i-1]
                else:
                    if(report[v].isna().sum() >= lvalsum):
                        mdict[mindex].append(v)
                    else:
                        mdict[mindex].append(lvalidx)
                        lvalsum = report[v].isna().sum()
                        lvalidx = v
            else:
                mstr = l
                mindex = i
                lvalsum = -1
                lvalidx = -1
    #print("DUPLICATE HEADER COLUMNS TO BE DELETED")
    print(mdict)
    for item in mdict:
        header = header.drop(mdict[item], axis=1)
    return header

In [42]:
tableRules = [
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["STATEMENTS OF CASH FLOWS"],
        "ACTIONS":["STMTCASHFLOW"] # Statement of Cash Flow
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["NON-GAAP FINANCIAL", "NON-GAAP OPERATING EXPENSES"],
        "ACTIONS":["ACCOUNTING"]
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["KEY FINANCIAL RESULT"],
        "ACTIONS":["HIGHLIGHT"]
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["NON-GAAP NET INCOME"],
        "ACTIONS":["ACCOUNTING"]
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["NON-GAAP GROSS PROFIT"],
        "ACTIONS":["ACCOUNTING"]
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["STATEMENTS OF INCOME"],
        "ACTIONS":["STMTOP"] # Statement of Operation/Income
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["STATEMENTS OF COMPREHENSIVE INCOME"],
        "ACTIONS":["STMTOP"] # Statement of Operation/Income
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["CONSOLIDATED STATEMENTS OF OPERATIONS"],
        "ACTIONS":["STMTOP"] # Statement of Operation/Income
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"EXACT",
        "CONDITIONS":["ASSETS"],
        "ACTIONS":["BALANCESHEET"]
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["BALANCE SHEETS"],
        "ACTIONS":["BALANCESHEET"]
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["SEGMENTED ADJUSTED GROSS MARGIN"],
        "ACTIONS":["SEGNGGM"]
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["ADJUSTED GROSS MARGIN"],
        "ACTIONS":["NGGM"]
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["SEGMENTED GROSS MARGIN"],
        "ACTIONS":["SEGGM"]
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["ADJUSTED EBITDA"],
        "ACTIONS":["NGEBITDA"]
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search table description
        "MATCH":"ANY",
        "CONDITIONS":["EARNINGS BEFORE INTEREST AND TAXES"],
        "ACTIONS":["NGEBIT"]
    },
    {
        "SOURCE":["COLUMN:FIRST"], # Search within original first column name (renamed by "METRIC")
        "MATCH":"ANY",
        "CONDITIONS":["DIVISIONAL REVENUES"],
        "ACTIONS":["REVENUECHN"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["ADJUSTED EBITDA MARGIN"],
        "ACTIONS":["HIGHLIGHT"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["TOTAL CURRENT ASSETS"],
        "ACTIONS":["BALANCESHEET"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["TOTALCURRENTASSETS"],
        "ACTIONS":["BALANCESHEET"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["CASH, CASH EQUIVALENTS, AND INVESTMENTS"],
        "ACTIONS":["BALANCESHEET"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["CASH AND CASH EQUIVALENTS"],
        "ACTIONS":["BALANCESHEET"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["FREE CASH FLOW"],
        "ACTIONS":["FCF"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["COST OF REVENUE"],
        "ACTIONS":["STMTOP"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["NET SALES"],
        "ACTIONS":["STMTOP"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["COST OF PRODUCTS SOLD"],
        "ACTIONS":["STMTOP"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["COST OF REVENUES"],
        "ACTIONS":["STMTOP"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["COST OF SALES"],
        "ACTIONS":["STMTOP"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"ANY",
        "CONDITIONS":["PER SHARE DATA"],
        "ACTIONS":["PERSHARE"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"ANY",
        "CONDITIONS":["NET INVESTMENT INCOME"],
        "ACTIONS":["STMTOP"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["COST OF GOODS SOLD"],
        "ACTIONS":["STMTOP"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["GROSS PROFIT"],
        "ACTIONS":["STMTOP"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["OPERATING ACTIVITIES"],
        "ACTIONS":["STMTCASHFLOW"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["CASH, ENDING"],
        "ACTIONS":["STMTCASHFLOW"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["CASH FLOWS FROM OPERATING ACTIVITIES"],
        "ACTIONS":["STMTCASHFLOW"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["CASH FLOWS FROM OPERATING ACTIVITIES:"],
        "ACTIONS":["STMTCASHFLOW"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["CASH FLOWS FROM OPERATING ACTIVITIES:"],
        "ACTIONS":["STMTCASHFLOW"]
    },
    {
        "SOURCE":["COLUMN:METRIC"], # Search data only from "METRIC" column
        "MATCH":"ANY",
        "CONDITIONS":["ARPU", "DELIVERIES", "MAUS", "LOSS RATIO", "GROSS WRITTEN PREMIUMS", "ACTIVE BUYERS", "ACTIVE CLIENTS", "ASSETS AT FLOATING RATES", "NUMBER OF PORTFOLIO COMPANIES", "TOTAL ORIGINATIONS", "# OF INVESTMENTS"],
        "ACTIONS":["OPMETRIC"]
    },
    {
        "SOURCE":["COLUMN:METRIC"],
        "MATCH":"EXACT",
        "CONDITIONS":["GAAP INCOME FROM OPERATIONS"],
        "ACTIONS":["ACCOUNTING"]
    },
    {
        "SOURCE":["COLUMN:ANY"], # No specific column name, search any column name
        "MATCH":"ANY", # Match any condition
        "CONDITIONS":["GUIDANCE"],
        "ACTIONS":["GUIDANCE"]
    },
    {
        "SOURCE":["DESCRIPTION:ANY"], # Search table description
        "MATCH":"ANY",
        "CONDITIONS":["GUIDANCE", "OUTLOOK"],
        "ACTIONS":["GUIDANCE"]
    },
    {
        "SOURCE":["DESCRIPTION:ANY"], # Search table description
        "MATCH":"ANY",
        "CONDITIONS":["ADJUSTED EBITDA"],
        "ACTIONS":["NGEBITDA"]
    },
    {
        "SOURCE":["DESCRIPTION:ANY"], # Search table description
        "MATCH":"ANY",
        "CONDITIONS":["CONSOLIDATED BALANCE SHEETS"],
        "ACTIONS":["BALANCESHEET"]
    },
    {
        "SOURCE":["DESCRIPTION:ANY"], # Search table description
        "MATCH":"ANY",
        "CONDITIONS":["GAAP FINANCIAL METRICS", "EARNINGS PER SHARE RECONCILE"],
        "ACTIONS":["ACCOUNTING"]
    },
    {
        "SOURCE":["DESCRIPTION:ANY"], # Search table description
        "MATCH":"EXACT",
        "CONDITIONS":["NET REVENUE"],
        "ACTIONS":["REVENUE"]
    },
    {
        "SOURCE":["DESCRIPTION:ANY"], # Search table description
        "MATCH":"EXACT",
        "CONDITIONS":["REVENUE BY CHANNEL"],
        "ACTIONS":["REVENUECHN"]
    },
    {
        "SOURCE":["DESCRIPTION:ANY"], # Search table description
        "MATCH":"EXACT",
        "CONDITIONS":["REVENUE BY FORM"],
        "ACTIONS":["REVENUEFORM"]
    },
    {
        "SOURCE":["DESCRIPTION:ANY"],
        "MATCH":"EXACT",
        "CONDITIONS":["FINANCIAL RESULTS"],
        "ACTIONS":["STMTOP"]
    },
    {
        "SOURCE":["DESCRIPTION:ANY"], # Search table description
        "MATCH":"EXACT",
        "CONDITIONS":["ADJUSTED GROSS MARGIN"],
        "ACTIONS":["NGGM"] # Non-GAAP Gross Margin
    },
    {
        "SOURCE":["DESCRIPTION:ANY"], # Search table description
        "MATCH":"ANY",
        "CONDITIONS":["OPERATING METRIC"],
        "ACTIONS":["OPMETRIC"]
    }
]
print(tableRules)

[{'SOURCE': ['COLUMN:FIRST'], 'MATCH': 'ANY', 'CONDITIONS': ['STATEMENTS OF CASH FLOWS'], 'ACTIONS': ['STMTCASHFLOW']}, {'SOURCE': ['COLUMN:FIRST'], 'MATCH': 'ANY', 'CONDITIONS': ['NON-GAAP FINANCIAL', 'NON-GAAP OPERATING EXPENSES'], 'ACTIONS': ['ACCOUNTING']}, {'SOURCE': ['COLUMN:FIRST'], 'MATCH': 'ANY', 'CONDITIONS': ['KEY FINANCIAL RESULT'], 'ACTIONS': ['HIGHLIGHT']}, {'SOURCE': ['COLUMN:FIRST'], 'MATCH': 'ANY', 'CONDITIONS': ['NON-GAAP NET INCOME'], 'ACTIONS': ['ACCOUNTING']}, {'SOURCE': ['COLUMN:FIRST'], 'MATCH': 'ANY', 'CONDITIONS': ['NON-GAAP GROSS PROFIT'], 'ACTIONS': ['ACCOUNTING']}, {'SOURCE': ['COLUMN:FIRST'], 'MATCH': 'ANY', 'CONDITIONS': ['STATEMENTS OF INCOME'], 'ACTIONS': ['STMTOP']}, {'SOURCE': ['COLUMN:FIRST'], 'MATCH': 'ANY', 'CONDITIONS': ['STATEMENTS OF COMPREHENSIVE INCOME'], 'ACTIONS': ['STMTOP']}, {'SOURCE': ['COLUMN:FIRST'], 'MATCH': 'ANY', 'CONDITIONS': ['CONSOLIDATED STATEMENTS OF OPERATIONS'], 'ACTIONS': ['STMTOP']}, {'SOURCE': ['COLUMN:FIRST'], 'MATCH': 'EXA

In [43]:
import traceback
from datetime import date
def getOneTable(tables, tableNum, tblDesc):
    if not tables:
        print("TABLES CORRUPTED")
        return None
    if(tableNum >= len(tables)):
        print("INVALID TABLE INDEX")
        return None
    try:
        
        todays_date = date.today()
        cyr = todays_date.year
        pyr = cyr - 1
        ppyr = cyr - 2
        nyr = cyr + 1
        nbr = str(nyr)[2:4]
        cbr = str(cyr)[2:4]
        nbr1 = "FY’"+nbr
        nbr2 = "FY"+nbr
        nbr3 = "’"+nbr
        cbr1 = "FY’"+cbr
        cbr2 = "FY"+cbr
        cbr3 = "’"+cbr
        cg = "FY"+cbr+"GUIDANCE"
        ng = "FY"+nbr+"GUIDANCE"
        
        hdmatch = ["FIRST QUARTER", "SECOND QUARTER", "THIRD QUARTER", "FOURTH QUARTER", "FY20", "FY21", cbr1, cbr2, cbr3, "FY19GUIDANCE", "FY20GUIDANCE", "FY21GUIDANCE", cg, ng, str(cyr), str(pyr), str(ppyr), str(nyr), nbr1, nbr2, nbr3, "2019", "2016", "2017", "2018", "FY19", "FY16", "FY17", "FY18"]
        
        mn = ["MILLIONS", "MILLION", "millions", "million"]
        bn = ["BILLIONS", "BILLION", "billions", "billion"]
        t = ["THOUSANDS", "THOUSAND", "thousands", "thousand", "$000"]
        
        stmt = tables[tableNum]
        print("ORIGINAL TABLE ", tableNum)
        print(stmt)
    
        #stmt=stmt.T.drop_duplicates().T
        # Clean first column which could be METRIC column
        stmt[stmt.columns[0]] = stmt[stmt.columns[0]].astype(str)
        stmt[stmt.columns[0]] = stmt[stmt.columns[0]].str.encode("ascii", "ignore")
        stmt[stmt.columns[0]] = stmt[stmt.columns[0]].str.decode(encoding="utf8")
        stmt[stmt.columns[0]] = stmt[stmt.columns[0]].replace("—%", np.nan)
        stmt[stmt.columns[0]] = stmt[stmt.columns[0]].replace(r'^\s*$', np.nan, regex=True)
        stmt[stmt.columns[0]] = stmt[stmt.columns[0]].replace(r'nan', np.nan)
        stmt[stmt.columns[0]] = stmt[stmt.columns[0]].replace("•", np.nan)
        
        stmt = stmt.dropna(axis=1, how="all")
        stmt = stmt.dropna(axis=0, how="all")
        columns = [i for i, x in enumerate(list(stmt.columns))]
        #print(columns)
        stmt.columns = columns
        #print("TABLE AFTER REMOVING DUPLICATE ROWS AND COLUMNS")
        #print(stmt)
    
        headers,stmt = findHeaders(stmt, hdmatch)
        #print(headers)
    
        if(len(headers) == 0):
            print("INVALID TABLE, HEADER NOT FOUND")
            return None
    
        #print("TABLE AFTER REMOVING DUPLICATES")
        #print(stmt)
    
        #Itereate through headers
        cnt = 0
        ft = dict()
        for i in list(headers):
            #print(i)
            tblName = None
            tblType = None
            cnt = cnt + 1
            hstart = int(i.split(":")[0])
            hend = int(i.split(":")[1])
            if(len(headers) > cnt):
                rend = int(headers[cnt].split(":")[0])
            else:
                rend = len(stmt)
            #print("\nHEADER START", hstart, "HEADER END", hend, "REPORT END", rend)
            header = stmt.iloc[hstart:hend+1,0:]
            #header = header.dropna(axis=1, how="all")
            report = stmt.iloc[hend+1:rend,0:]
            #report = report.dropna(axis=1, how="all")
            #print("\nHEADER "+str(cnt))
            #print(header)
            #print("\nREPORT "+str(cnt))
            #print(report)
            
            # Make sure column with valid calendar field is present in subsequent tables
            mfound = False
            if(cnt > 1):
                for i,v in enumerate(header.columns):
                    l = " ".join((header[v].astype(str).values))
                    #print("FOR CNT {}, value is {}".format(cnt, l))
                    if(any(mtch.upper() in l.upper() for mtch in hdmatch)):
                        mfound = True
                        break
                #print("CALENDER FIELD PRESENT: {}".format(mfound))
                if(not mfound):
                    fh = headers[0]
                    fhs = int(fh.split(":")[0])
                    fhe = int(fh.split(":")[1])
                    #print(fhs, fhe)
                    fhd = stmt.iloc[fhs:fhe+1,0:]
                    fhd = fhd.replace(np.nan, "APNATEC")
                    mrowidx = -1
                    #print("FHD\n", fhd)
                    for v in list(fhd.columns):
                        mrows = fhd[fhd[v].str.contains("|".join(hdmatch))]
                        if(len(mrows) > 0):
                            mrow = mrows.iloc[0]
                            mrow = mrow.replace("APNATEC", np.nan)
                            mrowidx = mrows.index[0]
                            #print("MATCH ROW:", mrowidx)
                            break
                    if(mrowidx >= 0):
                        #header = stmt.loc[mrowidx] + header
                        header.loc[len(header.index)] = stmt.loc[mrowidx]
                        #print("NEW HEADER\n", header)
            
            for col in list(report.columns):
                report[report.columns[col]] = report[report.columns[col]].astype(str)
                report[report.columns[col]] = report[report.columns[col]].replace("—%", np.nan)
                report[report.columns[col]] = report[report.columns[col]].str.encode("ascii", "ignore")
                report[report.columns[col]] = report[report.columns[col]].str.decode(encoding="utf8")
        
                report[report.columns[col]] = report[report.columns[col]].replace(r'nan', np.nan)
                report[report.columns[col]] = report[report.columns[col]].replace(r'\\u200b', np.nan)
                report[report.columns[col]] = report[report.columns[col]].replace(r'\\u00a0', np.nan)
                report[report.columns[col]] = report[report.columns[col]].replace("", np.nan)
                report[report.columns[col]] = report[report.columns[col]].replace("•", np.nan)
            
            #print(report.to_json(orient="records"))
            #print("TABLE AFTER CLEANING UP\n")
            #print(report)
            
            header = dedupHeaderColumns(header, report)
            
            #print("\nAFTER DELETING DUPLICATE COLUMN HEADER")
            #print("\nHEADER "+str(cnt))
            #print(header)
            
            if(len(header) == 0):
                print("NO HEADER FOUND")
                return None
            
            header1 = header[0]
            #print("HEADER BATCH 1")
            #print(header1)
            
            header2 = header[header.columns[1:]]
            header2 = header2.dropna(axis=1, how="all")
            
            #print("\nHEADER BATCH 2 BEFORE DROPPING BASED ON FILTERS\n")
            #print(header2)
            
            hddrop = list()
            newmatch = hdmatch + ["CHANGE", "QOQ", "YOY", "GROWTH", "MARGIN", "MILLIONS", "OUTLOOK", "GAAP QUARTERLY"]
            nomatch = ["COMPARED TO", "WAS", "GROSS", "OPERATING", "INCREASED", "DECREASED", "WERE", "HAS", "HAVE"]
            for hd in list(header2.columns):
                header2[hd] = (header2[hd]).astype(str).str.upper()
                mcount = header2[hd].str.contains("|".join(list(map(str.upper,newmatch)))).sum()
                nmcount = header2[hd].str.contains("|".join(list(map(str.upper,nomatch)))).sum()
                #print(hd, mcount, nmcount)
                if(mcount == 0 or nmcount > 0):
                    hddrop.append(hd)
            
            #print("\nINVALID HEADER")
            #print(hddrop)
            header2 = header2.drop(hddrop, axis=1)
            #print("HEADER BATCH 2\n")
            #print(header2)
            
            if(len(header2) == 0 or len(list(header2.columns)) == 0):
                print("NO HEADER FOUND AFTER DROPPING COLUMNS")
                return None
            
            header = pd.concat([header1, header2], axis=1, join='inner')
            header[header.columns[0:]] = header[header.columns[0:]].astype(str)
            #print(header)
            header[header.columns[0:]] = header[header.columns[0:]].applymap(lambda x: re.sub(r'\(\d+\)|\(\d+[a-zA-Z]\)*|\*', r'', x))
            #print("FINAL HEADER")
            #print(header)
            
            #report = report.T.drop_duplicates().T
            report = report.dropna(axis=1, how="all")
            
            #print("\nAFTER DELETING DUPLICATE ROWS")
            #print("\nREPORT "+str(cnt))
            #print(report)
            
            if(len(report) > 0):
            
                # Merge REPORT columns present with special characters - e.g. $/% etc...
                rd = report.where(report=="$")
                rd = rd.dropna(axis=1, how="all")
                #print("\nSPECIAL COLUMNS")
                #print(rd.columns)
                dropList = list()
                #print("BEFORE DROPPING COLUMNS FROM REPORT\n", report)
                #print("BEFORE DROPPING COLUMNS FROM RD\n", rd)
                for i in list(rd.columns):
                    #print(report[i])
                    report[i] = report[i].map(lambda x: "" if str(x) != "$" else x)
                    k = i + 1
                    while(k in list(rd.columns)):
                        dropList.append(k)
                        #rd.columns = list(rd.columns).remove(k)
                        k = k + 1
                    while(k not in list(report.columns) and k <= max(list(report.columns))):
                        #print(i, k, report[i], report[k])
                        k = k + 1
                    if(k <= max(list(report.columns))):
                        if(i in list(header.columns)):
                            report[i] = report[i] + report[k]
                            dropList.append(k)
                        else: # column k in headers
                            report[k] = report[i] + report[k]
                            dropList.append(i)
                #print(dropList)
                #print(report)
                report = report.drop(dropList, axis=1)
                report[report.columns[1:]] = report[report.columns[1:]].astype(str)
                #report[report.columns[1:]] = report[report.columns[1:]].applymap(lambda x: x.replace('$(','-$'))
                #report[report.columns[1:]] = report[report.columns[1:]].applymap(lambda x: x.replace('(','-'))
                #report[report.columns[1:]] = report[report.columns[1:]].applymap(lambda x: x.replace(')',''))
                report[report.columns[1:]] = report[report.columns[1:]].applymap(lambda x: x.replace(',',''))
                report[0] = report[0].str.replace(":","")
                report[0] = report[0].str.replace(r'\d+|\(\d+\)|\(\d+[a-zA-Z]\)*|\*', r'')
                report[0] = report[0].str.upper()
                #report[report.columns[1:]] = report[report.columns[1:]].astype(float)
                #print("AFTER DROPPING COLUMNS FROM REPORT")
                #print(report)
                #print("HEADER COLUMNS")
                #print(header.columns)
                
                rd = report.where(report=="%")
                rd = rd.dropna(axis=1, how="all")
                #print(rd)
                dropList = list()
                mgclmn = -1
                #print(rd.columns)
                for i in list(rd.columns):
                    #print(report[i])
                    report[i] = report[i].map(lambda x: "" if (str(x) != "%" and str(x) != "%)") else x)
                    mgclmn = i - 1
                    while(mgclmn>=0):
                        if mgclmn not in header.columns:
                            mgclmn = mgclmn - 1
                        else:
                            #print(mgclmn,i)              
                            report[mgclmn] = report[mgclmn] + report[i]
                            dropList.append(i)
                            break
                report = report.drop(dropList, axis=1)
                
                rd = report.where(report==")")
                rd = rd.dropna(axis=1, how="all")
                #print(rd)
                dropList = list()
                mgclmn = -1
                #print(rd.columns)
                for i in list(rd.columns):
                    #print(report[i])
                    report[i] = report[i].map(lambda x: "" if (str(x) != ")") else x)
                    mgclmn = i - 1
                    while(mgclmn>=0):
                        if mgclmn not in header.columns:
                            mgclmn = mgclmn - 1
                        else:
                            #print(mgclmn,i)              
                            report[mgclmn] = report[mgclmn] + report[i]
                            dropList.append(i)
                            break
                report = report.drop(dropList, axis=1)
                #print("\nREPORT AFTER MERGING SPECIAL COLUMNS")
                #print(report)
            
                hdclmn = header.columns
                rclmn = report.columns
                #print("\nHEADER COLUMNS", hdclmn)
                #print("REPORT COLUMNS", rclmn)
            
                if(len(hdclmn) == 1 and len(header) == 1):
                    #print("SINGLE COLUMN")
                    if(str(header.iloc[0,0]) == "nan"):
                        #print("INVALID HEADER CONTENT FOR SINGLE COLUMN, BAILING OUT")
                        return None
                    s = header.iloc[0,0]
                    #Remove special characters
                    s = re.sub('[^a-zA-Z0-9 \n\.]', '', s)
                    #print(s)
                    data = list()
                    data = [str(s)+"***"+str(item) for item in list(rclmn)]
                    header = pd.DataFrame(np.array([data]),columns=rclmn)
                    hdclmn = header.columns
                    #print("NEW HEADER COLUMNS", hdclmn)
            
            
                finalClmns = hdclmn.intersection(rclmn)
                #print("INTERSECTION COLUMNS",finalClmns)
                header = header[finalClmns]
                #print("FINAL HEADER")
                #print(header)
            
                hstr = list()
            
                count = -1
                for i in list(header.columns):
                    count = count + 1
                    l = header[i].astype(str).values
                    l = ' '.join(dict.fromkeys(l))
                    l = l.replace("-nan","-")
                    l = l.replace("nan-","")
                    l = l.replace("nan ","")
                    l = l.replace(" nan","")
                    l = l.replace(" nan ","")
                    l = l.strip()
                    #print(hstr)
                    if l.upper() in hstr:
                        l = l+"***"+str(count)
                    hstr.append(l.upper())
                    #print(l)
            
                tblType = hstr[0]
                #print("\nORIGINAL FIRST COLUMN NAME")
                #print(tblType)
            
                #print("\nTABLE DESCRIPTION")
                #print(tblDesc)
            
                hstr[0] = "METRIC"
                #print("\nFINAL HEADER STRING")
                #print(hstr)
                
                report = report[finalClmns]
                report.columns = hstr
                print("\nFINAL REPORT")
                print(report)
            
                #print("\nREPORT COLUMNS")
                #print(report.columns)
            else:
                # When entire report rows are detected as header of table
                #print("EMPTY REPORT, ASSIGN HEADER TO REPORT")
                #hstr = list(header.columns)
                print("HEADER FOR EMPTY ROW\n", header)
                hstr = list(header.iloc[0])
                #print(hclmn)
                hstr[0] = "METRIC"
                report = header
                hstr = map(lambda x: str(x), hstr)
                #print("HEADER COLUMNS FOR EMPTY ROW-1", hstr)
                report.columns = (hstr)
                print("\nFINAL REPORT")
                print(report)
                #report.columns[0] = "METRIC"
            
            # Select unit of the table numbers
            unit = None
            for word in (mn+bn+t):
                if((tblType and word in tblType)):
                    if word in mn:
                        unit = "M"
                        break
                    elif word in bn:
                        unit = "B"
                        break
                    elif word in t:
                        unit = "T"
                        break
            if(not unit):
                unit = "T"
                for word in (mn+bn+t):
                    if((hstr and any(word in clmn for clmn in hstr)) or (tblDesc and word in tblDesc) or report["METRIC"].str.contains(word).sum() > 0):
                        if word in mn:
                            unit = "M"
                            break
                        elif word in bn:
                            unit = "B"
                            break
                        else:
                            unit = "T"
                            break
            
            # Select table type
            for item in list(tableRules):
                source = (item["SOURCE"][0])
                stype = item["SOURCE"][0].split(":")[0]
                sval = item["SOURCE"][0].split(":")[1]
                condition = item["CONDITIONS"][0]
                match = item["MATCH"]
                action = item["ACTIONS"][0]
                #print(match, condition, sval)
                #print(condition)
                
                if(stype == "COLUMN"):
                    if(sval == "FIRST"):
                        if match == "EXACT" and tblType and tblType == condition:
                            tblName = action
                            break
                        elif match == "ANY" and tblType and any(word in tblType for word in item["CONDITIONS"]):
                            tblName = action
                            break
                    elif(sval != "ANY"):
                        if match == "EXACT" and report[sval].eq(condition).sum()> 0:
                            #print("TABLE NAME BALANCESHEET")
                            tblName = action
                            break
                        elif match == "ANY" and report[sval].str.contains("|".join(item["CONDITIONS"])).sum()> 0:
                            tblName = action
                            break
                    else:
                        if(match == "ANY" and any(s in " ".join(report.columns) for s in item["CONDITIONS"])):
                            tblName = action
                            break
                        elif(match == "EXACT" and any(s in (report.columns) for s in item["CONDITIONS"])):
                            tblName = action
                            break
                elif(stype == "DESCRIPTION"):
                    if(sval == "ANY"):
                        #print(match)
                        #print("|".join(item["CONDITIONS"]))
                        if match == "EXACT" and tblDesc and tblDesc == condition:
                            tblName = action
                            break
                        elif match == "ANY" and tblDesc and any(word in tblDesc for word in item["CONDITIONS"]):
                            tblName = action
                            break
                
            if not tblName:
                key = str(tableNum)+":"+unit+":"+"OTHER"+":"+str(cnt)
                #ft[str(tableNum)+":"+unit+":"+"OTHER"+":"+str(cnt)] = report.to_json(orient="records")
            else:
                key = str(tableNum)+":"+unit+":"+tblName+":"+str(cnt)
                #ft[str(tableNum)+":"+unit+":"+tblName+":"+str(cnt)] = report.to_json(orient="records")
            ft[key] = dict()
            ft[key]["FIRSTCOLUMN"] = tblType
            ft[key]["TABLEDESC"] = tblDesc
            ft[key]["TABLENAME"] = tblName
            ft[key]["SUBTABLE"] = cnt
            ft[key]["UNIT"] = unit
            ft[key]["TABLENUM"] = tableNum
            ft[key]["COLUMNS"] = list(report.columns)
            ft[key]["METRICS"] = report["METRIC"].values.tolist()
            ft[key]["TABLE"] = report.to_json(orient="records")
            print("TABLE {} First Column {} UNIT {}".format(tblName, tblType, unit))
            #print(ft)
        return(ft)
    except Exception as e:
        print("EXCEPTION:", e)
        print(traceback.format_exc())
        return None

In [44]:
def getPgSource(url):
    driver = webdriver.Chrome()

    driver.get(url)
    time.sleep(2)

    source = driver.page_source
    #print(driver.page_source)
    driver.close()
    return(source)

In [45]:
def getAllTables(url, src):
    allTables = dict()
    source = getPgSource(url)
    tables = None
    try:
        tables = pd.read_html(source)
    except:
        tables = None
        return None
    
    print("NUMBER OF TABLES", len(tables))
    allTables["TOTAL"] = len(tables)
    allTables["PARSESUCCESS"] = list()
    allTables["PARSEFAIL"] = list()
    
    tableDesc = getElement("PREVELEM", source, src)
    #print("ALL TABLE DESCRIPTIONS")
    #print(tableDesc)
    
    for i in range(0, len(tables)):
        tableNum = i
        print("\nFOR TABLE", tableNum)
        desc = "NONE"
        if tableDesc and tableNum < len(tableDesc):
            desc = tableDesc[tableNum]
        print("\nTABLE DESCRIPTION:", desc)

        ft = getOneTable(tables, tableNum, desc)
        #print("\n")
        #print(ft)
        if i not in allTables:
            allTables[i] = dict()
        allTables[i]["ORIGINAL"] = tables[tableNum].to_json(orient="records")
        if ft:
            allTables["PARSESUCCESS"].append(i)
            for key in ft:
                tblName = key.split(":")[2]
                #print(tblName)
                if tblName not in allTables:
                    allTables[tblName] = list()
                if "PARSE" not in allTables[i]:
                    allTables[i]["PARSE"] = list()
                if "TYPE" not in allTables[i]:
                    allTables[i]["TYPE"] = list()
                allTables[tblName].append(ft[key])
                allTables[i]["PARSE"].append(ft[key])
                allTables[i]["TYPE"].append(tblName)
        else:
            allTables["PARSEFAIL"].append(i)
        
    return (allTables)

In [41]:
import json
#url = "https://www.sec.gov/Archives/edgar/data/1477449/000155837019001185/ex-99d1.htm"
url = "https://finance.yahoo.com/news/docusign-announces-first-quarter-fiscal-200500058.html"
#org = "PLTR"
dest = "../../Summary/report/"
filename = "PLTR-REPORT-2022-02-28_14-46-18.038611.txt"
allTables = getAllTables(url, "EDGAR")
#print("\nALL TABLES")
#print(allTables)
#if(allTables):
    #print(data)
#    json_object = json.dumps(allTables, indent = 4)
#    file = dest+filename
  
    # Writing to sample.json
#    with open(file, "w") as outfile:
#        outfile.write(json_object)

NUMBER OF TABLES 14

FOR TABLE 0

TABLE DESCRIPTION:  THE COMPANY CURRENTLY EXPECTS THE FOLLOWING GUIDANCE:
ORIGINAL TABLE  0
                                                   0  \
0  Quarter ending July 31, 2022 (in millions, exc...   
1                                      Total revenue   
2                               Subscription revenue   
3                                           Billings   
4                              Non-GAAP gross margin   
5                          Non-GAAP operating margin   
6  Non-GAAP diluted weighted-average shares outst...   
7                                                NaN   

                                                   1  \
0  Quarter ending July 31, 2022 (in millions, exc...   
1                                               $600   
2                                               $583   
3                                               $599   
4                                                79%   
5                                

HEADERSSSSSSSSS ['0:2']
{}

FINAL REPORT
                                               METRIC  \
4                            GAAP SALES AND MARKETING   
5                       LESS STOCK-BASED COMPENSATION   
6   LESS AMORTIZATION OF ACQUISITION-RELATED INTAN...   
7   LESS EMPLOYER PAYROLL TAX ON EMPLOYEE STOCK TR...   
8                        NON-GAAP SALES AND MARKETING   
9   GAAP SALES AND MARKETING AS A PERCENTAGE OF RE...   
10  NON-GAAP SALES AND MARKETING AS A PERCENTAGE O...   
12                      GAAP RESEARCH AND DEVELOPMENT   
13                      LESS STOCK-BASED COMPENSATION   
14  LESS EMPLOYER PAYROLL TAX ON EMPLOYEE STOCK TR...   
15                  NON-GAAP RESEARCH AND DEVELOPMENT   
16  GAAP RESEARCH AND DEVELOPMENT AS A PERCENTAGE ...   
17  NON-GAAP RESEARCH AND DEVELOPMENT AS A PERCENT...   
19                    GAAP GENERAL AND ADMINISTRATIVE   
20                      LESS STOCK-BASED COMPENSATION   
21  LESS EMPLOYER PAYROLL TAX ON EMPLOYEE STOCK

In [46]:
def storeRefinedContent(source, url, file):
    soup = BeautifulSoup(source, 'lxml')
    title = soup.find("title")
    title = (title.text)
    with open(file, 'w', encoding = 'utf-8') as f:
        f.write("url="+url)
        f.write("\n")
        f.write(title)
        f.write(".\n")
        list_of_forms = soup.find_all('div', class_="caas-body")
        for item in (list_of_forms):
            children = item.findChildren("p", recursive=True)
            for ctag in children:
                if(len(ctag.text.strip().split(" ")) < 2):
                    continue
                ctext = (" ".join(ctag.strings))
                ctext = ctext.strip()
                ctext = ctext.replace(u'\xa0', ' ')
                ctext = ("PG*** "+ctext)
                if (ctext[len(ctext)-1]) != ".":
                    ctext = ctext + ".\n"
                else:
                    ctext = ctext + "\n"
                if("Forward-Looking Statements" in ctext or "Forward Looking Statements" in ctext):
                    break
                else:
                    f.write(ctext)

In [47]:
def getOrgFileData(org):
    orgDataPath = "../../Summary/orgData/"+org+".txt"
    file = Path(orgDataPath)
    if file.is_file():
        #print(True)
        with open(orgDataPath) as f:
            data = json.load(f)
        #print(data)
        return data
    return None

In [48]:
def getOrgAttr(orgData, attr):
    if not orgData:
        return None
    asplit = attr.split("|")
    parent = asplit[0]
    if "SOURCE" in orgData[parent]:
        src = orgData[parent]["SOURCE"]
        if src == "YH" or (parent == "ORGPROFILE" and src == "AD"):
            p = orgData
            for i in range(0, len(asplit)):
                if asplit[i] not in p:
                    return None
                p = p[asplit[i]]
            #print(p)
            return(p)
    return None

In [49]:
def getLatestReportDate(csym):
    path = "../../Summary/EDGAR/8-K/"+csym
    files = glob.glob(path+"/"+csym+"_*")   
    if(len(files) > 0):
        files.sort(reverse=True, key=os.path.getmtime)
        return(files[0].split("_")[1])
    return None

In [50]:
def refineContent(content):
    #content = "-91-90%"
    #content = "-.06 - -.01"
    mn = ["MILLIONS", "MILLION", "MN"]
    bn = ["BILLIONS", "BILLION", "BN"]
    t = ["THOUSANDS", "THOUSAND", "$000"]
    ca = content.split("to")
    #print(ca)
    if(len(ca) < 2):
        ca = content.split("-")
    #ca = content.split("-")
    #print(ca)
    first = None
    fi = None
    for i,a in enumerate(ca):
        if a and a != "":
            #print(a)
            a = a.strip()
            if not first:
                first = a
                fi = i
            if(first):
                if("%" in first and "%" not in a):
                    a = a+"% "
                    ca[i] = a
                elif("%" not in first and "%" in a):
                    first = first+"% "
                    ca[fi] = first
                    #ca[i] = " "+a
                if("$" in first and "$" not in a):
                    a = " $"+a+" "
                    ca[i] = a
                elif("$" not in first and "$" in a):
                    first = " $"+first + " "
                    ca[fi] = first
                if(any(m in first.upper() for m in mn) and not any(m in a.upper() for m in mn)):
                    print("1", first.upper(), a.upper())
                    a = a+" MN "
                    ca[i] = a
                elif(not any(m in first.upper() for m in mn) and any(m in a.upper() for m in mn)):
                    print("2", first.upper(), a.upper())
                    first = first+" MN "
                    ca[fi] = first
                elif(any(m in first.upper() for m in bn) and not any(m in a.upper() for m in bn)):
                    a = a+" BN "
                    ca[i] = a
                elif(not any(m in first.upper() for m in bn) and any(m in a.upper() for m in bn)):
                    first = first+" BN "
                    ca[fi] = first
                elif(any(m in first.upper() for m in t) and not any(m in a.upper() for m in t)):
                    a = a+" T "
                    ca[i] = a
                elif(not any(m in first.upper() for m in t) and any(m in a.upper() for m in t)):
                    first = first+" T "
                    ca[fi] = first
    if("to" in content):
        content = "to ".join(ca)
        #print("to ".join(ca))
    else:
        content = "-".join(ca)
        #print("-".join(ca))
    return(content)

In [51]:
def isBold(tag, ctext):
    listag = ["ul", "li"]
    if(tag and tag.name and tag.parent.parent):
        print("TAGGGGG", tag.name, tag.text, tag.parent.parent.name)
    if(tag.name in ["b", "strong"] and tag.parent.parent and tag.parent.parent.name in listag):
        return False
    if((tag.name in ["b", "strong"] and tag.parent.parent and tag.parent.parent.name not in listag) or (tag.name in ["b", "strong"] and tag.parent.name not in listag) or tag.parent.name in ["b", "strong"]):
        return True
    if "style" in tag.attrs:
        style = tag.attrs["style"]
        #print("TAGGGGGGGGGGG", ctext, style)
        sarr = style.split(";")
        fontFound = False
                
        for stype in sarr:
            starr = stype.split(":")
            #print(starr)
            if("font-weight" in starr):
                if(starr[1] == "normal"):
                    return False
                if(starr[1] == "bold" or (starr[1]) > str("400")):
                    if(len(ctext.split(" ")) > 1 and len(ctext.split(" ")) < 14):
                        return True
                    if(len(ctext.split(" ")) == 1 and len(ctext.strip().split(" ")[0]) > 3):
                        return True
    return False

In [52]:
def isSection(ctag, ctext):
    if not ctag:
        return False
    tag = ctag
    if tag.findParent("table"):
        return False
    #print("TAGGGG", next(tag.strings))
    if(isBold(tag, next(tag.strings))):
        return True
    tags = ctag.findChildren(recursive=True)
    tag = None
    #print("CHILDRENNNNN", len(tags), ctag.name, ctag.text, tags)
    if(len(tags) >= 1):
        #tag = tag[0]
        for tag in tags:
            if(tag.name == "u"):
                continue
            if(tag.text and tag.text.strip() != ""):
                #print("HELLLLLLLLLLLLLLLLOOOOOOOOOOOO\n")
                break
    #    print(tag[0].attrs["style"], tag.text)
        if(tag and isBold(tag, tag.text)):
            return True
        #tag = ctag
        #if(isBold(tag, ctext)):
        #    return True
        
    return False

In [53]:
def findHeaderFromTable(data):
    search = ["FY20", "2018", "2019", "2020", "2021", "2022", "FY21", "FY22"]
    headers = list()
    for item in data:
        item = item.replace(u'\xa0', ' ')
        if(any(s in item for s in search) and len(item.split(" ")) < 5):
            headers.append(item)
    return(headers)

In [54]:
def isPadLeft(item):
    if(item.name == "ul" or item.name == "li"):
        return True
    if("style" in item.attrs):
        styles = item.attrs["style"].split(";")
        #print(styles)
        for style in styles:
            if("padding-left" in style):
                return True
            if("text-indent" in style):
                val = style.split(":")[1]
                val = val.replace("%","")
                try:
                    val = float(val)
                    if(val > 0):
                        return True
                except ValueError:
                    return False
                return False
    return False

In [55]:
def isFontNormal(item):
    tags = item.findChildren(recursive=False)
    if(len(tags) > 0):
        for tag in tags:
            if(tag.text and tag.text.strip() != ""):
                if("style" in tag.attrs):
                    styles = tag.attrs["style"].split(";")
                    for style in styles:
                        if("font-weight" in style and "normal" in style):
                            return True
    return False

In [56]:
def writePara(item, txt, f, possibleTblTitle=None, allWrite=False):
    nntag = ["font", "b"]
    if not item:
        return(possibleTblTitle)
    
    pgtag = ["p", "div"]
    listag = ["ul", "li"]
    if not txt:
        if(item.name in listag):
            ctext = (" ".join(item.strings))
        else:
            ctext = ("".join(item.strings))
    else:
        ctext = txt
    ctext = ctext.replace("•","")
    ctext = ctext.replace("◦","")
    ctext = ctext.replace("\n","")
    ctext = ctext.replace(u'\xa0', ' ')
    ctext = ctext.replace(u"\u00a0", " ")
    ctext = ctext.replace(u"\uf0b7", " ")
    ctext = ctext.replace("       ", " ")
    ctext = ctext.replace("     ", " ")
    ctext = ctext.replace("    ", " ")
    ctext = ctext.replace("   ", " ")
    ctext = ctext.replace("  ", " ")
    ctext = ctext.strip()
    
    if(ctext == "" or ctext == " " or len(ctext) == 1):
        if(item.name in pgtag or len(item.findPreviousSiblings()) == 0):
            ctext = ("PG*** "+ctext)
            f.write(ctext)
        return possibleTblTitle
    if(item.name not in nntag):
        if (ctext[len(ctext)-1]) != ".":
            ctext = ctext + ".\n"
        else:
            ctext = ctext + "\n"
    else:
        ctext = ctext + " "
    #print("CTEXTTTTTTT", ctext, len(ctext))
    #print(item.name, ctext, item.findParent("div"))
    #print("DONEEEEEEEEEEE")
    #if("•" in ctext):
        #    print(ctext)
        #print(ctext)
    
    # Let ML model predict tag for paragraphs found in earning report
    sentag = getSenTag(nlp, ctext)
    if("SC" in sentag):
        ctext = ("\n"+sentag+"*** "+ctext)
    else:
        ctext = (sentag+"*** "+ctext)
    f.write(ctext)
    if("SC" in ctext or "GF" in ctext or "GQ" in ctext or "CS" in ctext):
        print(ctext)
    
    
    """
    if(item.name in pgtag or len(item.findPreviousSiblings()) == 0):
        if (isSection(item, ctext) and not isPadLeft(item) and not isFontNormal(item)):
            ctext = ("\nSC*** "+ctext)
            possibleTblTitle = None
            #print(ctext)
        else:
            ctext = ("PG*** "+ctext)
    
        if(item.name not in listag and item.parent.name not in listag):
            if("style" in item.attrs):
                styles = item.attrs["style"].split(";")
                #print(styles)
                found = False
                for style in styles:
                    if("padding-left" in style):
                        found = True
                        break
                if(not found):
                    if("SC***" not in ctext):
                        ctext = ctext.replace("PG*** ", "")
                        ctext = ("NOPAD*** "+ctext)
            else:
                if("SC***" not in ctext):
                    ctext = ctext.replace("PG*** ", "")
                    ctext = ("NOPAD*** "+ctext)
                
    if(not allWrite):
        if (item.name == "p" and not item.findParent("div")):
            #print(item.name, ctext)
            if("SC***" in ctext):
                print(ctext)
            if("NOPAD***" in ctext):
                print(ctext)
                #print(item.attrs, ctext)
            f.write(ctext)
        elif (item.name == "div" and not item.findParent("p")):
            #print(item.name, ctext)
            if("SC***" in ctext):
                print(ctext)
            if("NOPAD***" in ctext):
                print(ctext)
            #print(item.attrs, ctext)
            f.write(ctext)
    else:
        if("SC***" in ctext):
            print(ctext)
        if("NOPAD***" in ctext):
            print(ctext)
        f.write(ctext)
        
        # Adding more variants of words if pattern like " - " (i.e. non - GAAP) found for training set
        #if("\n" in ctext):
        #    sr = re.search(r'([a-z]|[A-Z])\s+-\s+([a-z]|[A-Z])',ctext)
            #print(sr)
       #     if(sr):
       #         ntext = ctext.replace(" - ", "-")
                #print(nstr)
       #         f.write(ntext)
        
       #     sr = re.search(r'([a-z]|[A-Z])-([a-z]|[A-Z])',ctext)
            #print(sr)
       #     if(sr):
       #         ntext = ctext.replace("-", " - ")
                #print(nstr)
       #         f.write(ntext)
    """
    
    return(possibleTblTitle)

In [57]:
def isFloat(string):
    string = string.replace(",","")
    try:
        float(string)
        return True
    except ValueError:
        return False
    return False

In [58]:
def writeTable(table, f, tblTitle, possibleTblTitle=None):
    tblStr = "TBLST*** "
    tblEstr = "TBLET*** "
    mn = ["MILLIONS", "MILLION"]
    bn = ["BILLIONS", "BILLION"]
    t = ["THOUSANDS", "THOUSAND", "$000"]
    titleTags = ["IN MILLION", "IN THOUSAND", "IN BILLION"]
    
    if tblTitle == "" and possibleTblTitle:
        tblTitle = possibleTblTitle
            
    tblTitle = tblStr + tblTitle
    suffix = ""
    #print(tblTitle, "\n")
    f.write("\n")
    f.write(tblTitle+" .")
    f.write("\n")
                
    table_body = table.find('tbody')
    rows = table_body.find_all('tr')
    cnt = 0
    headers = list()
    tables = dict()
    for row in rows:
        cols = row.find_all('td')
        cols = [ele.text.strip() for ele in cols if ele]
        #print(cols)
        data = ([ele for ele in cols if ele])
        ndata = list()
        adata = list()
        if(len(data) > 0):
            suffix = ""
            cnt = cnt + 1
            if(cnt == 1):
                #print("DATAAAAAAAAAA", data, cnt)
                headers = findHeaderFromTable(data)
                if(len(headers) > 0):
                    print("HEADERSSSSSSSSS", headers)
                    continue
            #print(data)
            colCnt = 0
            pitem = None
            tables = dict()
            if any(match in tblTitle.upper() for match in mn):
                suffix = "MN"
            elif any(match in tblTitle.upper() for match in bn):
                suffix = "BN"
            elif any(match in tblTitle.upper() for match in t):
                suffix = "T"
            if any(match in data[0].upper() for match in mn):
                suffix = "MN"
            elif any(match in data[0].upper() for match in bn):
                suffix = "BN"
            elif any(match in data[0].upper() for match in t):
                suffix = "T"
            for eitem in data:
                #eitem = str(eitem)
                #print(len(data))
                colCnt = colCnt + 1
                eitem = eitem.replace(u'\xa0', ' ')
                eitem = eitem.strip()
                if(colCnt == 1 and len(headers) > 0):
                    tables[eitem] = dict()
                    pitem = eitem
                    continue
                eitem = eitem.replace("–","-")
                eitem = eitem.replace("~","")
                earr = eitem.split("-")
                #print(earr, eitem)
                adata = list()
                for aitem in earr:
                    #print("AITEMMMMM",aitem)
                    aitem = aitem.strip()
                    if(aitem):
                        if(aitem[0] == "$" and len(re.findall('\d*\.?\d+', aitem)) > 0 and "PER DILUTED SHARE" not in data[0].upper() and "PER SHARE" not in data[0].upper()):
                            if("million" not in aitem and "billion" not in aitem and "thousand" not in aitem):
                                neitem = aitem.strip() + " " + suffix
                                #neitem = data[0]+ " " + neitem
                                adata.append(neitem)
                            else:
                                #eitem = data[0]+ " " + eitem
                                adata.append(aitem.strip())
                        elif((aitem.strip().isdecimal() or isFloat(aitem.strip())) and "PER DILUTED SHARE" not in data[0].upper() and "PER SHARE" not in data[0].upper()):
                            if("million" not in aitem and "billion" not in aitem and "thousand" not in aitem):
                                neitem = aitem.strip() + " " + suffix
                                #neitem = data[0]+ " " + neitem
                                adata.append(neitem)
                            else:
                                #eitem = data[0]+ " " + eitem
                                adata.append(aitem.strip())
                        elif(aitem[0] == "(" and len(aitem) > 1 and (aitem[1:].strip().isdecimal() or isFloat(aitem[1:].strip())) and "PER DILUTED SHARE" not in data[0].upper() and "PER SHARE" not in data[0].upper()):
                            if("million" not in aitem and "billion" not in aitem and "thousand" not in aitem):
                                neitem = aitem.strip() + " " + suffix
                                #neitem = data[0]+ " " + neitem
                                adata.append(neitem)
                            else:
                                #eitem = data[0]+ " " + eitem
                                adata.append(aitem.strip())
                        elif(aitem[0] == "(" and len(aitem) > 1 and aitem[len(aitem)-1] == ")" and (aitem[1:len(aitem)-1].strip().isdecimal() or isFloat(aitem[1:len(aitem)-1].strip())) and "PER DILUTED SHARE" not in data[0].upper() and "PER SHARE" not in data[0].upper()):
                            if("million" not in aitem and "billion" not in aitem and "thousand" not in aitem):
                                neitem = aitem.strip() + " " + suffix
                                #neitem = data[0]+ " " + neitem
                                adata.append(neitem)
                            else:
                                #eitem = data[0]+ " " + eitem
                                adata.append(aitem.strip())
                        elif(aitem[0:2] == "($" and len(aitem) > 2 and aitem[len(aitem)-1] == ")" and (aitem[2:len(aitem)-1].strip().isdecimal() or isFloat(aitem[2:len(aitem)-1].strip())) and "PER DILUTED SHARE" not in data[0].upper() and "PER SHARE" not in data[0].upper()):
                            if("million" not in aitem and "billion" not in aitem and "thousand" not in aitem):
                                neitem = aitem.strip() + " " + suffix
                                #neitem = data[0]+ " " + neitem
                                adata.append(neitem)
                            else:
                                #eitem = data[0]+ " " + eitem
                                adata.append(aitem.strip())
                        else:
                            #eitem = data[0]+ " " + eitem
                            adata.append(aitem.strip())
                    else:
                        adata.append(aitem.strip())
                #print("ADATAAAA", adata)
                if(len(adata)>0):
                    ndata.append(" - ".join(adata))
                    #print(colCnt)
                    if(pitem and len(headers) > (colCnt-2)):
                        tables[pitem][headers[colCnt-2]] = " - ".join(adata)
                else:
                    ndata.append("".join(adata))
                    if(pitem and len(headers) > (colCnt-2)):
                        tables[pitem][headers[colCnt-2]] = "".join(adata)
        if(tables):
            #print(tables)
            for t in tables:
                for tk in tables[t]:
                    print(tk, t, tables[t][tk])
                    f.write(tk + " " + t + " " + tables[t][tk]+" .")
                    f.write("\n")
        elif(len(ndata)>0):
            #print(" ".join(ndata))
            #print("\n")
            ndata = " ".join(ndata)
            ndata = ndata.replace("\n"," ")
            ndata = ndata.replace("$ ","$")
            ndata = ndata.replace(" %","%")
            ndata = ndata.replace(" to ","  ")
            ndata = ndata.replace("Non - GAAP", "Non-GAAP")
            ndata = ndata.replace("non - GAAP", "Non-GAAP")
            print(ndata)
            f.write("PG*** "+ndata+" .")
            f.write("\n")
            #print(item.name, " ".join(ndata))
            
            #ctext = " ".join(ndata)
            #sr = re.search(r'([a-z]|[A-Z])\s+-\s+([a-z]|[A-Z])',ctext)
            #print(sr)
            #if(sr):
            #    ntext = ctext.replace(" - ", "-")
                #print(nstr)
            #    f.write(ntext)
            #f.write("\n")
            
            #sr = re.search(r'([a-z]|[A-Z])-([a-z]|[A-Z])',ctext)
            #print(sr)
            #if(sr):
            #    ntext = ctext.replace("-", " - ")
                #print(nstr)
            #    f.write(ntext)
            #f.write("\n")
            
    #print(tblEstr, "\n")
    f.write(tblEstr+" .")
    f.write("\n")
    return possibleTblTitle

In [59]:
def getPossibleMonths(qtrs):
    emonth = list()
    qtrStr = dict()
    qtrStr["Q1"] = ["FIRST"]
    qtrStr["Q2"] = ["SECOND"]
    qtrStr["Q3"] = ["THIRD"]
    qtrStr["Q4"] = ["FOURTH"]
    
    em = qtrs[qtrs["EQTR"]]["EM"]
    en = (qtrs[qtrs["EQTR"]]["END"])
    emfull = str(calendar.month_name[en]).upper()
    #emn = int(en)
    if(en == 12):
        emn = 1 #Next Month
    else:
        emn = int(en) + 1
    emnfull = str(calendar.month_name[emn]).upper()

    gm = qtrs[qtrs["GQTR"]]["EM"]
    gn = (qtrs[qtrs["GQTR"]]["END"])
    gmfull = str(calendar.month_name[gn]).upper()

    emonth.append("FULL YEAR")
    emonth.append("YEAR ENDING")
    emonth.append("FULL-YEAR")
    emonth.append("FULL FISCAL")
    emonth.append("FISCAL")
    emonth.append(qtrs["GQTR"])
    emonth.append(qtrs["EQTR"])
    emonth.append(em)
    emonth.append(emfull)
    emonth.append(emnfull)
    emonth.append(str(en)+"/")
    emonth.append("/"+str(en))
    emonth.append(gm)
    emonth.append(gmfull)
    emonth.append(str(gn)+"/")
    emonth.append("/"+str(gn))
    emonth.append("GUIDANCE")
    emonth.append("FY")
    emonth = emonth + qtrStr[qtrs["EQTR"]]
    emonth = emonth + qtrStr[qtrs["GQTR"]]
    
    return emonth

In [60]:
def getPossibleYears(qtrs):
    eyr = list()
    
    eyr.append(qtrs["EFYR"])
    eyr.append("FY"+qtrs["EFYR"][2:4])
    eyr.append("FY"+qtrs["EFYR"][2:4]+"GUIDANCE")
    eyr.append(qtrs["GFYR"])
    eyr.append("FY"+qtrs["GFYR"][2:4])
    eyr.append("FY"+qtrs["GFYR"][2:4]+"GUIDANCE")
    eyr.append(qtrs["EYR"])
    eyr.append("FY"+qtrs["EYR"][2:4])
    eyr.append("FY"+qtrs["EYR"][2:4]+"GUIDANCE")
    eyr.append("QUARTER")
    
    return eyr

In [61]:
def writePandasTable(csym, edate, ptable, unit, f):
    tblStr = "TBLST*** "
    tblEstr = "TBLET*** "
    nocheck = ["SIX", "NINE", "PRIOR"]
    
    mn = ["MILLIONS", "MILLION", "millions", "million"]
    bn = ["BILLIONS", "BILLION", "billions", "billion"]
    t = ["THOUSANDS", "THOUSAND", "thousands", "thousand", "$000"]
    replc = ["NON-GAAP", "NON GAAP", "GAAP"]
    
    un = mn + bn + t
    
    orgData = getOrgFileData(csym)
    val = None
    if orgData:
        val = getOrgAttr(orgData, "ORGPROFILE|FiscalYearEnd")
    else:
        orgProfile = getOrgProfile(csym)
        #print(orgProfile)
        if(orgProfile and "Symbol" in orgProfile):
            val = orgProfile["FiscalYearEnd"]
    if(val):
        dobj = datetime.strptime(val, "%B")
        fynd = (dobj.month)
        qtrs = getQtrsFrmRpt(csym, edate, fynd)

        emonth = getPossibleMonths(qtrs)
        print("POSSIBLE EARNING MONTH STR", emonth)

        eyr = getPossibleYears(qtrs)
        #eyr = eyr + emonth
        print("POSSIBLE EARNING YEAR STR", eyr)
    else:
        return
            
    pdt = (pd.read_json(ptable))
    for col in pdt.columns.values:
        if(col != "METRIC"):
            newcol = re.sub(r'\*\*\*\d+', "", col)
            if(not any(month in newcol for month in emonth) or not any(yr in newcol for yr in eyr) or any(chk in newcol for chk in nocheck)):
                print("DROPPING COLUMN ", newcol)
                pdt = pdt.drop(col, axis=1)
    print(pdt)
    rowCnt = 0
    header = None
    hc = False #Header continue to next row
    dollarCol = list()
    f.write("\n")
    f.write(tblStr+" .")
    f.write("\n")
    for met in (pdt["METRIC"]):
        if not met:
            rowCnt = rowCnt + 1
            header = None
            hc = False
            continue
        nanCnt = 0
        met = string.capwords(met.lower())
        if("Non-gaap" in met):
            met = met.replace("Non-gaap", "Non-GAAP")
        if("Gaap" in met):
            met = met.replace("Gaap", "GAAP")
        for col in pdt.columns.values:
            if(col != "METRIC"):
                newcol = col.replace("NAN ", "")
                newcol = newcol.replace("\\u00a0", " ")
                newcol = newcol.replace("\u00a0", " ")
                newcol = newcol.replace("\xa0", " ")
                newcol = newcol.strip()
                newcol = re.sub(r'\*\*\*\d+', "", newcol)
                for i, rp in enumerate(replc):
                    if(rp in newcol):
                        newcol = newcol.replace(rp, "")
                        newcol = rp + " " + newcol
                        if(rp == "NON-GAAP" or rp == "NON GAAP"):
                            newcol = newcol.replace(rp, "Non-GAAP")
                            break
                newcol = string.capwords(newcol.lower())
                if("Non-gaap" in newcol):
                    newcol = newcol.replace("Non-gaap", "Non-GAAP")
                if("Gaap" in newcol):
                    newcol = newcol.replace("Gaap", "GAAP")
                content = str(pdt.loc[rowCnt, col])
                if(content and content != "nan" and content != ""):
                    content = str(pdt.loc[rowCnt, col])
                    if "MARGIN" in newcol.upper() and "%" not in content:
                        content = content + "%"
                    content = content.replace("~","")
                    content = content.replace("--"," -")
                    content = content.replace("%-","% - ")
                    cd = re.search(r'\d-\d', content)
                    if (cd):
                        content = content.replace("-"," - ")
                    cd = re.search(r'\d-\$\d', content)
                    if(cd):
                        content = content.replace("-"," - ")
                    cd = re.search(r'\d\)-\(\d', content)
                    if(cd):
                        content = content.replace("-"," - ")
                    cd = re.search(r'\d\)-\$\(\d', content)
                    if(cd):
                        content = content.replace("-"," - ")
                    cd = re.search(r'\)-\(', content)
                    if(cd):
                        content = content.replace("-"," - ")
                    content = refineContent(content)
                    if(col not in dollarCol and "$" in str(pdt.loc[rowCnt, col])):
                        dollarCol.append(col)
                    if("%" not in content and "%" not in met and "PER COMMON SHARE" not in met.upper() and "EPS" not in met.upper() and "PER DILUTED SHARE" not in met.upper() and "PER SHARE" not in met.upper() and len(re.findall('\d*\.?\d+', content)) > 0):
                        if(any(u.upper() in content.upper() for u in un)):
                            unit = ""
                        if(col in dollarCol and "$" not in content and "SHARES OUTSTANDING" not in met):
                            content = "$" + content + " " + unit
                            content = content.replace("$-","-$")
                            if(header):
                                towrite = header + " " + met + " in " + newcol + " is " + content
                            else:
                                towrite = met + " in " + newcol + " is " + content
                            f.write(towrite + " .")
                            f.write("\n")
                            print(newcol, header, met, "$"+str(pdt.loc[rowCnt, col])+unit)
                        else:
                            content = content + " " + unit
                            if(header):
                                towrite = header + " " + met + " in " + newcol + " is " + content
                            else:
                                towrite = met + " in " + newcol + " is " + content
                            f.write(towrite + " .")
                            f.write("\n")
                            print(newcol, header, met, str(pdt.loc[rowCnt, col])+unit)
                    else:
                        if(col in dollarCol and "$" not in content and ("PER DILUTED SHARE" in met.upper() or "PER COMMON SHARE" in met.upper() or "PER SHARE" in met.upper() or "EPS" in met.upper())):
                            if(len(re.findall('\d*\.?\d+', content)) > 0):
                                content = "$" + content
                                content = content.replace("$-","-$")
                            if(header):
                                towrite = header + " " + met + " in " + newcol + " is " + content
                            else:
                                towrite = met + " in " + newcol + " is " + content
                            f.write(towrite + " .")
                            f.write("\n")
                            print(newcol, header, met, "$"+str(pdt.loc[rowCnt, col]))
                        else:
                            if("%" in met and "%" not in content):
                                content = content+"%"
                            if(header):
                                towrite = header + " " + met + " in " + newcol + " is " + content
                            else:
                                towrite = met + " in " + newcol + " is " + content
                            f.write(towrite + " .")
                            f.write("\n")
                            print(newcol, header, met, str(pdt.loc[rowCnt, col]))
                else:
                    nanCnt = nanCnt + 1
        if(nanCnt == (len(pdt.columns.values)-1)):
            if not header:
                header = met
                hc = True
            else:
                if hc:
                    header = header + " " + met
                else:
                    header = met
        elif(met == "TOTAL"):
            header = None
        else:
            hc = False
        rowCnt = rowCnt + 1
    print(dollarCol)
    f.write(tblEstr+" .")
    f.write("\n")

In [62]:
def testTag(tag, csym, edate, f, title, allTables):
    brkStr = ["WEBCAST INFORMATION:", "WEBCAST INFORMATION", "FORWARD-LOOKING STATEMENTS:", "QUARTERLY CONFERENCE CALL", "CONFERENCE CALL DETAILS", "FORWARD-LOOKING STATEMENTS", "FORWARD LOOKING STATEMENTS", "CONFERENCE CALL INFORMATION", "FORWARD-LOOKING INFORMATION"]
    ntag = ["div", "p", "br", "li"]
    tblTitle = ""
    global tblCnt
    if(tag and tag.name):
        if(tag.name == "table"):
            table_body = tag.find('tbody')
            #print("TBODYYYYYYYY", table_body)
            if table_body:
                print("TABLEEEEEEEEEEE", tblCnt)
                if(allTables and tblCnt in allTables["PARSESUCCESS"]):
                    print("TABLE {} PARSED SUCCESSFULLY".format(tblCnt))
                    for pidx, val in enumerate(allTables[tblCnt]["PARSE"]):
                        ptableName = (allTables[tblCnt]["PARSE"][pidx]["TABLENAME"])
                        #if(ptableName == "STMTOP" or ptableName == "STMTCASHFLOW" or ptableName == "BALANCESHEET"):
                        if(ptableName == "STMTCASHFLOW" or ptableName == "BALANCESHEET"):
                            return False
                        ptable = (allTables[tblCnt]["PARSE"][pidx]["TABLE"])
                        ptable = ptable.replace('\\u200b', "")
                        ptable = ptable.replace('\\u00a0', " ")
                        #print(ptable)
                        unit = (allTables[tblCnt]["PARSE"][pidx]["UNIT"])
                        if(unit == "M"):
                            unit = "MN"
                        elif(unit == "B"):
                            unit = "BN"
                        print("WRITING PANDAS TABLE ", tblCnt)
                        writePandasTable(csym, edate, ptable, unit, f)
                else:
                    print("WRITING REGULAR TABLE ", tblCnt)
                    writeTable(tag, f, tblTitle, title)
                f.write("\n")
                tblCnt = tblCnt + 1
                print("TABLEEEE CNTTTTT", tblCnt)
        elif(tag.name == "ul" and len(tag.findChildren("li", recursive=True)) == 0):
            if(any(bitem in tag.text.upper() for bitem in brkStr) and len(tag.text.strip().split(" ")) < 6):
                return False
            writePara(tag, None, f, title, True)
        elif(tag.name == "li" and len(tag.findChildren("li", recursive=True)) == 0):
            f.write("\n")
            if(any(bitem in tag.text.upper() for bitem in brkStr) and len(tag.text.strip().split(" ")) < 6):
                return False
            writePara(tag, None, f, title, True)
        elif(tag.name == "p" and len(tag.findChildren("table", recursive=True)) == 0):
            f.write("\n")
            if(any(bitem in tag.text.upper() for bitem in brkStr) and len(tag.text.strip().split(" ")) < 6):
                return False
            writePara(tag, None, f, title, True)
        elif(tag.name == "div" and len(tag.findChildren(["table", "p"], recursive=True)) == 0):
            f.write("\n")
            if(any(bitem in tag.text.upper() for bitem in brkStr) and len(tag.text.strip().split(" ")) < 6):
                return False
            writePara(tag, None, f, title, True)
        else:
            if(tag.name in ntag):
                f.write("\n")
            tags = tag.findChildren(recursive=False)
            if(len(tags) > 0):
                txt = tag.find(text=True, recursive=False)
                if(txt):
                    if(any(bitem in txt.upper() for bitem in brkStr) and len(txt.strip().split(" ")) < 6):
                        return False
                    writePara(tag, txt, f, title, True)
                for titem in tags:
                    if(titem.name):
                        result = testTag(titem, csym, edate, f, title, allTables)
                        if(result == False):
                            return False
                        #f.write(next(titem.strings))
                        #f.write("\n")
            else:
                #print("TEXTTT", tag.text, len(tag.text.strip().split(" ")))
                if("FORWARD‑LOOKING STATEMENTS" in tag.text.upper() and len(tag.text.strip().split(" ")) < 6):
                    return False
                if(any(bitem in tag.text.upper() for bitem in brkStr) and len(tag.text.strip().split(" ")) < 6):
                    return False
                writePara(tag, None, f, title, True)
    return True

In [63]:
def testOne8KRpt(url, csym, txtfilename, source=None, allTables=None, extraSents=None):
    if txtfilename and os.path.isfile(txtfilename):
        print("{} already exists, skipping".format(txtfilename))
        return
    
    yn = False
    if("finance.yahoo.com" in url):
        yn = True
    
    if not txtfilename:
        if(not yn):
            rptDest = "../../Summary/EDGAR/8-K/"+csym
        else:
            rptDest = "../../Summary/Refined/"+csym
        try:
            os.mkdir(rptDest) 
        except OSError as error: 
            print(error)
        txtfilename = rptDest+"/8k1.txt"
        edate = "2022-05-26"
    else:
        edate = txtfilename.split("_")[1]
        
    data = list()
    
    brkStr = ["QUARTERLY CONFERENCE CALL", "CONFERENCE CALL DETAILS", "FORWARD-LOOKING INFORMATION", "FORWARD-LOOKING STATEMENTS", "FORWARD LOOKING STATEMENTS", "CONFERENCE CALL INFORMATION"]
    tblStr = "TBLST*** "
    tblEstr = "TBLET*** "
    tblTitle = None
    #searchTags = ["font","p", "div", "b"]
    searchTags = ["p", "div", "ul", "text"]
    mn = ["MILLIONS", "MILLION"]
    bn = ["BILLIONS", "BILLION"]
    t = ["THOUSANDS", "THOUSAND", "$000"]
    titleTags = ["IN MILLION", "IN THOUSAND", "IN BILLION"]
    possibleTblTitle = None
    global tblCnt
    tblCnt = 0

    if not source:
        source = getPgSource(url)
    soup = BeautifulSoup(source, 'lxml')
    if(yn): # Yahoo News
        list_of_forms = soup.find_all(searchTags, class_="caas-body")
    else:
        list_of_forms = soup.find_all(searchTags)
    #print(len(list_of_forms))
    #list_of_forms = soup.parent()
    with open(txtfilename, 'w', encoding = 'utf-8') as f:
    #if(True):
        f.write(url)
        f.write("\n")
        
        #Write essential metrics retrieved from ER tables in refined content file
        if(extraSents and len(extraSents) > 0):
            for sent in extraSents:
                if(sent):
                    sent = sent + " @@@"
                    f.write(sent)
                    f.write("\n")
            
        for item in (list_of_forms):
            #print(item.text)
            #print(item.name)
            if(any(bitem in item.text.upper() for bitem in brkStr) and len(item.text.strip().split(" ")) < 10):
                #print(item.text)
                return
            if(len(item.text.strip().split(" ")) == 1 and len(item.text.strip().split(" ")[0]) < 3):
                tables = len(item.findChildren("table", recursive=True))
                if(tables > 0):
                    tblCnt = tblCnt + 1
                continue
            if(any(ttagitem in item.text.upper() for ttagitem in titleTags) and len(item.text.strip().split(" ")) < 15):
                possibleTblTitle = item.text.strip()
                #print(possibleTblTitle)
            #print(item.text)
            if item.name and not yn:
                #if(item.findParent("div") or item.findParent("p")):
                if(item.findParent(searchTags)):
                    continue
            #print(item.text)
            result = testTag(item, csym, edate, f, possibleTblTitle, allTables)
            #print("TABLE COUNTTTTTTT", tblCnt)
            if not result:
                return

In [76]:
#url ="https://www.sec.gov/Archives/edgar/data/1261333/000126133319000003/q419ex-991er.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1261333/000126133319000105/q320ex-991er.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1585521/000156459019021917/zm-ex991_6.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1585521/000158552121000292/zm-20211031ex991.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1713683/000171368320000028/zs-01312020991.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1535527/000155837019006148/ex-99d1.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1477449/000155837021013611/tdoc-20211027xex99d1.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1671933/000115752319000414/a51943983_ex991.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1671933/000115752321001026/a52473492ex99_1.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1640147/000164014720000020/fy2021q3earnings.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1477333/000119312522034540/d243920dex991.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1261333/000126133322000031/q422ex-991er.htm"
url = "https://investor.docusign.com/investors/press-releases/press-release-details/2023/DocuSign-Announces-Second-Quarter-Fiscal-2024-Financial-Results-Announces-Increase-to-Share-Repurchase-Program/default.aspx"
source = getPgSource(url)

In [77]:
allTables = getAllTables(url, "EDGAR")

NUMBER OF TABLES 15

FOR TABLE 0

TABLE DESCRIPTION:  THE COMPANY CURRENTLY EXPECTS THE FOLLOWING GUIDANCE:
ORIGINAL TABLE  0
                                                   0  \
0  • Quarter ending October 31, 2023 (in millions...   
1                                      Total revenue   
2                               Subscription revenue   
3                                           Billings   
4                              Non-GAAP gross margin   
5                          Non-GAAP operating margin   
6  Non-GAAP diluted weighted-average shares outst...   

                                                   1  \
0  • Quarter ending October 31, 2023 (in millions...   
1                                               $687   
2                                               $669   
3                                               $668   
4                                               81 %   
5                                               22 %   
6                                


FINAL REPORT
                                            METRIC NAN JULY 31, 2023  \
3                                           ASSETS               nan   
4                                   CURRENT ASSETS               nan   
5                        CASH AND CASH EQUIVALENTS         $ 1017778   
6                               INVESTMENTSCURRENT            426271   
7                         ACCOUNTS RECEIVABLE, NET            414740   
8                           CONTRACT ASSETSCURRENT             16188   
9        PREPAID EXPENSES AND OTHER CURRENT ASSETS             81492   
10                            TOTAL CURRENT ASSETS           1956469   
11                           INVESTMENTSNONCURRENT             85202   
12                     PROPERTY AND EQUIPMENT, NET            220916   
13             OPERATING LEASE RIGHT-OF-USE ASSETS            131341   
14                                        GOODWILL            353345   
15                          INTANGIBLE ASSETS, NET

{}

FINAL REPORT
                                               METRIC  \
4                            GAAP SALES AND MARKETING   
5                       LESS STOCK-BASED COMPENSATION   
6   LESS AMORTIZATION OF ACQUISITION-RELATED INTAN...   
7   LESS EMPLOYER PAYROLL TAX ON EMPLOYEE STOCK TR...   
8   LESS LEASE-RELATED IMPAIRMENT AND LEASE-RELATE...   
9                        NON-GAAP SALES AND MARKETING   
10  GAAP SALES AND MARKETING AS A PERCENTAGE OF RE...   
11  NON-GAAP SALES AND MARKETING AS A PERCENTAGE O...   
13                      GAAP RESEARCH AND DEVELOPMENT   
14                      LESS STOCK-BASED COMPENSATION   
15  LESS EMPLOYER PAYROLL TAX ON EMPLOYEE STOCK TR...   
16  LESS LEASE-RELATED IMPAIRMENT AND LEASE-RELATE...   
17                  NON-GAAP RESEARCH AND DEVELOPMENT   
18  GAAP RESEARCH AND DEVELOPMENT AS A PERCENTAGE ...   
19  NON-GAAP RESEARCH AND DEVELOPMENT AS A PERCENT...   
21                    GAAP GENERAL AND ADMINISTRATIVE   
22            

{}

FINAL REPORT
                                      METRIC  \
4  NET CASH PROVIDED BY OPERATING ACTIVITIES   
5   LESS PURCHASES OF PROPERTY AND EQUIPMENT   
6                    NON-GAAP FREE CASH FLOW   
7      NET CASH USED IN INVESTING ACTIVITIES   
8      NET CASH USED IN FINANCING ACTIVITIES   

  NAN THREE MONTHS ENDED JULY 31, 2023 NAN THREE MONTHS ENDED JULY 31, 2022  \
4                             $ 211016                             $ 120879   
5                              (27379)                              (15404)   
6                             $ 183637                             $ 105475   
7                            $ (64723)                            $ (83338)   
8                            $ (69347)                            $ (35453)   

  NAN SIX MONTHS ENDED JULY 31, 2023 NAN SIX MONTHS ENDED JULY 31, 2022  
4                           $ 444651                           $ 317165  
5                            (46436)                            (37113)

In [78]:
allTables

{'TOTAL': 15,
 'PARSESUCCESS': [2, 3, 4, 6, 7, 8, 9, 10, 11],
 'PARSEFAIL': [0, 1, 5, 12, 13, 14],
 0: {'ORIGINAL': '[{"0":" Quarter ending October 31, 2023 (in millions, except percentages):","1":"\\u2022 Quarter ending October 31, 2023 (in millions, except percentages):","2":"\\u2022 Quarter ending October 31, 2023 (in millions, except percentages):","3":"\\u2022 Quarter ending October 31, 2023 (in millions, except percentages):"},{"0":"Total revenue","1":"$687","2":"to","3":"$691"},{"0":"Subscription revenue","1":"$669","2":"to","3":"$673"},{"0":"Billings","1":"$668","2":"to","3":"$678"},{"0":"Non-GAAP gross margin","1":"81\\u00a0%","2":"to","3":"82\\u00a0%"},{"0":"Non-GAAP operating margin","1":"22\\u00a0%","2":"to","3":"23\\u00a0%"},{"0":"Non-GAAP diluted weighted-average shares outstanding","1":"207","2":"to","3":"212"}]'},
 1: {'ORIGINAL': '[{"0":" Year ending January 31, 2024 (in millions, except percentages):","1":"\\u2022 Year ending January 31, 2024 (in millions, except perc

In [79]:
csym = "DOCU"
#rptDest = "../../Summary/EDGAR/8-K/"+csym
#rptDest = "../../Summary/Refined/"+csym
#textFilename = rptDest+"/PATH_2021-12-08_EP.txt"
#textFilename = rptDest+"/8k1.txt"
#testOne8KRpt(url, csym, textFilename, source, allTables)
testOne8KRpt(url, csym, None, source, allTables)

[WinError 183] Cannot create a file when that file already exists: '../../Summary/EDGAR/8-K/DOCU'

SCG*** Financial Information.


SCBQ*** Financial Reports.


SCHQ*** FAQs.


SCBQ*** Press Releases.


SCBQ*** Press Release Details.

GQ*** September 07, 2023.

PG*** SAN FRANCISCO, Sept. 7, 2023 /PRNewswire/ -- DocuSign, Inc. (NASDAQ: DOCU), which offers the world's #1 e-signature product as part of its industry leading lineup, today announced results for its fiscal quarter ended July 31, 2023.

CS*** "Our results for the first half were solid and reflect strong progress on our business transformation," said Allan Thygesen, CEO of DocuSign. "We increased our pace of innovation by delivering key new features, while strengthening our self-service and partner distribution channels, and we've received tremendous enthusiasm on our product roadmap, particularly from our enterprise customers.".


SCHQ*** Second Quarter Financial Highlights.


SCBQ*** Operational and Other Financial Highlights:

In [64]:
def execFormula(formula):
    #code = ast.parse("print((10-12)-(12))")  
    code = ast.parse(formula)
    f = StringIO()
    with redirect_stdout(f):
        exec(compile(code, filename="", mode="exec"))
    val = (f.getvalue())
    val = float(val)
    val = round(val, 2)
    return(val)

In [65]:
mtable = [
    {
        "TABLE":"STMTOP",
        "ALIAS":"REVENUE",
        "DESC":"REVENUE",
        "VAR":"*GR",
        "ARGS":None,
        "SMETRIC":"NET REVENUES||TOTAL REVENUES||TOTAL REVENUE||TOTAL NET SALES||REVENUES||REVENUE||NET SALES",
        "MTYPE":"MONEY",
        "HOW":"EXACT",
        "VTYPE":"INTERNAL",
        "FORMULA":None
    },
    {
        "TABLE":"STMTOP",
        "ALIAS":"TOTAL COST OF REVENUE",
        "DESC":"TOTAL COST OF REVENUE",
        "VAR":"*GTCR",
        "ARGS":None,
        "SMETRIC":"TOTAL COST OF REVENUE||TOTAL COST OF REVENUES||COST OF REVENUES||TOTAL COST OF SALES||COST OF SALES||COST OF PRODUCTS SOLD||COST OF REVENUE||COST OF GOODS SOLD||COST OF REVENUE (EXCLUSIVE OF DEPRECIATION AND AMORTIZATION, WHICH IS SHOWN SEPARATELY BELOW)||COST OF PRODUCT REVENUE",
        "MTYPE":"MONEY",
        "HOW":"EXACT",
        "VTYPE":"INTERNAL",
        "FORMULA":None
    },
    {
        "TABLE":"STMTCASHFLOW",
        "ALIAS":"OPERATING CASH FLOW",
        "DESC":"OPERATING CASH FLOW",
        "VAR":"*GOCF",
        "ARGS":None,
        "SMETRIC":"CASH PROVIDED BY OPERATING ACTIVITIES||CASH GENERATED BY OPERATING ACTIVITIES||NET CASH (USED IN) PROVIDED BY OPERATING ACTIVITIES||NET CASH PROVIDED BY (USED IN) OPERATING ACTIVITIES||NET CASH PROVIDED BY OPERATING ACTIVITIES||NET CASH USED IN OPERATING ACTIVITIES",
        "MTYPE":"MONEY",
        "HOW":"EXACT",
        "VTYPE":"INTERNAL",
        "FORMULA":None
    },
    {
        "TABLE":"STMTCASHFLOW",
        "ALIAS":"CAPITAL EXPENDITURE",
        "DESC":"CAPITAL EXPENDITURE",
        "VAR":"*GCE",
        "ARGS":None,
        "SMETRIC":"CAPITAL EXPENDITURES||ACQUISITION OF PROPERTY AND EQUIPMENT||PURCHASES OF PROPERTY AND EQUIPMENT AND INTANGIBLE ASSETS||PAYMENTS FOR ACQUISITION OF PROPERTY, PLANT AND EQUIPMENT||PURCHASES OF PROPERTY, EQUIPMENT AND OTHER ASSETS||PURCHASE OF PROPERTY AND EQUIPMENT||PURCHASES OF LONG-LIVED AND INTANGIBLE ASSETS||CAPITAL EXPENDITURES - PROPERTY AND EQUIPMENT||PURCHASES OF PROPERTY AND EQUIPMENT||PURCHASES OF PROPERTY AND EQUIPMENTS||CAPITAL SPENDING||PURCHASES OF PROPERTY, PLANT, AND EQUIPMENT",
        "MTYPE":"MONEY",
        "HOW":"EXACT",
        "VTYPE":"INTERNAL",
        "FORMULA":None
    },
    {
        "TABLE":"STMTOP",
        "ALIAS":"GAAP-EPS", # Search metric for entity facts file
        "DESC":"GAAP NET INCOME PER SHARE", # Metric that goes to entity relation file
        "RAWDESC":"GAAP Net Income Per Share", # Goes to earning refined content file
        "VAR":"*GEPS",
        "ARGS":None,
        "SMETRIC":"NET LOSS PER SHARE AVAILABLE TO COMMON STOCKHOLDERSBASIC AND DILUTED||BASIC AND DILUTED NET LOSS PER SHARE||BASIC AND DILUTED||DILUTED EARNINGS PER COMMON SHARE||NET (LOSS) INCOME PER COMMON SHARE  DILUTED||NET LOSS PER SHARE ATTRIBUTABLE TO COMMON STOCKHOLDERS, DILUTED||EARNINGS PER SHARE, DILUTED||NET LOSS PER SHARE, BASIC AND DILUTED||NET LOSS PER SHARE ATTRIBUTABLE TO COMMON STOCKHOLDERS - BASIC AND DILUTED||NET LOSS PER SHARE ATTRIBUTABLE TO CLASS A AND CLASS B COMMON STOCKHOLDERS, BASIC AND DILUTED||NET LOSS PER SHARE ATTRIBUTABLE TO COMMON STOCKHOLDERS, BASIC AND DILUTED",
        "MATCH":["NET LOSS PER SHARE ATTRIBUTABLE", "NET INCOME PER SHARE ATTRIBUTABLE", "EARNINGS PER SHARE", "NET INCOME PER SHARE", "NET INCOME (LOSS) PER SHARE"],
        "MUSTMATCH":["DILUTED"],
        "MUSTNOTMATCH":["WEIGHTED AVERAGE SHARES"],
        "MTYPE":"MONEY",
        "HOW":"EXACT",
        "VTYPE":"EXTERNAL",
        "FORMULA":None
    },
    {
        "TABLE":"BALANCESHEET",
        "ALIAS":"CASH AND EQUIVALENTS",
        "DESC":"CASH AND EQUIVALENTS",
        "RAWDESC":"Cash And Cash Equivalents",
        "VAR":"*GCEQ",
        "ARGS":None,
        "SMETRIC":"CASH||CASH AND CASH EQUIVALENTS||CASH AND CASH EQUIVALENT",
        "MTYPE":"MONEY",
        "HOW":"EXACT",
        "VTYPE":"EXTERNAL",
        "FORMULA":None
    },
    {
        "TABLE":"STMTOP",
        "ALIAS":"GAAP GROSS PROFIT",
        "DESC":"GAAP GROSS PROFIT",
        "RAWDESC":"GAAP Gross Profit",
        "VAR":"*GGPT",
        "ARGS":None,
        "SMETRIC":"GROSS PROFIT",
        "MTYPE":"MONEY",
        "HOW":"EXACT",
        "VTYPE":"EXTERNAL",
        "FORMULA":None
    },
    {
        "TABLE":"STMTOP",
        "ALIAS":"GAAP GROSS PROFIT",
        "DESC":"GAAP GROSS PROFIT",
        "RAWDESC":"GAAP Gross Profit",
        "VAR":"*GGPT",
        "ARGS":["*GR", "*GTCR"],
        "SMETRIC":"GROSS PROFIT",
        "MTYPE":"MONEY",
        "HOW":"EXACT",
        "VTYPE":"EXTERNAL",
        "FORMULA":"print(*GR - *GTCR)"
    },
    {
        "TABLE":"STMTOP",
        "ALIAS":"GAAP GROSS MARGIN",
        "DESC":"GAAP GROSS MARGIN",
        "RAWDESC":"GAAP Gross Margin",
        "VAR":"*GGM",
        "ARGS":["*GR", "*GGPT"],
        "SMETRIC":"GROSS GROSS MARGIN",
        "MTYPE":"PCT",
        "HOW":"EXACT",
        "VTYPE":"EXTERNAL",
        "FORMULA":"print((*GGPT / *GR) * 100)"
    },
    {
        "TABLE":"STMTCASHFLOW",
        "ALIAS":"GAAP FREE CASH FLOW",
        "DESC":"GAAP FREE CASH FLOW",
        "RAWDESC":"GAAP Free Cash Flow",
        "VAR":"*GFCF",
        "ARGS":["*GOCF", "*GCE"],
        "SMETRIC":"GAAP FREE CASH FLOW",
        "MTYPE":"MONEY",
        "HOW":"EXACT",
        "VTYPE":"EXTERNAL",
        "FORMULA":"print(*GOCF + *GCE)"
    },
    {
        "TABLE":"STMTCASHFLOW",
        "ALIAS":"GAAP FREE CASH FLOW MARGIN",
        "DESC":"GAAP FREE CASH FLOW MARGIN",
        "RAWDESC":"GAAP Free Cash Flow Margin",
        "VAR":"*GFCFM",
        "ARGS":["*GR", "*GFCF"],
        "SMETRIC":"GAAP FREE CASH FLOW MARGIN",
        "MTYPE":"PCT",
        "HOW":"EXACT",
        "VTYPE":"EXTERNAL",
        "FORMULA":"print((*GFCF / *GR) * 100)"
    }
]
print(mtable)

[{'TABLE': 'STMTOP', 'ALIAS': 'REVENUE', 'DESC': 'REVENUE', 'VAR': '*GR', 'ARGS': None, 'SMETRIC': 'NET REVENUES||TOTAL REVENUES||TOTAL REVENUE||TOTAL NET SALES||REVENUES||REVENUE||NET SALES', 'MTYPE': 'MONEY', 'HOW': 'EXACT', 'VTYPE': 'INTERNAL', 'FORMULA': None}, {'TABLE': 'STMTOP', 'ALIAS': 'TOTAL COST OF REVENUE', 'DESC': 'TOTAL COST OF REVENUE', 'VAR': '*GTCR', 'ARGS': None, 'SMETRIC': 'TOTAL COST OF REVENUE||TOTAL COST OF REVENUES||COST OF REVENUES||TOTAL COST OF SALES||COST OF SALES||COST OF PRODUCTS SOLD||COST OF REVENUE||COST OF GOODS SOLD||COST OF REVENUE (EXCLUSIVE OF DEPRECIATION AND AMORTIZATION, WHICH IS SHOWN SEPARATELY BELOW)||COST OF PRODUCT REVENUE', 'MTYPE': 'MONEY', 'HOW': 'EXACT', 'VTYPE': 'INTERNAL', 'FORMULA': None}, {'TABLE': 'STMTCASHFLOW', 'ALIAS': 'OPERATING CASH FLOW', 'DESC': 'OPERATING CASH FLOW', 'VAR': '*GOCF', 'ARGS': None, 'SMETRIC': 'CASH PROVIDED BY OPERATING ACTIVITIES||CASH GENERATED BY OPERATING ACTIVITIES||NET CASH (USED IN) PROVIDED BY OPERATING

In [66]:
def isSectionExist(data, section):
    #print(data)
    for d in data:
        for t in d:
            if(t[1] == "SECTION" and t[0] == section):
                print(t[0])
                return True
    return False

In [67]:
def updateMet(csym, qtrs, metric, mtype, edate, content, number, rawdesc=None):
    backupDir = "../../Summary/entities/Backup"
    sent = list()
    if not qtrs:
        return(sent)
    qtr = qtrs["EQTR"]
    if(qtr == "Q1"):
        qtr = "first quarter"
    elif(qtr == "Q2"):
        qtr = "second quarter"
    elif(qtr == "Q3"):
        qtr = "third quarter"
    else:
        qtr = "fourth quarter"
    yr = qtrs["EFYR"]
    erPath = "../../Summary/entities/"+csym+"_"+edate+"_EP.json"
    erFile = Path(erPath)
    entities = None
    er = None
    
    if erFile.is_file():
        print("ER File {} found".format(erFile))
        with open(erPath, encoding="utf-8") as f:
            er = json.load(f)
    else:
        print("ER File {} not found".format(erFile))
    
    ndesc = rawdesc
    nmetric = metric
    if not er:
        # Fill up sentences if these need to be written in refined content in absense of entity relation files
        if(number < 0):
            nmetric = metric.replace("INCOME", "LOSS")
            if(rawdesc):
                ndesc = rawdesc.replace("Income", "Loss")
        if(ndesc):
            sentence = ndesc + " is " + content + " in " + qtr + " " + yr
        else:
            sentence = nmetric + " is " + content + " in " + qtr + " " + yr
        print(sentence)
        sent.append(sentence)
    else:
        updateRqd = False
        
        if(number < 0):
            nmetric = metric.replace("INCOME", "LOSS")
        
        sentence = nmetric + " is " + content + " in " + qtr + " " + yr
        print(sentence)
        #sent.append(sentence)
        #print(er["CASH AND EQUIVALENTS"])
        if nmetric not in er:
            er[nmetric] = list()
            updateRqd = True
        elif not isSectionExist(er[nmetric], "REGULAR"):
            updateRqd = True
        if(updateRqd):
            smetric = list()
            smetric.append(["-1","LINE",-1,-1])
            smetric.append(["REGULAR","SECTION",-1,-1])
            smetric.append([str(content),mtype,-1,-1])
            smetric.append([qtr,"CALENDAR",-1,-1])
            smetric.append([str(yr),"YEAR",-1,-1])
            smetric.append([sentence,"SENTENCE",-1,-1])
            er[nmetric].append(smetric)
            print(er[nmetric])
            shutil.copy2(erPath, backupDir)
            json_object = json.dumps(er, indent = 4)
  
            # Writing to sample.json
            with open(erPath, "w") as outfile:
                outfile.write(json_object)
    return sent

In [68]:
def isMetUpdateRqd(csym, metric, qtrs):
    #print(metric)
    entPath = "../../Summary/entities/"+csym+"-ENTITIES.json"
    entFile = Path(entPath)
    entities = None
    if not qtrs:
        return True
    if not entFile.is_file():
        return True
    with open(entPath, encoding="utf-8") as f:
        entity = json.load(f)
        entities = entity[csym]
    qtr = qtrs["EQTR"]+"-"+qtrs["EFYR"]
    if not entities:
        return True
    if qtr not in entities:
        return True
    #print(qtr)
    if entities and qtr in entities:
        if metric not in entities[qtr]:
            #print(entities["LATEST-QTR"])
            return True
        elif "CONFLICT" in entities[qtr][metric] and entities[qtr][metric]["CONFLICT"]:
            #print(entities["LATEST-QTR"])
            return True
    return False

In [69]:
def getMetricData(csym, tfile=None, mlist=None, updateMissing=False, forceUpdate=False):
    nocheck = ["SIX", "NINE", "PRIOR", "YEAR ENDED", "TWELVE"]
    mn = ["MILLIONS", "MILLION", "millions", "million"]
    bn = ["BILLIONS", "BILLION", "billions", "billion"]
    t = ["THOUSANDS", "THOUSAND", "thousands", "thousand", "$000"]
    replc = ["NON-GAAP", "NON GAAP", "GAAP"]

    un = mn + bn + t
    mvar = dict()
    sentences = list()
    allTables = None

    if not tfile:
        rptPath = "../../Summary/report"
        rptFiles = glob.glob(rptPath+"/"+csym+"-REPORT*")
        #tfile = None
        if(len(rptFiles) > 0):
            rptFiles.sort(reverse=True, key=os.path.getmtime)
            tfile = rptFiles[0]
    print(csym, tfile)
    if tfile:
        basefile = os.path.basename(tfile)
        filename = os.path.splitext(basefile)[0]
        fsplit = filename.split("-")
        edate = fsplit[2]+"-"+fsplit[3]+"-"+fsplit[4].split("_")[0]
        #print(edate)
        ofile = Path(tfile)
        if ofile.is_file():
            #print(True)
            with open(ofile) as f:
                allTables = json.load(f)
        orgData = getOrgFileData(csym)
        emonth = None
        eyr = None
        qtrs = None
        val = None
        
        if orgData:
            val = getOrgAttr(orgData, "ORGPROFILE|FiscalYearEnd")
        else:
            orgProfile = getOrgProfile(csym)
            #print(orgProfile)
            if(orgProfile and "Symbol" in orgProfile):
                val = orgProfile["FiscalYearEnd"]
        
        if(val):
            dobj = datetime.strptime(val, "%B")
            fynd = (dobj.month)
            qtrs = getQtrsFrmRpt(csym, edate, fynd)

            emonth = getPossibleMonths(qtrs)
            #print("POSSIBLE EARNING MONTH STR", emonth)

            eyr = getPossibleYears(qtrs)
            #eyr = eyr + emonth
            #print("POSSIBLE EARNING YEAR STR", eyr)

        for m in mtable:
            tname = m["TABLE"]
            smetric = None
            how = m["HOW"]
            var = m["VAR"]
            alias = m["ALIAS"]
            if(mlist and alias not in mlist):
                continue
            if(var in mvar and mvar[var]):
                #Metric Value Already Obtiained
                print(csym, alias, mvar[var])
                continue
            mtype = m["MTYPE"]
            desc = m["DESC"]
            vtype = "INTERNAL"
            if "VTYPE" in m:
                vtype = m["VTYPE"]
            match = None
            mustmatch = None
            mustnotmatch = None
            rawdesc = None
            if "RAWDESC" in m:
                rawdesc = m["RAWDESC"]
            if "MUSTMATCH" in m:
                mustmatch = m["MUSTMATCH"]
            if "MUSTNOTMATCH" in m:
                mustnotmatch = m["MUSTNOTMATCH"]
            if "MATCH" in m:
                match = m["MATCH"]
            if("SMETRIC" in m and m["SMETRIC"]):
                smetric = m["SMETRIC"]
                smetric = smetric.split("||")
            #print(smetric)
            #print(match)
            nfound = False
            
            if("ARGS" in m and m["ARGS"]):
                number = None
                args = m["ARGS"]
                for a in args:
                    if a not in mvar or not mvar[a]:
                        nfound = True
                        break
                if(not nfound):
                    if "FORMULA" in m and m["FORMULA"]:
                        formula = m["FORMULA"]
                        for a in mvar:
                            if mvar[a] and a in formula:
                                formula = formula.replace(a, str(mvar[a]))
                        number = execFormula(formula)
                        if(mtype == "MONEY"):
                            content = millify(number)
                            content = "$"+content
                            content = content.replace("$-","$(")
                            if("$(" in content):
                                content = content + ")"
                        elif(mtype == "PCT"):
                            content = str(number)
                            content = content.replace("-","(")
                            if("(" in content):
                                content = content + ")"
                            content = content + "%"
                        if var not in mvar or not mvar[var]:
                            mvar[var] = number
                        #print(csym, alias, mvar[var], formula, number, content)
                        if(vtype == "EXTERNAL"):
                            if forceUpdate:
                                print(csym, edate, alias, vtype, formula, content, number, "UPDATE REQUIRED")
                                sent = updateMet(csym, qtrs, desc, mtype, edate, content, number, rawdesc)
                                if(sent and len(sent) > 0):
                                    sentences = sentences + sent
                                print(csym, edate, alias, vtype, formula, content, number, "UPDATED")        
                            elif(isMetUpdateRqd(csym, alias, qtrs)):
                                print(csym, edate, alias, vtype, formula, content, number, "UPDATE REQUIRED")
                                if(updateMissing):
                                    sent = updateMet(csym, qtrs, desc, mtype, edate, content, number, rawdesc)
                                    if(sent and len(sent) > 0):
                                        sentences = sentences + sent
                                    print(csym, edate, alias, vtype, formula, content, number, "UPDATED")
                            else:
                                print(csym, edate, alias, vtype, formula, content, number, "UPDATE NOT REQUIRED")
                        else:
                            print(csym, edate, alias, vtype, formula, content, number, "UPDATE NOT REQUIRED")
                    else:
                        number = None
                        if var not in mvar:
                            mvar[var] = number
                        print(csym, alias, mvar[var])
                else:
                    number = None
                    if var not in mvar:
                        mvar[var] = number
                    print(csym, alias, mvar[var])
                if var not in mvar:
                    mvar[var] = number
                continue
            
            if not allTables:
                return(sentences)
            found = False
            for tblNo in allTables["PARSESUCCESS"]:
                if found:
                    break
                for pidx, val in enumerate(allTables[str(tblNo)]["PARSE"]):
                    if found:
                        break
                    ptableName = (allTables[str(tblNo)]["PARSE"][pidx]["TABLENAME"])
                    #print(ptableName)
                    if(ptableName == tname):
                        metrics = (allTables[str(tblNo)]["PARSE"][pidx]["METRICS"])
                        #if searchMet in metrics:
                        #    print(True)
                        ptable = (allTables[str(tblNo)]["PARSE"][pidx]["TABLE"])
                        ptable = ptable.replace('\\u200b', "")
                        ptable = ptable.replace('\\u00a0', " ")
                        #print(ptable)
                        unit = (allTables[str(tblNo)]["PARSE"][pidx]["UNIT"])
                        if(unit == "M"):
                            unit = "MN"
                        elif(unit == "B"):
                            unit = "BN"
                        pdt = (pd.read_json(ptable))
                        for col in pdt.columns.values:
                            if(col != "METRIC"):
                                newcol = re.sub(r'\*\*\*\d+', "", col)
                                newcol = newcol.replace("ENDED", "ENDED ")
                                #print(newcol)
                                #if(not any(month in newcol for month in emonth) or not any(yr in newcol for yr in eyr) or any(chk in newcol for chk in nocheck)):
                                if(emonth and eyr):
                                    if(not any(month in newcol for month in emonth) or not any(yr in newcol for yr in eyr)):
                                        #print("DROPPING COLUMN ", newcol)
                                        pdt = pdt.drop(col, axis=1)
                        
                        for col in pdt.columns.values:
                            if(col != "METRIC"):
                                #print(col)
                                newcol = re.sub(r'\*\*\*\d+', "", col)
                                newcol = newcol.replace("ENDED", "ENDED ")
                                if(tname != "STMTCASHFLOW" and any(chk in newcol for chk in nocheck)):
                                    #print("DROPPING COLUMN ", newcol)
                                    pdt = pdt.drop(col, axis=1)
                        
                        rowCnt = 0
                        partialMatch = False
                        
                        #print(pdt["METRIC"])
                        for met in pdt["METRIC"]:
                            if not met:
                                rowCnt = rowCnt + 1
                                continue
                            #print(met)
                            met = met.strip()
                            #print("PARTIAL MATCH", partialMatch)
                            if met in (smetric) or (match and any(mch in met for mch in match)) or (partialMatch and mustmatch and any(mch in met for mch in mustmatch)):
                                #print(met, pdt.columns.values)
                                if(partialMatch):
                                    partialMatch = False
                                for col in pdt.columns.values:
                                    if(col != "METRIC"):
                                        newcol = col.replace("NAN ", "")
                                        newcol = newcol.replace("\\u00a0", " ")
                                        newcol = newcol.replace("\u00a0", " ")
                                        newcol = newcol.replace("\xa0", " ")
                                        newcol = newcol.replace("ENDED", "ENDED ")
                                        newcol = newcol.strip()
                                        newcol = re.sub(r'\*\*\*\d+', "", newcol)
                                        #print(newcol)
                                        content = str(pdt.loc[rowCnt, col]).strip()
                                        #print(met, content)
                                        if not content or content == "nan":
                                            if(match and any(mch in met for mch in match)):
                                                if(not mustnotmatch or (mustnotmatch and not any(mch in met for mch in mustnotmatch))):
                                                    #print("PARTIAL MATCH", met)
                                                    partialMatch = True
                                            break
                                        elif (match and any(mch in met for mch in match) and (mustmatch and not any(mch in met for mch in mustmatch))):
                                            partialMatch = False
                                            break
                                        if(mtype == "MONEY"):
                                            content = content.replace("%", "")
                                        partialMatch = False
                                        if("$(" in content and ")" not in content):
                                            content = content + ")"
                                        if("%" not in content and "%" not in met and "EPS" not in alias.upper() and "PER SHARE" not in met.upper() and len(re.findall('\d*\.?\d+', content)) > 0):
                                            if(any(u.upper() in content.upper() for u in un)):
                                                unit = ""
                                            if("$" not in content and "SHARES OUTSTANDING" not in met):
                                                content = "$" + content + " " + unit
                                                content = content.replace("$-","-$")
                                            else:
                                                content = content + " " + unit
                                        else:
                                            if("$" not in content and ("PER SHARE" in met.upper() or "EPS" in alias.upper())):
                                                if(len(re.findall('\d*\.?\d+', content)) > 0):
                                                    content = "$" + content
                                                    content = content.replace("$-","-$")
                                            else:
                                                if("%" in met and "%" not in content):
                                                    content = content+"%"
                                        
                                        #print("*****"+content)

                                        content = content.replace("$ ", "$")
                                        #number = content.replace("$", "")
                                        #number = number.replace("%", "")
                                        temp = re.findall('\d*\.?\d+', content)
                                        if not temp or len(temp) == 0:
                                            continue
                                        number = float(temp[0])
                                        if("(" in content):
                                        #    number = number.replace("(", "")
                                        #    number = number.replace(")", "")
                                            number = -float(number)
                                        #else:
                                        #    number = float(number)
                                        if("T" in content):
                                            number = int(number) * 10**3
                                        elif("MN" in content):
                                            number = int(number) * 10**6
                                        elif("BN" in content):
                                            number = int(number) * 10**9
                                        #print(csym, edate, alias, newcol, content, number)
                                        found = True
                                        if var not in mvar or not mvar[var]:
                                            mvar[var] = number
                                        if(vtype == "EXTERNAL"):
                                            if forceUpdate:
                                                print(csym, edate, alias, vtype, newcol, content, number, "UPDATE REQUIRED")
                                                sent = updateMet(csym, qtrs, desc, mtype, edate, content, number, rawdesc)
                                                if(sent and len(sent) > 0):
                                                    sentences = sentences + sent
                                                print(csym, edate, alias, vtype, newcol, content, number, "UPDATED")        
                                            elif(isMetUpdateRqd(csym, alias, qtrs)):
                                                print(csym, edate, alias, vtype, newcol, content, number, "UPDATE REQUIRED")
                                                if(updateMissing):
                                                    sent = updateMet(csym, qtrs, desc, mtype, edate, content, number, rawdesc)
                                                    if(sent and len(sent) > 0):
                                                        sentences = sentences + sent
                                                    print(csym, edate, alias, vtype, newcol, content, number, "UPDATED")
                                            else:
                                                print(csym, edate, alias, vtype, newcol, content, number, "UPDATE NOT REQUIRED")
                                        else:
                                            print(csym, edate, alias, vtype, newcol, content, number, "UPDATE NOT REQUIRED")
                                        break
                                if(found):
                                    break
                            if(found):
                                break
                            rowCnt = rowCnt + 1
                        if not found:
                            content = None
                            number = None
                            if var not in mvar:
                                mvar[var] = number
                            print("1", csym, alias, content, number)
        print(mvar)
        print(sentences)
    return(sentences)

In [70]:
getMetricData("DOCN", updateMissing=False)

DOCN ../../Summary/report\DOCN-REPORT-2023-08-03_12-58-52.732916.txt
DOCN 2023-08-03 REVENUE INTERNAL THREE MONTHS ENDED  JUNE 30, 2023 $169814 T 169814000 UPDATE NOT REQUIRED
DOCN 2023-08-03 TOTAL COST OF REVENUE INTERNAL THREE MONTHS ENDED  JUNE 30, 2023 $67354 T 67354000 UPDATE NOT REQUIRED
DOCN 2023-08-03 OPERATING CASH FLOW INTERNAL SIX MONTHS ENDED JUNE 30, 2023 $100376 T 100376000 UPDATE NOT REQUIRED
DOCN 2023-08-03 CAPITAL EXPENDITURE INTERNAL SIX MONTHS ENDED JUNE 30, 2023 $(46848) T -46848000 UPDATE NOT REQUIRED
1 DOCN GAAP-EPS None None
DOCN 2023-08-03 CASH AND EQUIVALENTS EXTERNAL JUNE 30,2023 $120045 T 120045000 UPDATE NOT REQUIRED
DOCN 2023-08-03 GAAP GROSS PROFIT EXTERNAL THREE MONTHS ENDED  JUNE 30, 2023 $102460 T 102460000 UPDATE NOT REQUIRED
DOCN GAAP GROSS PROFIT 102460000
DOCN 2023-08-03 GAAP GROSS MARGIN EXTERNAL print((102460000 / 169814000) * 100) 60.34% 60.34 UPDATE NOT REQUIRED
DOCN 2023-08-03 GAAP FREE CASH FLOW EXTERNAL print(100376000 + -46848000) $53.5MN 53

[]

In [480]:
entPath = "../../Summary/entities/"
files = glob.glob(entPath+"/*-ENTITIES.json")   
if(len(files) > 0):
    for file in (files):
        basefile = os.path.basename(file)
        filename = os.path.splitext(basefile)[0]
        csym = filename.split("-")[0]
        getMetricData(csym, mlist=["REVENUE", "OPERATING CASH FLOW", "CAPITAL EXPENDITURE", "GAAP FREE CASH FLOW", "GAAP FREE CASH FLOW MARGIN"], updateMissing=False)
        print("\n")

APPN ../../Summary/report\APPN-REPORT-2022-02-17_13-57-47.699180.txt
APPN 2022-02-17 REVENUE INTERNAL THREE MONTHS ENDED  DECEMBER 31, 2021 (UNAUDITED) $104988 T 104988000 UPDATE NOT REQUIRED
APPN 2022-02-17 OPERATING CASH FLOW INTERNAL YEAR ENDED  DECEMBER 31, 2021 $(53918) T -53918000 UPDATE NOT REQUIRED
APPN 2022-02-17 CAPITAL EXPENDITURE INTERNAL YEAR ENDED  DECEMBER 31, 2021 $(6058) T -6058000 UPDATE NOT REQUIRED
APPN 2022-02-17 GAAP FREE CASH FLOW EXTERNAL print(-53918000 + -6058000) $(60MN) -59976000.0 UPDATE NOT REQUIRED
APPN 2022-02-17 GAAP FREE CASH FLOW MARGIN EXTERNAL print((-59976000.0 / 104988000) * 100) (57.13)% -57.13 UPDATE NOT REQUIRED
{'*GR': 104988000, '*GOCF': -53918000, '*GCE': -6058000, '*GFCF': -59976000.0, '*GFCFM': -57.13}


BILL None


CFLT ../../Summary/report\CFLT-REPORT-2022-02-10_14-43-13.447623.txt
CFLT 2022-02-10 REVENUE INTERNAL THREE MONTHS ENDED  DECEMBER 31, 2021 $119928 T 119928000 UPDATE NOT REQUIRED
1 CFLT OPERATING CASH FLOW None None
1 CFLT CAP

ZM 2022-02-28 OPERATING CASH FLOW INTERNAL THREE MONTHS ENDED  JANUARY 31, 2022 $209396 T 209396000 UPDATE NOT REQUIRED
ZM 2022-02-28 CAPITAL EXPENDITURE INTERNAL THREE MONTHS ENDED  JANUARY 31, 2022 $(20774) T -20774000 UPDATE NOT REQUIRED
ZM 2022-02-28 GAAP FREE CASH FLOW EXTERNAL print(209396000 + -20774000) $189MN 188622000.0 UPDATE NOT REQUIRED
ZM 2022-02-28 GAAP FREE CASH FLOW MARGIN EXTERNAL print((188622000.0 / 1071376000) * 100) 17.61% 17.61 UPDATE NOT REQUIRED
{'*GR': 1071376000, '*GOCF': 209396000, '*GCE': -20774000, '*GFCF': 188622000.0, '*GFCFM': 17.61}


ZS ../../Summary/report\ZS-REPORT-2022-02-24_17-33-46.014693.txt
ZS 2022-02-24 REVENUE INTERNAL THREE MONTHS ENDED  JANUARY 31, 2022 $255563 T 255563000 UPDATE NOT REQUIRED
ZS 2022-02-24 OPERATING CASH FLOW INTERNAL SIX MONTHS ENDED  JANUARY 31, 2022 $141533 T 141533000 UPDATE NOT REQUIRED
ZS 2022-02-24 CAPITAL EXPENDITURE INTERNAL SIX MONTHS ENDED  JANUARY 31, 2022 $(20442) T -20442000 UPDATE NOT REQUIRED
ZS 2022-02-24 G

In [70]:
import time
from selenium import webdriver
from selenium.webdriver.chrome.service import Service 
#from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.chrome.options import Options
from bs4 import BeautifulSoup
import json

def store_earning_news(earningDateStr, stock):
    # Web scrapper for infinite scrolling page 
    url = "https://finance.yahoo.com/quote/" + stock + "/press-releases?p=" + stock
    
    options = webdriver.ChromeOptions()
    options.add_experimental_option('excludeSwitches', ['enable-logging'])
    driver = webdriver.Chrome(options=options)
    driver.get(url)
    time.sleep(2)  # Allow 2 seconds for the web page to open
    scroll_pause_time = 2 
    screen_height = driver.execute_script("return window.screen.height;")   # get the screen height of the web

    i = 1
   
    SCROLL_PAUSE_TIME = 0.5
    last_height = driver.execute_script("return document.body.scrollHeight")
    while True:
        driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
        time.sleep(SCROLL_PAUSE_TIME)
        new_height = driver.execute_script("return document.body.scrollHeight")
        if new_height == last_height:
            break
        last_height = new_height

    ##### Extract Article Titles #####

    earningDate = datetime.strptime(earningDateStr, '%Y-%m-%d')
    
    rfnDest = "../../Summary/Refined/"+stock
    try:
        os.mkdir(rfnDest) 
    except OSError as error: 
        print(error)
    
    news_list = list()
    soup = BeautifulSoup(driver.page_source, "html.parser")

    for t in soup.find_all(class_="Cf"):
        #print(t)
        news = dict()
        a_tag = t.find("a", class_="Fw(b)", href=True)
        #a_tag = t.find("u", class_="StretchedBox")
        if a_tag:
            #print(a_tag)
            text = a_tag.text
            news["Title"] = text
            news["Link"] = "https://finance.yahoo.com" + a_tag["href"]
            news["Provider"] = None
            news["Date"] = None
            news["Content"] = None
        
            provider = t.find("div", class_="C(#959595)")
            if provider:
                c = provider.text
                ctx = (c.encode("ascii", "replace").decode())
                l = ctx.split("?")
                news["Provider"] = l[0]
                news["Date"] = str(get_newsDate(l[1]))
            else:
                continue
        
            p_content = t.find("p", class_="Fz(14px)")
            if p_content:
                c = p_content.text
                news["Content"] = c
        
            newsDateArr = news["Date"].split(" ")
            newsDateStr = newsDateArr[0]
            newsDate = datetime.strptime(newsDateStr, '%Y-%m-%d')
            if not is_earningReport(news["Title"], earningDate, newsDate):
                continue
            else:
                news_list.append(news)
                break
    if(len(news_list) == 0):
        driver.quit()
        return False, None, None

    filename = None
    newsDateStr = None
    try:
        for news in news_list:
            print(news["Link"])
            newsDateArr = news["Date"].split(" ")
            newsTime = newsDateArr[1].replace(":", "-")
            newsDateStr = newsDateArr[0]
            #filename = stock + "-" + earningDateStr + "_" + newsTime + ".txt"
            filename = stock + "-" + newsDateStr + "_" + newsTime + ".txt"
            rptname = stock + "-" + "REPORT" + "-" + newsDateStr + "_" + newsTime + ".txt"
            rfnfname = stock + "_" + newsDateStr + "_EP_YH.txt" 
            path = "../../Summary/unsup/"+filename
            rptpath = "../../Summary/report/"+rptname
            rfnpath = rfnDest+"/"+rfnfname
            url = news["Link"]
            driver.get(url)
            time.sleep(5)
    
            soup = BeautifulSoup(driver.page_source, "html.parser")
    
            content = soup.find("div", class_="caas-body")
    
            with open(path, 'x', encoding = 'utf-8') as f:
                newStr = "url="+url
                f.write(newStr)
                f.write("\n")
                if content:
                    #text = content.text
                    text = (" ".join(content.strings))
    
                    text = re.sub(r'Forward-Looking Statements.*|Forward Looking Statements.*',"",text)
                    #print(text)
                    if "Title" in news:
                        f.write(news["Title"])
                        f.write("\n")
                    f.write(text)
                else:
                    if "Title" in news:
                        f.write(news["Title"])
                        f.write("\n")
                    f.write(news["Content"])
            
            print("TRYING TO STORE TABLES IN FILE {}".format(rptpath))
            allTables = getAllTables(url, "YH")
            if allTables:
                with open(rptpath, 'x', encoding = 'utf-8') as outfile:
                    json_object = json.dumps(allTables, indent = 4)
                    outfile.write(json_object)
                    
            print("TRYING TO PARSE METRIC DATA FROM TABLES IN FILE {}".format(rptpath))
            sentences = getMetricData(stock, tfile=rptpath, updateMissing=True)
            
            print("TRYING TO STORE REFINED CONTENT IN FILE {}".format(rfnpath))
            testOne8KRpt(url, stock, rfnpath, driver.page_source, allTables, extraSents=sentences)
            #storeRefinedContent(driver.page_source, url, rfnpath)
            
            break
    except Exception as e:
        print(e)
        print(traceback.format_exc())
        driver.quit()
        return False, None, None
                
    driver.quit()
    return True, filename, newsDateStr

In [71]:
from datetime import date
import glob
import holidays

def get_earningDate_quote(content, stock):
    #print(content,stock)
    if type(content) is not str:
        return None
    
    if content and "(" not in content:
        year = datetime.now().year
        dateStr = (content.strip() + "-" + str(year))
        #print(dateStr)
        try:
            ed = datetime.strptime(dateStr, "%d-%b-%Y").date()
        except:
            ed = datetime.strptime(dateStr, "%d %b-%Y").date()
        
        #print(str(ed))
        
        currDate = date.today()
        #print(currDate)
        
        if(ed>currDate):
            print("Earning for stock {} will be released later on {}".format(stock, str(ed)))
            return None
        
        #filename = "./unsup/EPD-2021-05-03*"
        filename = "../../Summary/unsup/" + stock + "-" + str(ed) + "*"

        names = glob.glob(filename)
        #print(len(names))
        quote = None
        if(len(names) > 0):
            print("Earning report for stock {} on date {} exists".format(stock, str(ed)))

            for name in glob.glob(filename):
                #print(name)
                nArr = name.split("_")
                hour = (int(nArr[1].split("-")[0]))
                break
        else:
            print("Earning report for stock {} on date {} does not exist, trying to fetch it".format(stock, str(ed)))
            res, name, newsDateStr = store_earning_news(str(ed), stock)
            print("Earning report for stock {} fetching status {}, filename {}".format(stock, res, name))
            if not res or not name:
                cd = currDate + timedelta(hours=-9.30)
                #print(str(cd))
                if(ed < cd):
                    month, quote = get_dateStr(str(cd))
                    print("Updating new earning date {} for stock {}".format(quote, stock))
                    return quote
                return None
            print("Earning report for stock {} on date {} fetched, filename {}".format(stock, newsDateStr, name))
            nArr = name.split("_")
            hour = (int(nArr[1].split("-")[0]))
        
            newsDate = datetime.strptime(newsDateStr, "%Y-%m-%d").date()
            #print(newsDate)
            
            if (newsDate != ed):
                ed = newsDate
                print("New Earning Date {}".format(str(ed)))
        
        month, quote = get_dateStr(str(ed))
        
        newsHour = get_newsMarketTime(hour)
        print("Earning released for stock {} {}".format(stock, newsHour))
        
        us_holidays = holidays.UnitedStates(years=year)
        if newsHour == "AH":
            nextDate = ed + timedelta(days=1)
        else:
            nextDate = ed + timedelta(days=-1)
            
        while True:
            weekno = nextDate.weekday()         
            if str(nextDate) in us_holidays:
                if newsHour == "AH":
                    nextDate = nextDate + timedelta(days=1)
                else:
                    nextDate = nextDate + timedelta(days=-1)
                continue
            elif weekno >= 5:
                if newsHour == "AH":
                    nextDate = nextDate + timedelta(days=1)
                else:
                    nextDate = nextDate + timedelta(days=-1)
                continue
            else:
                break
        
        print("Get price diff for stock {} from date {} and date {}".format(stock, str(ed), str(nextDate)))
        
        ed = str(ed)
        nextDate = str(nextDate)
        
        retry = 0
        output = None
        #quote = None
        while(retry < 2):
            try:
                #url = "https://www.alphavantage.co/query?function=TIME_SERIES_DAILY_ADJUSTED&symbol="+stock+"&apikey=8NBLCOTKI465W93V"
                url = "https://www.alphavantage.co/query?function=TIME_SERIES_DAILY&symbol="+stock+"&apikey=8NBLCOTKI465W93V"
                r = requests.get(url)
                output = r.json()
                #print(output)
                break
            except Exception as e:
                print(e)
                retry = retry + 1
                time.sleep(5)
        if not output:
            return quote
        
        curr = output.get("Time Series (Daily)")
        if curr is None:
            return quote
        curr = curr.get(nextDate)
        if curr is None:
            return quote
        curr = curr.get("4. close")
        if curr is None:
            return quote
        
        prev = output.get("Time Series (Daily)")
        if prev is None:
            return quote
        prev = prev.get(ed)
        if prev is None:
            return quote
        prev = prev.get("4. close")
        if prev is None:
            return quote
        
        #print(curr, prev)
        if not quote:
            return quote
        
        if newsHour == "AH":
            diff = float(curr) - float(prev)
        else:
            diff = float(prev) - float(curr)
        #print(diff)
        if (diff > 0):
            if newsHour == "AH":
                quote = quote + (" - UP" + " (" + curr + ")")
            else:
                quote = quote + (" - UP" + " (" + prev + ")")
        elif (diff < 0):
            if newsHour == "AH":
                quote = quote + (" - DN" + " (" + curr + ")")
            else:
                quote = quote + (" - DN" + " (" + prev + ")")
        else:
            if newsHour == "AH":
                quote = quote + (" - NC" + " (" + curr + ")")
            else:
                quote = quote + (" - DN" + " (" + prev + ")")
        #print(quote)
        return (quote)
    
    return None

In [72]:
path = "../../Summary/stocks_csv.csv"
d = pd.read_csv(path)
#print(d[cell][60], d["Ticker"][60])
quote = get_earningDate_quote(d[cell][60], d["Ticker"][60])
print(quote)

Earning for stock NNOX will be released later on 2024-03-07
None


In [73]:
import time

def update_stock_earningDate(d, path, phase=1, updateAll=True):
    RETRY_COUNT = 3
    others = ["SCHB", "SCHD", "SCHA", "SRET", "SCHK", "DGRO", "DBEU", "TD6C", "TDG0", "PTTRX"]

    retry = 0
    status = True
    #pending_stocks = []
    
    stocks = d["Ticker"]
    #print(stocks)
    if(len(stocks) == 0):
        return True
    
    cell = get_cell(d)
    if not cell:
        return True
    
    for index, stock in enumerate(stocks):
        #if(stock != "CFLT"):
        #    continue
        if(index <= 87):
            continue
        retry = 0
        earningDate = d[cell][index]
        
        if phase==2:
            if type(earningDate) is not str:
                #print("Earning date for stock {} not available".format(stock))
                continue
            if "NA*" in earningDate:
                print("Report for stock {} on earning date {} not available".format(stock, earningDate.replace(" - NA*", "")))
                continue
            quote = get_earningDate_quote(earningDate, stock)
            if quote is not None:
                print("Update Stock {} with quote {}".format(stock, quote))
                d.loc[index, cell] = (quote)
                d.to_csv(path, index=False)
            else:
                if "(" in earningDate:
                    print("Quote for stock {} on earning date {} already generated".format(stock, earningDate))
                elif "NA*" in earningDate:
                    print("Quote for stock {} on earning date {} not available".format(stock, earningDate))
                else:
                    print("Quote for stock {} on earning date {} not generated yet".format(stock, earningDate))
            continue
        
        if phase==1:
            if type(earningDate) is str and not updateAll:
                continue
                        
            if type(earningDate) is str:
                if "(" in earningDate:
                    continue
        
        if stock in others:
            #print(stock, None)
            continue
        if type(stock) is not str:
            continue
        while(retry <= RETRY_COUNT):
            content = get_stock_earningDate_detail(stock)
            if content:
                content = str(content)
                #print(content)
                f = StringIO(content)
                tbl = pd.read_csv(f, nrows=1)
                if "reportDate" in tbl and len(tbl["reportDate"]) > 0:
                    dateStr = tbl["reportDate"][0]
                    #print(stock, dateStr)
                    month, dateStr = get_dateStr(dateStr)
                    status1 = is_currentQtr(month)
                    print(stock, month, dateStr, status1)
                    if not status1:
                        #print(stock,dateStr)
                        break
                    d.loc[index, cell] = str(dateStr)
                    d.to_csv(path, index=False)
                    time.sleep(5)
                    break
                elif "reportDate" not in tbl:
                    retry = retry + 1
                    if(retry > RETRY_COUNT):
                        print(stock, None)
                        #pending_stocks.append(stock)
                        status = False
                    time.sleep(5)
                    continue
                else:
                    print(stock, None)
                    #pending_stocks.append(stock)
                    status = False
                    time.sleep(5)
                    break
    return status

In [91]:
status = False
retry = 0
path = "../../Summary/stocks_csv.csv"
d = pd.read_csv(path)

while(retry < 2):
    if retry == 0:
        status = update_stock_earningDate(d, path, 1, True)
    else:
        status = update_stock_earningDate(d, path, 1, False)
    print(status, retry)
    if(status):
        break
    else:
        retry = retry + 1

print(d[cell])

MNDY 2 12-Feb True
FIVN 2 20-Feb True
U 2 20-Feb True
S 3 14-Mar True
APPS 2 06-Feb True
OPRX 2 21-Feb True
LAZR 2 26-Feb True
PATH 3 26-Mar True
MDB 3 06-Mar True
ZI 2 05-Feb True
BILL 1 31-Jan True
DDOG 2 13-Feb True
PLUG 2 28-Feb True
LULU 3 26-Mar True
NET 2 07-Feb True
INVZ 2 28-Feb True
BILI 2 29-Feb True
IDXX 2 05-Feb True
DXCM None
FUBO 2 26-Feb True
GLBE 2 18-Feb True
IOT 2 29-Feb True
ENPH 2 05-Feb True
PANW 2 19-Feb True
AMAT 2 14-Feb True
ISRG 1 23-Jan True
False 0


ValueError: time data 'f' does not match format '%Y-%m-%d'

In [74]:
path = "../../Summary/stocks_csv.csv"
d = pd.read_csv(path)

status = update_stock_earningDate(d, path, 2)
print(status)

Earning for stock NIO will be released later on 2024-02-28
Quote for stock NIO on earning date 28-Feb not generated yet
Earning for stock ABBV will be released later on 2024-02-02
Quote for stock ABBV on earning date 02-Feb not generated yet
Earning for stock EPD will be released later on 2024-02-01
Quote for stock EPD on earning date 01-Feb not generated yet
Earning for stock ENB will be released later on 2024-02-09
Quote for stock ENB on earning date 09-Feb not generated yet
Earning for stock KNSL will be released later on 2024-02-14
Quote for stock KNSL on earning date 14-Feb not generated yet
Earning for stock NKE will be released later on 2024-03-19
Quote for stock NKE on earning date 19-Mar not generated yet
Earning for stock BMY will be released later on 2024-02-02
Quote for stock BMY on earning date 02-Feb not generated yet
Earning for stock APPN will be released later on 2024-02-14
Quote for stock APPN on earning date 14-Feb not generated yet
Earning for stock TEAM will be rel

In [74]:
def get_earningDates(d, when):
    dt = datetime.today()
    stocks = d["Ticker"]
    
    cell = get_cell(d)
    if not cell:
        return None
    
    if(when == "WK"):
        start = dt - timedelta(days=dt.weekday())
        end = start + timedelta(days=6)
    elif (when == "TD"):
        start = dt
        end = start
    elif (when == "TM"):
        start = dt + timedelta(days=1)
        end = start
    elif (when == "YT"):
        start = dt - timedelta(days=1)
        end = start
    else:
        return None

    start = datetime.date(start)
    end = datetime.date(end)
    #print(start)
    #print(end)

    year = dt.year

    result = []
    for index, stock in enumerate(stocks):
        eStr = d[cell][index]
        combo = []
        
        if type(eStr) is not str:
            continue
            
        if "NA*" in eStr:
            continue
            
        if "(" in eStr:
            eStr = eStr.split("-")
            #print(eStr)
            dateStr = (eStr[0].strip() + "-" + eStr[1].strip() + "-" + str(year))
        else:
            dateStr = (eStr.strip() + "-" + str(year))

        #print(dateStr)
        try:
            ed = datetime.strptime(dateStr, "%d-%b-%Y").date()
        except:
            ed = datetime.strptime(dateStr, "%d %b-%Y").date()
        #print(ed)

        if ed >= start and ed <= end:
            #print(stock, start, end, ed, True)
            combo.append(stock)
            combo.append(dateStr)
            result.append(combo)
            
    return result

In [75]:
stocks = get_earningDates(d, "WK")
print(stocks, "\n", len(stocks))

[['TSLA', '23-Jan-2024'], ['NOW', '23-Jan-2024'], ['ISRG', '23-Jan-2024']] 
 3


In [ ]:
import re
import time
from selenium import webdriver
from bs4 import BeautifulSoup
import spacy

#nlp = spacy.load("en_core_web_trf")

url = "https://finance.yahoo.com/news/aurora-cannabis-announces-fiscal-2021-201500266.html"
print(url)

driver = webdriver.Chrome()

driver.get(url)
time.sleep(2)

soup = BeautifulSoup(driver.page_source, "html.parser")
    
content = soup.find("div", class_="caas-body")
#print(content)

if content:
    #print(content.get_text())
    #filename = "PANW-2021-05-20_16-52-59.518356.txt"
    #path = "./unsupnew/"+filename
    output = (" ".join(content.strings))
    
    output = re.sub(r'Forward-Looking Statements.*|Forward Looking Statements.*',"",output)
    
    print(output)
    
    #with open(path, 'x', encoding = 'utf-8') as f:
    #    f.write(output)
    #soup = BeautifulSoup(content, "html.parser")
    #soup.get_text(separator="\n")
    #print(content.text)
    #doc = nlp(output)
    #sentences = [str(sent).strip() for sent in doc.sents]
    #print(len(sentences))
    #print(sentences)
    
    #for line in sentences:
    #    print("****** {}".format(line))
        
driver.quit()

In [85]:
import os
import re
import time
from selenium import webdriver
from bs4 import BeautifulSoup
import spacy

files_link = [
              "https://finance.yahoo.com/news/aurora-cannabis-announces-fiscal-2021-201500266.html",
              "https://finance.yahoo.com/news/applied-materials-announces-second-quarter-200100432.html",
              "https://finance.yahoo.com/news/arista-networks-inc-reports-first-200500732.html",
              "https://finance.yahoo.com/news/appian-announces-first-quarter-2021-200100501.html",
              "https://finance.yahoo.com/news/alibaba-group-announces-march-quarter-112200701.html",
              "https://finance.yahoo.com/news/bristol-myers-squibb-reports-first-105900221.html",
              "https://finance.yahoo.com/news/beyond-meat-reports-first-quarter-200500876.html",
              "https://finance.yahoo.com/news/casper-reports-first-quarter-2021-103000149.html",
              "https://finance.yahoo.com/news/walt-disney-company-reports-second-200500011.html",
              "https://finance.yahoo.com/news/draftkings-reports-first-quarter-2021-110000293.html",
              "https://finance.yahoo.com/news/enbridge-reports-strong-first-quarter-110000848.html",
              "https://finance.yahoo.com/news/enterprise-reports-first-quarter-2021-100000525.html",
              "https://finance.yahoo.com/news/etsy-inc-reports-first-quarter-200500590.html",
              "https://finance.yahoo.com/news/exp-world-holdings-reports-record-123000146.html",
              "https://finance.yahoo.com/news/fulgent-genetics-reports-record-first-200500258.html",
              "https://finance.yahoo.com/news/farfetch-announces-first-quarter-2021-200600856.html",
              "https://finance.yahoo.com/news/fiverr-announces-first-quarter-2021-050000648.html",
              "https://finance.yahoo.com/news/hubspot-reports-q1-2021-results-201000012.html",
              "https://finance.yahoo.com/news/havertys-reports-first-quarter-2021-204000308.html",
              "https://finance.yahoo.com/news/horizon-therapeutics-plc-reports-first-110000158.html",
              "https://finance.yahoo.com/news/innovative-industrial-properties-reports-first-200600167.html",
              "https://finance.yahoo.com/news/inmode-reports-first-quarter-2021-111500734.html",
              "https://finance.yahoo.com/news/jd-com-announces-first-quarter-105300974.html",
              "https://finance.yahoo.com/news/lemonade-announces-first-quarter-2021-210000181.html",
              "https://finance.yahoo.com/news/medifast-inc-announces-first-quarter-200500463.html",
              "https://finance.yahoo.com/news/mercadolibre-inc-reports-first-quarter-213000148.html",
              "https://finance.yahoo.com/news/magnite-reports-first-quarter-2021-200500357.html",
              "https://finance.yahoo.com/news/match-group-reports-first-quarter-201100924.html",
              "https://finance.yahoo.com/news/nanox-announces-first-quarter-2021-110000907.html",
              "https://finance.yahoo.com/news/invitae-reports-103-6-million-200500995.html",
              "https://finance.yahoo.com/news/palo-alto-networks-reports-fiscal-200500317.html",
              "https://finance.yahoo.com/news/paycom-software-inc-reports-first-200500900.html",
              "https://finance.yahoo.com/news/palantir-reports-49-revenue-growth-110000817.html",
              "https://finance.yahoo.com/news/prospect-capital-releases-march-2021-203600447.html",
              "https://finance.yahoo.com/news/paypal-reports-first-quarter-2021-201600784.html",
              "https://finance.yahoo.com/news/qorvo-announces-fiscal-2021-fourth-200000135.html",
              "https://finance.yahoo.com/news/quantumscape-announces-first-quarter-2021-201500516.html",
              "https://finance.yahoo.com/news/repligen-reports-first-quarter-2021-113000798.html",
              "https://finance.yahoo.com/news/ringcentral-announces-first-quarter-2021-200600324.html",
              "https://finance.yahoo.com/news/roku-releases-first-quarter-2021-200300047.html",
              "https://finance.yahoo.com/news/revolve-group-announces-first-quarter-200500204.html",
              "https://finance.yahoo.com/news/square-inc-announces-first-quarter-200600101.html",
              "https://finance.yahoo.com/news/trade-desk-reports-first-quarter-123000864.html",
              "https://finance.yahoo.com/news/twilio-announces-first-quarter-2021-201000982.html",
              "https://finance.yahoo.com/news/uber-announces-results-first-quarter-200500302.html",
              "https://finance.yahoo.com/news/vir-biotechnology-provides-corporate-reports-200500093.html",
              "https://finance.yahoo.com/news/walker-dunlop-reports-20-growth-100000820.html",
              "https://finance.yahoo.com/news/wix-reports-first-quarter-2021-050000836.html",
              "https://finance.yahoo.com/news/ww-announces-first-quarter-2021-200100511.html",
              "https://finance.yahoo.com/news/zynga-announces-first-quarter-2021-200500864.html",
             ]

skip_list = ["AAPL", "ABBV", "CMG", "ASML", "ISRG", "INTC", "LRCX", 
             "KNSL", "LRN", "NIO", "MSFT", "NOW", "PACB", "PINS", "SHOP", "SIVB", "SNAP", 
             "TDOC", "TEAM", "TSLA", "V", "VRTX", "PTON"]
print(len(files_link), len(skip_list))

path = "../../Summary/unsup"
newpath = "../../Summary/unsupnew/"


cnt = 0
for fname in os.listdir(path):
    #print(fname)
    nf = os.path.join(newpath, fname)
    words = fname.split("-")
    stock = words[0]
    print(stock, nf, files_link[cnt])
    driver = webdriver.Chrome()    
    
    url = files_link[cnt]
    #print(url)

    driver.get(url)
    time.sleep(3)

    soup = BeautifulSoup(driver.page_source, "html.parser")
    
    content = soup.find("div", class_="caas-body")
    
    if content:
    
        output = (" ".join(content.strings))
    
        output = re.sub(r'Forward-Looking Statements.*|Forward Looking Statements.*',"",output)
    
        #print(output)
    
        with open(nf, 'x', encoding = 'utf-8') as f:
            f.write(output)
    
    driver.quit()
    cnt = cnt + 1
    
print(cnt)

50 23
ACB ./unsupnew/ACB-2021-05-13_16-52-59.518356.txt https://finance.yahoo.com/news/aurora-cannabis-announces-fiscal-2021-201500266.html
AMAT ./unsupnew/AMAT-2021-05-20_13-28-46.962705.txt https://finance.yahoo.com/news/applied-materials-announces-second-quarter-200100432.html
ANET ./unsupnew/ANET-2021-05-04_16-29-14.279301.txt https://finance.yahoo.com/news/arista-networks-inc-reports-first-200500732.html
APPN ./unsupnew/APPN-2021-05-06_13-01-52.344079.txt https://finance.yahoo.com/news/appian-announces-first-quarter-2021-200100501.html
BABA ./unsupnew/BABA-2021-05-13_07-54-38.989614.txt https://finance.yahoo.com/news/alibaba-group-announces-march-quarter-112200701.html
BMY ./unsupnew/BMY-2021-04-29_14-18-33.950906.txt https://finance.yahoo.com/news/bristol-myers-squibb-reports-first-105900221.html
BYND ./unsupnew/BYND-2021-05-06_13-06-00.598192.txt https://finance.yahoo.com/news/beyond-meat-reports-first-quarter-200500876.html
CSPR ./unsupnew/CSPR-2021-05-13_07-52-27.895874.txt ht

In [49]:
import pandas as pd
import os
import re
import time
from selenium import webdriver

#url = (
#    "https://raw.githubusercontent.com/pandas-dev/pandas/master/"
#    "pandas/tests/io/data/html/spam.html"
#)

#url = "https://finance.yahoo.com/quote/SFIX/analysis?p=SFIX"
#url = "https://finance.yahoo.com/quote/SFIX/profile?p=SFIX"
#url = "https://finance.yahoo.com/quote/PINS/holders?p=PINS"
url = "https://finance.yahoo.com/quote/PINS/insider-roster?p=PINS"
#url = "https://finance.yahoo.com/quote/SFIX/key-statistics?p=SFIX"

driver = webdriver.Chrome()

driver.get(url)
time.sleep(2)

source = driver.page_source
#print(driver.page_source)
driver.close()
#Executive_pay
#profile = pd.read_html(url)
#profile

In [76]:
profile = pd.read_html(source)
#print(len(profile), profile)
print(profile[0], profile[0].columns[0], profile[0].iloc[0,0], profile[0].iloc[1,0])
#print(profile[0],"\n")
#print(profile[0].loc[1])
#df = profile[0].loc[1]
#print(df, type(df), type(profile))
#print(df.loc["Current Qtr. (Sep 2021)"])
#print(profile[1].iloc[1,0], profile[1].columns[1], profile[1].iloc[1,1], profile[1].iloc[1,2], profile[1].iloc[1,3])
#print(df.loc["Current Qtr. *"])
#print(df["Avg. Estimate"])

NameError: name 'source' is not defined

In [76]:
DataExtract = [
    {
        "SOURCE":
        {
            "URL":"https://finance.yahoo.com/quote/*ORG/profile?p=*ORG"
        },
        "TABLE":
        {
            "NAME":"PROFILE",
            "TYPE":"SERIES"
        },
        "TUPLES":[
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":0
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":-1,
                            "COLUMN":-1,
                            "MATCH":None,
                            "ALIAS":"EXECS"
                        }
                    }
                ]
            }
        ]
    },
    {
        "SOURCE":
        {
            "URL":"https://finance.yahoo.com/quote/*ORG/insider-transactions?p=*ORG"
        },
        "TABLE":
        {
            "NAME":"INSIDERTRANS",
            "TYPE":"SERIES"
        },
        "TUPLES":[
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":0
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":-1,
                            "COLUMN":-1,
                            "MATCH":None,
                            "ALIAS":"TRANSSTAT"
                        }
                    }
                ]
            }
        ]
    },
    {
        "SOURCE":
        {
            "URL":"https://finance.yahoo.com/quote/*ORG/insider-roster?p=*ORG"
        },
        "TABLE":
        {
            "NAME":"MAJORTRANS",
            "TYPE":"SERIES"
        },
        "TUPLES":[
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":0
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":-1,
                            "COLUMN":-1,
                            "MATCH":None,
                            "ALIAS":"ROSTERS"
                        }
                    }
                ]
            }
        ]
    },
    {
        "SOURCE":
        {
            "URL":"https://finance.yahoo.com/quote/*ORG/holders?p=*ORG"
        },
        "TABLE":
        {
            "NAME":"HOLDERS",
            "TYPE":"SERIES"
        },
        "TUPLES":[
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":1
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":-1,
                            "COLUMN":-1,
                            "MATCH":None,
                            "ALIAS":"INST"
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":0
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":0,
                            "COLUMN":1,
                            "MATCH":"SHARES HELD BY ALL INSIDER",
                            "ALIAS":"INSIDERHELDPCT",
                            "VALUE":
                            {
                                "ROW":0,
                                "COLUMN":0
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":0
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":1,
                            "COLUMN":1,
                            "MATCH":"SHARES HELD BY INSTITUTIONS",
                            "ALIAS":"INSTHELDPCT",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":0
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":0
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":2,
                            "COLUMN":1,
                            "MATCH":"FLOAT HELD BY INSTITUTIONS",
                            "ALIAS":"INSTHELDFLTPCT",
                            "VALUE":
                            {
                                "ROW":2,
                                "COLUMN":0
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":0
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":3,
                            "COLUMN":1,
                            "MATCH":"NUMBER OF INSTITUTIONS",
                            "ALIAS":"INSTNUM",
                            "VALUE":
                            {
                                "ROW":3,
                                "COLUMN":0
                            }
                        }
                    }
                ]
            }
        ]
    },
    {
        "SOURCE":
        {
            "URL":"https://finance.yahoo.com/quote/*ORG/analysis?p=*ORG"
        },
        "TABLE":
        {
            "NAME":"ANALYSIS",
            "TYPE":"FRAME"
        },
        "TUPLES":[
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":2
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":1,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"EPS-ACT-HIST",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":2
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":2,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"EPS-ACT-HIST",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":2
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":2
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":3,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"EPS-ACT-HIST",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":3
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":2
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":4,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"EPS-ACT-HIST",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":4
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":2
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":1,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"EPS-EST-HIST",
                            "VALUE":
                            {
                                "ROW":0,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":2
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":2,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"EPS-EST-HIST",
                            "VALUE":
                            {
                                "ROW":0,
                                "COLUMN":2
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":2
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":3,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"EPS-EST-HIST",
                            "VALUE":
                            {
                                "ROW":0,
                                "COLUMN":3
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":2
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":4,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"EPS-EST-HIST",
                            "VALUE":
                            {
                                "ROW":0,
                                "COLUMN":4
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":1
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":1,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"REVENUE-EST",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":1
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":2,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"REVENUE-EST",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":2
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":1
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":3,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"REVENUE-EST",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":3
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":1
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":4,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"REVENUE-EST",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":4
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":0
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":1,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"EPS-EST",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":0
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":2,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"EPS-EST",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":2
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":0
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":3,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"EPS-EST",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":3
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":0
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "COLUMN":4,
                            "MATCH":None,
                            "ALIAS":None,
                            "NAME":"EPS-EST",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":4
                            }
                        }
                    }
                ]
            }
        ]
    },
    {      
        "SOURCE":
        {
            "URL":"https://finance.yahoo.com/quote/*ORG/key-statistics?p=*ORG"
        },
        "TABLE":
        {
            "NAME":"STATS",
            "TYPE":"SERIES"
        },
        "TUPLES":[
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":9
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":1,
                            "COLUMN":0,
                            "MATCH":"LEVERED FREE CASH FLOW",
                            "ALIAS":"FCF",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":8
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":0,
                            "COLUMN":0,
                            "MATCH":"TOTAL CASH",
                            "ALIAS":"CASH",
                            "VALUE":
                            {
                                "ROW":0,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":8
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":1,
                            "COLUMN":0,
                            "MATCH":"TOTAL CASH PER SHARE",
                            "ALIAS":"CASHPERSHARE",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":8
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":2,
                            "COLUMN":0,
                            "MATCH":"TOTAL DEBT",
                            "ALIAS":"DEBT",
                            "VALUE":
                            {
                                "ROW":2,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":8
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":4,
                            "COLUMN":0,
                            "MATCH":"CURRENT RATIO",
                            "ALIAS":"CURRATIO",
                            "VALUE":
                            {
                                "ROW":4,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":6
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":0,
                            "COLUMN":0,
                            "MATCH":"RETURN ON ASSETS",
                            "ALIAS":"ROA",
                            "VALUE":
                            {
                                "ROW":0,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":6
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":1,
                            "COLUMN":0,
                            "MATCH":"RETURN ON EQUITY",
                            "ALIAS":"ROE",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":4
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":0,
                            "COLUMN":0,
                            "MATCH":"FISCAL YEAR ENDS",
                            "ALIAS":"FISCALYEND",
                            "VALUE":
                            {
                                "ROW":0,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":4
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":1,
                            "COLUMN":0,
                            "MATCH":"MOST RECENT QUARTER",
                            "ALIAS":"MRQ",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":3
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":1,
                            "COLUMN":0,
                            "MATCH":"FORWARD ANNUAL DIVIDEND YIELD",
                            "ALIAS":"FDIVYLD",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":3
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":3,
                            "COLUMN":0,
                            "MATCH":"TRAILING ANNUAL DIVIDEND YIELD",
                            "ALIAS":"TDIVYLD",
                            "VALUE":
                            {
                                "ROW":3,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":3
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":5,
                            "COLUMN":0,
                            "MATCH":"PAYOUT RATIO",
                            "ALIAS":"PAYOUTRATIO",
                            "VALUE":
                            {
                                "ROW":5,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":3
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":6,
                            "COLUMN":0,
                            "MATCH":"DIVIDEND DATE",
                            "ALIAS":"DIVDATE",
                            "VALUE":
                            {
                                "ROW":6,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":3
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":7,
                            "COLUMN":0,
                            "MATCH":"EX-DIVIDEND DATE",
                            "ALIAS":"EXDIVDATE",
                            "VALUE":
                            {
                                "ROW":7,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":0
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":0,
                            "COLUMN":0,
                            "MATCH":"MARKET CAP",
                            "ALIAS":"MCAP",
                            "VALUE":
                            {
                                "ROW":0,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":0
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":5,
                            "COLUMN":0,
                            "MATCH":"PRICE/SALES",
                            "ALIAS":"PS",
                            "VALUE":
                            {
                                "ROW":5,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":1
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":5,
                            "COLUMN":0,
                            "MATCH":"50-DAY MOVING AVERAGE",
                            "ALIAS":"50DMA",
                            "VALUE":
                            {
                                "ROW":5,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":1
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":6,
                            "COLUMN":0,
                            "MATCH":"200-DAY MOVING AVERAGE",
                            "ALIAS":"200DMA",
                            "VALUE":
                            {
                                "ROW":6,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":2
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":0,
                            "COLUMN":0,
                            "MATCH":"AVG VOL (3 MONTH)",
                            "ALIAS":"AVGVOL3MONTH",
                            "VALUE":
                            {
                                "ROW":0,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":2
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":1,
                            "COLUMN":0,
                            "MATCH":"AVG VOL (10 DAY)",
                            "ALIAS":"AVGVOL10DAY",
                            "VALUE":
                            {
                                "ROW":1,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":2
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":9,
                            "COLUMN":0,
                            "MATCH":"SHORT % OF FLOAT",
                            "ALIAS":"SHORTPCTFLOAT",
                            "VALUE":
                            {
                                "ROW":9,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            },
            {
                "CONDITIONS":[
                    {
                        "TABLENUM":2
                    }
                ],
                "ACTIONS":[
                    {
                        "KEY":
                        {
                            "ROW":10,
                            "COLUMN":0,
                            "MATCH":"SHORT % OF SHARES OUTSTANDING",
                            "ALIAS":"SHORTPCTOUST",
                            "VALUE":
                            {
                                "ROW":10,
                                "COLUMN":1
                            }
                        }
                    }
                ]
            }
        ]
    }
]
print(DataExtract)

[{'SOURCE': {'URL': 'https://finance.yahoo.com/quote/*ORG/profile?p=*ORG'}, 'TABLE': {'NAME': 'PROFILE', 'TYPE': 'SERIES'}, 'TUPLES': [{'CONDITIONS': [{'TABLENUM': 0}], 'ACTIONS': [{'KEY': {'ROW': -1, 'COLUMN': -1, 'MATCH': None, 'ALIAS': 'EXECS'}}]}]}, {'SOURCE': {'URL': 'https://finance.yahoo.com/quote/*ORG/insider-transactions?p=*ORG'}, 'TABLE': {'NAME': 'INSIDERTRANS', 'TYPE': 'SERIES'}, 'TUPLES': [{'CONDITIONS': [{'TABLENUM': 0}], 'ACTIONS': [{'KEY': {'ROW': -1, 'COLUMN': -1, 'MATCH': None, 'ALIAS': 'TRANSSTAT'}}]}]}, {'SOURCE': {'URL': 'https://finance.yahoo.com/quote/*ORG/insider-roster?p=*ORG'}, 'TABLE': {'NAME': 'MAJORTRANS', 'TYPE': 'SERIES'}, 'TUPLES': [{'CONDITIONS': [{'TABLENUM': 0}], 'ACTIONS': [{'KEY': {'ROW': -1, 'COLUMN': -1, 'MATCH': None, 'ALIAS': 'ROSTERS'}}]}]}, {'SOURCE': {'URL': 'https://finance.yahoo.com/quote/*ORG/holders?p=*ORG'}, 'TABLE': {'NAME': 'HOLDERS', 'TYPE': 'SERIES'}, 'TUPLES': [{'CONDITIONS': [{'TABLENUM': 1}], 'ACTIONS': [{'KEY': {'ROW': -1, 'COLUM

In [77]:
import pandas as pd
import os
import re
import time
from selenium import webdriver

def GetTables(url):
    driver = webdriver.Chrome()

    driver.get(url)
    time.sleep(2)

    source = driver.page_source
    try:
        table = pd.read_html(source)
    except:
        return None
    #print(driver.page_source)
    driver.close()
    return table

In [78]:
def getOrgData(org):
    data = dict()
    orgProfile = getOrgProfile(org)
    if (not orgProfile):
        return None
    if("Symbol" not in orgProfile):
        print("INVALID PROFILE DATA, BAILING OUT")
        return None
    data["ORGPROFILE"] = orgProfile
    data["ORGPROFILE"]["SOURCE"] = "AD" #Alphaadvantage API
    today = date.today()
    tstr = today.strftime("%B %d, %Y")
    data["LASTUPDATE"] = tstr
    for idx,rule in enumerate(DataExtract):
        #print(rule["SOURCE"]["URL"])
        url = rule["SOURCE"]["URL"]
        url = url.replace("*ORG", org)
        print(url)
        table = GetTables(url)
        if not table:
            continue
        #print(table)
        tableName = rule["TABLE"]["NAME"]
        tableType = rule["TABLE"]["TYPE"]
        print("TABLE NAME", tableName)
        data[tableName] = dict()
        if ("yahoo" in url):
            data[tableName]["SOURCE"] = "YH"
        #print(rule["TUPLES"])
        for tidx,tple in enumerate(rule["TUPLES"]):
            #print(tple)
            found = False
            for cidx,cnd in enumerate(tple["CONDITIONS"]):
                #print(cnd)
                if "TABLENUM" in cnd:
                    print("Table Number", cnd["TABLENUM"])
                    tableNum = cnd["TABLENUM"]
                    if len(table) >= tableNum:
                        found = True
                        print("FOUND")
                    break
            if(found):
                for aidx,act in enumerate(tple["ACTIONS"]):
                    #print(act)
                    if "KEY" in act:
                        if tableType == "SERIES":
                            rowKey = act["KEY"]["ROW"]
                            columnKey = act["KEY"]["COLUMN"]
                            matchRegex = act["KEY"]["MATCH"]
                            alias = act["KEY"]["ALIAS"]
                    
                            if(rowKey == -1 and columnKey == -1 and alias):
                                data[tableName][alias] = table[tableNum].to_json(orient="records")
                            else:
                                key = table[tableNum].iloc[rowKey,columnKey]
                                if(not matchRegex or (matchRegex and matchRegex in key.upper())):
                                    valueRow = act["KEY"]["VALUE"]["ROW"]
                                    valueColumn = act["KEY"]["VALUE"]["COLUMN"]
                                    value = table[tableNum].iloc[valueRow,valueColumn]
                                    print(rowKey, columnKey, key.upper(), valueRow, valueColumn, value)
                                    data[tableName][alias] = value
                        elif tableType == "FRAME":
                            columnNum = act["KEY"]["COLUMN"]
                            matchRegex = act["KEY"]["MATCH"]
                            alias = act["KEY"]["ALIAS"]
                            keyName = act["KEY"]["NAME"]
                            column = table[tableNum].columns[columnNum]
                        
                            if keyName not in data[tableName]:
                                data[tableName][keyName] = dict()
                        
                            if(not matchRegex or (matchRegex and matchRegex in column.upper())):
                                valueRow = act["KEY"]["VALUE"]["ROW"]
                                valueColumn = act["KEY"]["VALUE"]["COLUMN"]
                                value = table[tableNum].iloc[valueRow,valueColumn]
                                print(columnNum, column.upper(), valueRow, valueColumn, value)
                                if(alias):
                                    data[tableName][keyName][alias] = value
                                else:
                                    data[tableName][keyName][column] = value
    return data

In [79]:
def storeOrgData(csym):
    dest = "../../Summary/orgData/"
    entPath = "../../Summary/entities/"
    orgs = list()
    if(csym == "ALLORGS"):
        files = glob.glob(entPath+"/*-ENTITIES.json")
        if(len(files) > 0):
            #print(len(files))
            for file in (files):
                basefile = os.path.basename(file)
                filename = os.path.splitext(basefile)[0]
                org = filename.split("-")[0]
                orgs.append(org)
    else:
        orgs = orgs+csym
    
    print("Processing data for {}".format(orgs))
    for org in orgs:
        print("Starting to collect data for {}".format(org))
        data = getOrgData(org)
        if(data):
            print(data)
            json_object = json.dumps(data, indent = 4)
            file = dest+org+".txt"

            # Writing to sample.json
            with open(file, "w") as outfile:
                outfile.write(json_object)
        time.sleep(10)

In [80]:
storeOrgData(["GTLB"])

Processing data for ['GTLB']
Starting to collect data for GTLB
https://finance.yahoo.com/quote/GTLB/profile?p=GTLB
TABLE NAME PROFILE
Table Number 0
FOUND
https://finance.yahoo.com/quote/GTLB/insider-transactions?p=GTLB
TABLE NAME INSIDERTRANS
Table Number 0
FOUND
https://finance.yahoo.com/quote/GTLB/insider-roster?p=GTLB
TABLE NAME MAJORTRANS
Table Number 0
FOUND
https://finance.yahoo.com/quote/GTLB/holders?p=GTLB
TABLE NAME HOLDERS
Table Number 1
FOUND
Table Number 0
FOUND
0 1 % OF SHARES HELD BY ALL INSIDER 0 0 5.57%
Table Number 0
FOUND
1 1 % OF SHARES HELD BY INSTITUTIONS 1 0 80.11%
Table Number 0
FOUND
2 1 % OF FLOAT HELD BY INSTITUTIONS 2 0 84.83%
Table Number 0
FOUND
3 1 NUMBER OF INSTITUTIONS HOLDING SHARES 3 0 400
https://finance.yahoo.com/quote/GTLB/analysis?p=GTLB
TABLE NAME ANALYSIS
Table Number 2
FOUND
1 1/30/2023 1 1 -0.03
Table Number 2
FOUND
2 4/29/2023 1 2 -0.06
Table Number 2
FOUND
3 7/30/2023 1 3 0.01
Table Number 2
FOUND
4 10/30/2023 1 4 0.09
Table Number 2
FOUND
1

In [80]:
#url = "https://finance.yahoo.com/news/pinterest-announces-second-quarter-2021-200500141.html"
#url = "https://finance.yahoo.com/news/crowdstrike-reports-second-quarter-fiscal-200500508.html"
#url = "https://finance.yahoo.com/news/stitch-fix-announces-fourth-quarter-200500527.html"
#url = "https://finance.yahoo.com/news/aurora-cannabis-announces-fiscal-2021-201500038.html"
#url = "https://finance.yahoo.com/news/canopy-growth-reports-first-quarter-110000649.html"
#url = "https://finance.yahoo.com/news/nike-inc-reports-fiscal-2022-201500472.html"
#url = "https://finance.yahoo.com/news/prospect-capital-announces-june-2021-230600417.html"
#url = "https://finance.yahoo.com/news/fiverr-announces-second-quarter-2021-050000560.html"
#url = "https://finance.yahoo.com/news/trade-desk-reports-second-quarter-123000360.html"
#url = "https://finance.yahoo.com/news/zoom-reports-financial-results-second-200500829.html"
#url = "https://finance.yahoo.com/news/kinsale-capital-group-inc-reports-201000573.html"
#url = "https://finance.yahoo.com/news/docusign-announces-second-quarter-fiscal-200500098.html"
#url = "https://finance.yahoo.com/news/nio-inc-reports-unaudited-second-213000202.html"
#url = "https://www.sec.gov/Archives/edgar/data/1671933/000115752320000277/a52180507_ex991.htm"
url = "https://www.sec.gov/Archives/edgar/data/0001713683/000171368322000025/zs-01312022_991.htm"
source = getPgSource(url)
tables = None
try:
    tables = pd.read_html(source)
except:
    tables = None
print(len(tables))

11


In [61]:
tableDesc = getElement("PREVELEM", source, "EDGAR")
print("ALL TABLE DESCRIPTIONS")
print(tableDesc)
tableNum = 0
desc = "NONE"
if tableDesc and tableNum < len(tableDesc):
    desc = tableDesc[tableNum]
print("\nTABLE DESCRIPTION:", desc)

ft = getOneTable(tables, tableNum, desc)
print("\n")
print(ft)

ALL TABLE DESCRIPTIONS
[' \n      THE FOLLOWING TABLE SUMMARIZES OUR CONSOLIDATED FINANCIAL RESULTS FOR\n      THE QUARTERS AND FISCAL YEARS ENDED DECEMBER 31, 2018 AND 2017 ($ IN\n      MILLIONS, EXCEPT PER SHARE AMOUNTS):\n    ', ' \n \n \n \n \n \n \n \n \n \n \n \n \n \n \n \n', ' \n \n \n \n \n \n \n \n \n \n \n \n \n \n \n \n', ' \n \n \n \n \n \n \n \n \n \n \n \n \n \n \n \n', ' \n      THE FOLLOWING TABLES SHOW THE COMPANY’S GAAP FINANCIAL METRICS\n      RECONCILED TO NON-GAAP FINANCIAL METRICS INCLUDED IN THIS RELEASE.\n    ', ' \n \n \n \n \n \n          \xa0\n         \n \n THREE MONTHS ENDED \n \n \n \n \n          \xa0\n         \n \n YEAR ENDED \n \n \n \n \n \n \n \n \n \n \n DECEMBER 31, \n \n \n \n \n \n \n DECEMBER 31, \n \n \n \n \n \n \n \n \n \n \n 2018 \n \n \n \n \n          \xa0\n         \n \n 2017 \n \n \n \n \n \n \n 2018 \n \n \n \n \n          \xa0\n         \n \n 2017 \n \n \n \n \n \n \n \n \n \n \n \n \n          \xa0\n         \n \n \n \n          NET 

In [81]:
def getRiskFactors(source):
    try:
        soup = BeautifulSoup(source, 'lxml')
        list_of_forms = soup.find_all('div')
    except (Exception) as e:
        print(e)
        list_of_forms = None
        return None

    found = False
    riskCnt = 0
    risks = dict()
    riskHdr = None
    riskSubHdr = None

    for item in (list_of_forms):
        searchText = item.text.strip()
        searchText = searchText.replace(u'\xa0', ' ')
        #searchText = searchText.replace("  ", "")
        #if("ITEM 1A. RISK FACTORS" in searchText):
        if("RISK FACTORS" in searchText.upper() and "ITEM 1A. " in searchText.upper() and len(searchText.split(" ")) < 10):
            #print(item.text, print(len(searchText.split(" "))))
        #if("ITEM 1A. RISK FACTORS" == searchText.upper()):
        #if("ITEM 1A. RISK FACTORS" in item.text.upper()):
            children = item.findChildren(recursive=True)
            for ctag in children:
                if(len(ctag.text.strip().split(" ")) < 2):
                    continue
                if "style" in ctag.attrs:
                    #print(ctag.attrs["style"], ctag.text)
                    style = ctag.attrs["style"]
                    sarr = style.split(";")
                    for stype in sarr:
                        starr = stype.split(":")
                        if("font-weight" in starr):
                            if(starr[1] == "bold" or int(starr[1]) > 400):
                                print(item.text)
                                found = True
                                continue
        if("ITEM 2." in searchText.upper() or "ITEM 1B" in searchText.upper() or "ITEMS 2, 3" in searchText.upper()):
            #print(item.text)
            found = False
        if (found):
            #if(len(item.text.split(" ")) < 2):
            if(len(searchText.split(" ")) < 2):
                continue
            #print(item.text)
            children = item.findChildren(recursive=True)
            for ctag in children:
                #print(ctag.text, ctag.attrs)
                if(len(ctag.text.strip().split(" ")) < 2):
                    continue
                if "style" in ctag.attrs:
                    #print(ctag.attrs["style"], ctag.text)
                    style = ctag.attrs["style"]
                    sarr = style.split(";")
                    fontFound = False
                    #print(sarr)
                    for stype in sarr:
                        starr = stype.split(":")
                        if("font-weight" in starr):
                            if(starr[1] == "bold" or int(starr[1]) > 400):
                                #print(style, ctag.text)
                                if(len(ctag.text.split(" ")) < 12 and "RISKS" in ctag.text.upper()):
                                    riskHdr = ctag.text.strip()
                                    riskHdr = riskHdr.upper().replace("OUR", "").replace("  "," ")
                                    print("RISK HEADER", riskHdr)
                                    if riskHdr not in risks:
                                        risks[riskHdr] = dict()
                                else:
                                    riskCnt = riskCnt + 1
                                    riskSubHdr = ctag.text.strip()
                                    if riskHdr in risks and riskSubHdr not in risks:
                                        risks[riskHdr][riskSubHdr] = list()
                            else:
                                if(riskHdr is not None and riskSubHdr is not None and riskSubHdr in risks[riskHdr]):
                                    risks[riskHdr][riskSubHdr].append(ctag.text.strip())
                            fontFound = True
                            break
                    if not fontFound:
                        if(riskHdr is not None and riskSubHdr is not None and riskSubHdr in risks[riskHdr]):
                            risks[riskHdr][riskSubHdr].append(ctag.text.strip())
    print("RISKS COUNT", riskCnt)
    risks["COUNT"] = riskCnt
    return(risks)

In [85]:
def storeEdgarTxt(source, f):
    write = True
    if not f:
        write = False
    soup = BeautifulSoup(source, 'lxml')
    list_of_forms = soup.find_all('div')
    for item in (list_of_forms):
        children = item.findChildren(recursive=False)
        for ctag in children:
            if(len(ctag.text.strip().split(" ")) < 2):
                continue
            ctext = ctag.text.strip()
            ctext = ctext.replace(u'\xa0', ' ')
            if "style" in ctag.attrs:
                #print(ctag.attrs["style"], ctag.text)
                style = ctag.attrs["style"]
                sarr = style.split(";")
                fontFound = False
                
                for stype in sarr:
                    starr = stype.split(":")
                    if("font-weight" in starr):
                        if(starr[1] == "bold" or (starr[1]) > str("400")):
                            if(len(ctext.split(" ")) < 12):
                                if not write:
                                    print("SECTION***", ctext)
                                else:
                                    newStr = "SECTION*** "+ctext
                                    f.write(newStr)
                                    f.write("\n")
                        else:
                            if not write:
                                print(ctext)
                            else:
                                newStr = ctext
                                f.write(newStr)
                                f.write("\n")
                        fontFound = True
                        break
                if not fontFound:
                    if not write:
                        print(ctext)
                    else:
                        newStr = ctext
                        f.write(newStr)
                        f.write("\n")

In [86]:
def xbrltojson(source):
    sreport = dict()
    soup = BeautifulSoup(source, 'lxml')
    tag_list = soup.find_all()
    for tag in tag_list:
        if tag.name == "context" or tag.name == "xbrli:context" or "contextref" in tag.attrs:
            #print(tag.attrs, list(tag.children))
            children = tag.findChildren(recursive=True)
            #print("CHILDRENNNN", children)
            if(len(children) > 0):
                for child in children:
                    #print("CHILDDDD", child)
                    ctag_list = child.findChildren(recursive=False)
                    #print("CTAGLIST", ctag_list)
                    for ctag in ctag_list:
                        #print(list(ctag.children))
                        if "\n" in ctag.text:
                            continue
                        cid = tag.attrs["id"]
                        if cid not in sreport:
                            sreport[cid] = dict()
                        if ctag.name not in sreport[cid]:
                            sreport[cid][ctag.name] = list()
                        val = dict()
                        val["TEXT"] = ctag.text
                        if ctag.attrs:
                            val["ATTR"] = (ctag.attrs)
                        sreport[cid][ctag.name].append(val)
                        #if not ctag.attrs:
                        #    print(tag.name, tag.attrs["id"], ctag.name, ctag.text)
                        #else:
                        #    print(tag.name, tag.attrs["id"], ctag.attrs, ctag.name, ctag.text)
            elif "contextref" in tag.attrs:
                cid = tag.attrs["contextref"]
                tname = tag.name
                val = dict()
                if cid in sreport:
                    if tname not in sreport:
                        sreport[tname] = list()
                    val["CONTEXT"] = sreport[cid]
                    val["CONTEXTID"] = cid
                    val["ATTR"] = tag.attrs
                    val["TEXT"] = tag.text
                    sreport[tname].append(val)
                #print(tag.name, tag.attrs["contextref"], tag.attrs, tag.text)
        #print(tag)
        #print(sreport)
    return sreport

In [82]:
def getTagValue(sreport, tag, smy, emy, member=None):
    if tag not in sreport:
        return None
    revList = sreport[tag]
    for item in range(0, len(revList)):
        skey=ekey=None
        #print(revList)
        #print(revList[item]["CONTEXT"])
        #print(revList[item]["CONTEXT"].keys())
        
        keys = revList[item]["CONTEXT"].keys()
        if "startdate" in keys and "enddate" in keys:
            skey = "startdate"
            ekey = "enddate"
        elif "xbrli:startdate" in keys and "xbrli:enddate" in keys:
            skey = "xbrli:startdate"
            ekey = "xbrli:enddate"
        
        if skey and ekey:
            #print(revList[item]["CONTEXT"]["startdate"][0]["TEXT"], revList[item]["CONTEXT"]["enddate"][0]["TEXT"])
            if smy in revList[item]["CONTEXT"][skey][0]["TEXT"] and emy in revList[item]["CONTEXT"][ekey][0]["TEXT"]:
                if member is None and 'xbrldi:explicitmember' not in revList[item]["CONTEXT"].keys():
                    #print(revList[item]["CONTEXT"][skey][0]["TEXT"], revList[item]["CONTEXT"][ekey][0]["TEXT"])
                    #print(revList[item]["TEXT"])
                    return revList[item]["TEXT"]
    return None

In [88]:
edgar.download_index('../../Summary/EDGAR/MASTER', 2019, "Apnatec admin@apnatec.com", skip_all_present_except_last=False)

In [85]:
def storeAll8KEdgarRpt(csym):
    edgsrc = "../../Summary/EDGAR/MASTER/"
    rptDest = "../../Summary/EDGAR/8-K/"+csym
    
    try:
        os.mkdir(rptDest) 
    except OSError as error: 
        print(error)
    
    orgdata = getOrgFileData(csym)
    cik = getOrgAttr(orgdata, "ORGPROFILE|CIK")
    cik = int(cik)
    print(cik)
    rptype = ["8-K"]
    srptype = ["EX-99.1", "EXHIBIT 99.1", "EX-99"]
    path = os.walk(edgsrc)
    urls = list()

    for root, directories, files in path:
        #if(len(urls) == 3):
        #    break
        for file in files:
            #if(len(urls) == 3):
            #    break
            fpath = edgsrc+file
            htmlink = None
            dateFiled = None
            fileType = None
            newurl = None
            #print(fpath)
            csv = pd.read_csv(fpath, sep="|",  lineterminator='\n', names=None, header=None)
            #print(csv.columns.values)
            creport = csv[(csv[0] == cik) & (csv[2].str.contains("|".join(rptype)))]
            cnt = 0
            prefix = "EP"
            for item in creport[5]:
                dateFiled = (creport.iloc[cnt,3])
                fileType = (creport.iloc[cnt,2])
                #print(item, dateFiled)
                htmlink = (item)
                url = "https://www.sec.gov/Archives/" + htmlink
                url = url.strip()
                cnt = cnt + 1
                print("8K URL", url)
                lstr = getLatestReportDate(csym)
                
                if(lstr):
                    ldate = datetime.strptime(lstr, "%Y-%m-%d")
                    fdate = datetime.strptime(dateFiled, "%Y-%m-%d")

                    if ldate and ldate >= fdate:
                        print("EARNING REPORT ALREADY EXISTS FOR URL {}".format(url))
                        continue
                
                txtfilename = csym + "_" + dateFiled + "_" + prefix + ".txt"
                txtfilename = rptDest+"/"+txtfilename
                rptname = csym + "-" + "REPORT" + "-" + dateFiled + "_" + "01.087695" + ".txt"
                rptpath = "../../Summary/report/"+rptname
    
                if os.path.isfile(txtfilename):
                    print("{} already exists, skipping".format(txtfilename))
                    continue

                source = getPgSource(url)
                df = pd.read_html(source)
                document_index = df[0]
                #print(document_index)
                #document_index = document_index.dropna()
                document_index = document_index.replace(np.nan, "HI")
                #print(document_index)

                document_name = document_index[document_index['Type'].str.contains("|".join(srptype))]
                #document_name = document_name['Document'].str.split(' ')
                #print(document_name)
                #print(document_index[document_index['Type']])
                if(len(document_name) == 0):
                    document_name = document_index[document_index['Description'].str.contains("|".join(srptype))]
                    if(len(document_name) == 0):
                        print("EARNING REPORT NOT FOUND FROM URL {}".format(url))
                        #return(urls)
                        continue
                #document_name = document_name[1][0].strip()
                document_name = document_name.iloc[0,2].strip()
                #print(document_name)
                report_formatted = url.replace('-','').replace('index.html','').strip()
                report_formatted = report_formatted + "/"+ document_name
                print("EP LINK:", report_formatted)
                
                allTables = getAllTables(report_formatted, "EDGAR")
                    
                if(allTables and ("STMTOP" in allTables or "BALANCESHEET" in allTables or "STMTCASHFLOW" in allTables)):
                    print("EARNING REPORT FOUND FROM URL {}, STORING REPORT AND OTHER DETAILS...".format(report_formatted))
                    
                    print("TRYING TO STORE TABLES IN FILE {}".format(rptpath))
                    if os.path.isfile(rptpath):
                        print("{} already exists, skipping".format(rptpath))
                    else:
                        with open(rptpath, 'x', encoding = 'utf-8') as outfile:
                            json_object = json.dumps(allTables, indent = 4)
                            outfile.write(json_object)

                    print("TRYING TO PARSE METRIC DATA FROM TABLES IN FILE {}".format(rptpath))
                    sentences = getMetricData(csym, tfile=rptpath, updateMissing=True)

                    print("TRYING TO STORE REFINED CONTENT IN FILE {}".format(txtfilename))
                    #storeOne8KEdgarRpt(report_formatted, csym, txtfilename, None, allTables)
                    testOne8KRpt(report_formatted, csym, txtfilename, None, allTables, extraSents=sentences)
                    urls.append(report_formatted)
                    time.sleep(10)
                else:
                    print("EARNING REPORT NOT FOUND FROM URL {}".format(report_formatted))
                #if(len(urls) == 3):
                #    break
                #time.sleep(10)
    return(urls)

In [86]:
csym = "GTLB"
urls = storeAll8KEdgarRpt(csym)
print(urls)

[WinError 183] Cannot create a file when that file already exists: '../../Summary/EDGAR/8-K/GTLB'
1653482
8K URL https://www.sec.gov/Archives/edgar/data/1653482/0001628280-21-024582-index.html
EP LINK: https://www.sec.gov/Archives/edgar/data/1653482/000162828021024582/gitlab-exhibit99120211031.htm
NUMBER OF TABLES 7

FOR TABLE 0

TABLE DESCRIPTION: 
ORIGINAL TABLE  0
    0   1   2   3   4   5             6             7             8
0 NaN NaN NaN NaN NaN NaN           NaN           NaN           NaN
1 NaN NaN NaN NaN NaN NaN  Exhibit 99.1  Exhibit 99.1  Exhibit 99.1
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 1

TABLE DESCRIPTION:  
ORIGINAL TABLE  1
                                                   0   \
0                                                 NaN   
1                                                 NaN   
2                                             Revenue   
3                                   GAAP Gross margin   
4                               Non-G

                                                   0   \
0                                                 NaN   
1                                                 NaN   
2                                                 NaN   
3               CASH FLOWS FROM OPERATING ACTIVITIES:   
4   Net loss, including amounts attributable to no...   
5   Adjustments to reconcile net loss to net cash ...   
6                    Stock-based compensation expense   
7                     Other non-cash expense (income)   
8                   Amortization of intangible assets   
9   Amortization of deferred contract acquisition ...   
10            Unrealized foreign exchange (gain) loss   
11                 Changes in assets and liabilities:   
12                                Accounts receivable   
13          Prepaid expenses and other current assets   
14                             Other long-term assets   
15     Costs deferred related to contract acquisition   
16                             

8K URL https://www.sec.gov/Archives/edgar/data/1653482/0001628280-22-006052-index.html
EP LINK: https://www.sec.gov/Archives/edgar/data/1653482/000162828022006052/gitlab-ex99120220131fy22.htm
NUMBER OF TABLES 8

FOR TABLE 0

TABLE DESCRIPTION: 
ORIGINAL TABLE  0
    0   1   2   3   4   5             6             7             8
0 NaN NaN NaN NaN NaN NaN           NaN           NaN           NaN
1 NaN NaN NaN NaN NaN NaN  Exhibit 99.1  Exhibit 99.1  Exhibit 99.1
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 1

TABLE DESCRIPTION:  
ORIGINAL TABLE  1
                                                   0   \
0                                                 NaN   
1                                                 NaN   
2                                             Revenue   
3                                   GAAP Gross margin   
4                               Non-GAAP Gross margin   
5                                 GAAP Operating loss   
6                             

HEADERSSSSSSSSS ['0:0']
{0: [1, 2], 3: [4, 5], 6: [7, 8]}

FINAL REPORT
                                               METRIC JANUARY 31, 2022
2                                              ASSETS              nan
3                                      CURRENT ASSETS              nan
4                           CASH AND CASH EQUIVALENTS          $884672
5                              SHORT-TERM INVESTMENTS            50031
6   ACCOUNTS RECEIVABLE, NET OF ALLOWANCE FOR DOUB...            77233
7        DEFERRED CONTRACT ACQUISITION COSTS, CURRENT            24363
8           PREPAID EXPENSES AND OTHER CURRENT ASSETS            15544
9                                TOTAL CURRENT ASSETS          1051843
10                        PROPERTY AND EQUIPMENT, NET             3271
11                                           GOODWILL             8145
12                             INTANGIBLE ASSETS, NET             6285
13   DEFERRED CONTRACT ACQUISITION COSTS, NON-CURRENT            14743
14   

{0: [1, 2], 3: [4, 5], 6: [7, 8], 9: [10, 11], 12: [13, 14], 15: [16, 17], 18: [19, 20]}

FINAL REPORT
                                               METRIC  \
3                                             REVENUE   
4                   SUBSCRIPTIONSELF-MANAGED AND SAAS   
5                       LICENSESELF-MANAGED AND OTHER   
6                                       TOTAL REVENUE   
7                                     COST OF REVENUE   
8                   SUBSCRIPTIONSELF-MANAGED AND SAAS   
9                       LICENSESELF-MANAGED AND OTHER   
10                              TOTAL COST OF REVENUE   
11                                       GROSS PROFIT   
12                                 OPERATING EXPENSES   
13                                SALES AND MARKETING   
14                           RESEARCH AND DEVELOPMENT   
15                         GENERAL AND ADMINISTRATIVE   
16                           TOTAL OPERATING EXPENSES   
17                               LOSS FROM

...

TABLE None First Column NAN UNIT T

FOR TABLE 2

TABLE DESCRIPTION:  FOR THE FOURTH QUARTER AND FISCAL YEAR 2024, GITLAB INC. EXPECTS  ( IN MILLIONS , EXCEPT SHARE AND PER SHARE DATA) :
ORIGINAL TABLE  2
                                                  0   \
0                                                NaN   
1                                                NaN   
2                                            Revenue   
3                   Non-GAAP operating income (loss)   
4  Non-GAAP net income per share assuming approxi...   
5                                                NaN   
6                                                NaN   
7                                                NaN   
8                                                NaN   

                                                  1   \
0                                                NaN   
1                                                NaN   
2                                            Revenue   
3          

HEADERSSSSSSSSS ['0:1']
{0: [1, 2], 3: [4, 5], 6: [7, 8], 9: [10, 11], 12: [13, 14], 15: [16, 17], 18: [19, 20]}

FINAL REPORT
                                               METRIC  \
3                                             REVENUE   
4                   SUBSCRIPTIONSELF-MANAGED AND SAAS   
5                       LICENSESELF-MANAGED AND OTHER   
6                                       TOTAL REVENUE   
7                                     COST OF REVENUE   
8                   SUBSCRIPTIONSELF-MANAGED AND SAAS   
9                       LICENSESELF-MANAGED AND OTHER   
10                              TOTAL COST OF REVENUE   
11                                       GROSS PROFIT   
12                                 OPERATING EXPENSES   
13                                SALES AND MARKETING   
14                           RESEARCH AND DEVELOPMENT   
15                         GENERAL AND ADMINISTRATIVE   
16                           TOTAL OPERATING EXPENSES   
17                

ORIGINAL TABLE  6
                                                   0   \
0                                                 NaN   
1                                                 NaN   
2                                                 NaN   
3                          Gross profit on GAAP basis   
4                          Gross margin on GAAP basis   
5                    Stock-based compensation expense   
6                Amortization of acquired intangibles   
7                               Restructuring charges   
8                      Gross profit on non-GAAP basis   
9                      Gross margin on non-GAAP basis   
10                                                NaN   
11                  Sales and marketing on GAAP basis   
12                   Stock-based compensation expense   
13                              Restructuring charges   
14              Sales and marketing on non-GAAP basis   
15                                                NaN   
16           


FINAL REPORT
                                               METRIC  \
3                          GROSS PROFIT ON GAAP BASIS   
4                          GROSS MARGIN ON GAAP BASIS   
5                    STOCK-BASED COMPENSATION EXPENSE   
6                AMORTIZATION OF ACQUIRED INTANGIBLES   
7                               RESTRUCTURING CHARGES   
8                      GROSS PROFIT ON NON-GAAP BASIS   
9                      GROSS MARGIN ON NON-GAAP BASIS   
11                  SALES AND MARKETING ON GAAP BASIS   
12                   STOCK-BASED COMPENSATION EXPENSE   
13                              RESTRUCTURING CHARGES   
14              SALES AND MARKETING ON NON-GAAP BASIS   
16             RESEARCH AND DEVELOPMENT ON GAAP BASIS   
17                   STOCK-BASED COMPENSATION EXPENSE   
18                              RESTRUCTURING CHARGES   
19         RESEARCH AND DEVELOPMENT ON NON-GAAP BASIS   
21           GENERAL AND ADMINISTRATIVE ON GAAP BASIS   
22               

TABLEEEEEEEEEEE 0
WRITING REGULAR TABLE  0
Exhibit 99.1
TABLEEEE CNTTTTT 1

SCHQ*** Fiscal Third Quarter Highlights:.

CS*** “We delivered a strong quarter, which was driven by the continued adoption of our DevSecOps Platform,” said Sid Sijbrandij, GitLab CEO and co-founder. “GitLab is the only DevSecOps company that integrates security, compliance, and AI into one platform. With enterprises facing complexity from all directions, they need a partner to help them realize business value. GitLab helps improve developer productivity and reduces software spend, which is why our customers report seeing 7x faster cycle times with GitLab.”.

CS*** “Revenue grew 32% year-over-year, which demonstrates continued business momentum driven by our market-leading platform approach,” said Brian Robins, GitLab chief financial officer. We continue to grow responsibly and delivered over 2,200 basis points of non-GAAP operating margin expansion. I am pleased to share that we had our first quarter of non-GA

In [84]:
def storeEdgarRpt(csym):
    edgsrc = "../../Summary/EDGAR/MASTER/"
    #cik = 1506293
    #csym = "PINS"
    orgdata = getOrgFileData(csym)
    cik = getOrgAttr(orgdata, "ORGPROFILE|CIK")
    cik = int(cik)
    print(cik)
    rptype = ["10-Q","10-K"]
    path = os.walk(edgsrc)
    urls = dict()
    textDest = "../../Summary/EDGAR/TEXT/"+csym
    jsonDest = "../../Summary/EDGAR/JSON/"+csym
    riskDest = "../../Summary/EDGAR/RISKS/"+csym
    tblDest = "../../Summary/EDGAR/TABLES/"+csym

    try:
        os.mkdir(textDest) 
        os.mkdir(jsonDest)
        os.mkdir(riskDest)
        os.mkdir(tblDest)
    except OSError as error: 
        print(error)  

    for root, directories, files in path:
        for file in files:
            fpath = edgsrc+file
            htmlink = None
            dateFiled = None
            fileType = None
            newurl = None
            #print(fpath)
            csv = pd.read_csv(fpath, sep="|",  lineterminator='\n', names=None, header=None)
            #print(csv.columns.values)
            creport = csv[(csv[0] == cik) & (csv[2].str.contains("|".join(rptype)))]
            #print(creport)
            for item in creport[5]:
                if "html" in item:
                    htmlink = (item)
                    dateFiled = (creport.iloc[0,3])
                    fileType = (creport.iloc[0,2])
                    break
            #htmlink = str(creport.iloc[0,5])
            if htmlink:
                txtfilename = fileType+"_"+dateFiled+".txt"
                txtfilename = textDest+"/"+txtfilename
            
                jsonfilename = fileType+"_"+dateFiled+".json"
                jsonfilename = jsonDest+"/"+jsonfilename
                
                riskfilename = fileType+"_"+dateFiled+".json"
                riskfilename = riskDest+"/"+riskfilename
                
                tblfilename = fileType+"_"+dateFiled+".json"
                tblfilename = tblDest+"/"+tblfilename
            
                if os.path.isfile(jsonfilename):
                    print("{} already exists, skipping".format(jsonfilename))
                    continue
            
                url = "https://www.sec.gov/Archives/" + htmlink
                url = url.strip()
                #print(url)
                #print(dateFiled, fileType, url)
                #print(url, dateFiled)
                source = getPgSource(url)
                df = pd.read_html(source)
                document_index = df[0]
                document_index = document_index.dropna()

                document_name = document_index[document_index['Description'].str.contains("|".join(rptype))]
                document_name = document_name['Document'].str.split(' ')
                document_name = document_name[0][0].strip()
                if("10q_" in document_name):
                    xmldoc = document_name.replace("10q_","").replace("htm","xml")
                elif("10k_" in document_name):
                    xmldoc = document_name.replace("10k_","").replace("htm","xml")
                else:
                    xmldoc = document_name.replace(".htm", "_htm.xml")
                #print(document_name)

                report_formatted = htmlink.replace('-','').replace('index.html','').strip()
                #print(report_formatted)
            
                newurl = "https://www.sec.gov/Archives/" + report_formatted + "/" + document_name
                xmlink = "https://www.sec.gov/Archives/" + report_formatted + "/" + xmldoc
                #print(url, newurl, xmlink)
                
                if(fileType != "10-Q" and fileType != "10-K"):
                    print("INVALID Report type {}, continuing...".format(fileType))
                    continue
            
                print("TRYING TO WRITE TEXT DATA FOR {}, report type {}, date filed {}".format(csym, fileType, dateFiled))
                txtsrc = getPgSource(newurl)
                with open(txtfilename, 'x', encoding = 'utf-8') as f:
                    newStr = newurl
                    f.write(newStr)
                    f.write("\n")
                    newStr = xmlink
                    f.write(newStr)
                    f.write("\n")
                    storeEdgarTxt(txtsrc, f)
            
                print("TRYING TO WRITE RISKS DATA FOR {}, report type {}, date filed {}".format(csym, fileType, dateFiled))
                risks = getRiskFactors(txtsrc)
                if risks:
                    with open(riskfilename, 'x', encoding = 'utf-8') as rfile:
                        json_object = json.dumps(risks, indent = 4)
                        rfile.write(json_object)
                
                print("TRYING TO WRITE TABLES DATA FOR {}, report type {}, date filed {}".format(csym, fileType, dateFiled))
                tables = getAllTables(newurl, "YH")
                if tables:
                    with open(tblfilename, 'x', encoding = 'utf-8') as tfile:
                        json_object = json.dumps(tables, indent = 4)
                        tfile.write(json_object)
                
                print("TRYING TO WRITE XBRL JSON DATA FOR {}, report type {}, date filed {}".format(csym, fileType, dateFiled))
                xmlsrc = getPgSource(xmlink)
                sreport = xbrltojson(xmlsrc)
                if sreport:
                    with open(jsonfilename, 'x', encoding = 'utf-8') as outfile:
                        json_object = json.dumps(sreport, indent = 4)
                        outfile.write(json_object)
                time.sleep(10)

In [74]:
csym = "OKTA"
storeEdgarRpt(csym)

1660134
TRYING TO WRITE TEXT DATA FOR OKTA, report type 10-K, date filed 2019-03-14
TRYING TO WRITE RISKS DATA FOR OKTA, report type 10-K, date filed 2019-03-14
Item 1A. Risk Factors 
RISK HEADER RISKS RELATED TO BUSINESS
RISK HEADER RISKS RELATED TO OWNERSHIP OF CLASS A COMMON STOCK
RISK HEADER RISKS RELATED TO OUTSTANDING CONVERTIBLE NOTES
RISKS COUNT 68
TRYING TO WRITE TABLES DATA FOR OKTA, report type 10-K, date filed 2019-03-14
NUMBER OF TABLES 248

FOR TABLE 0

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  0
     0                                                  1
0  NaN                                                NaN
1  NaN                                                NaN
2    ý  ANNUAL REPORT PURSUANT TO SECTION 13 OR 15(d) ...
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 1

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  1
     0                                                  1
0  NaN                                                NaN
1  NaN                         

HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 45

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  45
     0                                                  1
0  NaN                                                NaN
1    •  Infrastructure-as-a-service providers, such as...
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 46

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  46
     0                                                  1
0  NaN                                                NaN
1    •  Dedicated customer identity and access managem...
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 47

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  47
     0                                                  1
0  NaN                                                NaN
1    •  price our platform effectively so that we are ...
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 48

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  48
     0                                    

HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 92

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  92
     0                                              1
0  NaN                                            NaN
1    •  unforeseen integration or other expenses; and
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 93

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  93
     0                                                  1
0  NaN                                                NaN
1    •  future impairment of goodwill or other acquire...
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 94

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  94
     0                                                  1
0  NaN                                                NaN
1    •  unexpected costs and errors in the localizatio...
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 95

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  95
     0                                                

HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 137

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  137
     0                                                  1
0  NaN                                                NaN
1    •  any derivative action or proceeding brought on...
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 138

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  138
     0                                                 1
0  NaN                                               NaN
1    •  any action asserting a breach of fiduciary duty;
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 139

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  139
     0                                                  1
0  NaN                                                NaN
1    •  any action asserting a claim against us arisin...
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 140

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  140
     0                               

{1: [2, 3], 5: [6, 7], 9: [10, 11], 13: [14, 15], 17: [18, 19]}

FINAL REPORT
                                               METRIC  \
6                                             REVENUE   
7                                        SUBSCRIPTION   
8                     PROFESSIONAL SERVICES AND OTHER   
9                                       TOTAL REVENUE   
10                                    COST OF REVENUE   
11                                       SUBSCRIPTION   
12                    PROFESSIONAL SERVICES AND OTHER   
13                              TOTAL COST OF REVENUE   
14                                       GROSS PROFIT   
15                                 OPERATING EXPENSES   
16                           RESEARCH AND DEVELOPMENT   
17                                SALES AND MARKETING   
18                         GENERAL AND ADMINISTRATIVE   
19                           TOTAL OPERATING EXPENSES   
20                                     OPERATING LOSS   
21        

...

{0: [1, 2], 3: [4, 5], 6: [7, 8], 9: [10, 11], 12: [13, 14], 15: [16, 17], 18: [19, 20], 21: [22, 23]}

FINAL REPORT
                             METRIC  \
4                           REVENUE   
5                      SUBSCRIPTION   
6   PROFESSIONAL SERVICES AND OTHER   
7                     TOTAL REVENUE   
8             PERCENTAGE OF REVENUE   
9                      SUBSCRIPTION   
10  PROFESSIONAL SERVICES AND OTHER   
11                            TOTAL   

   NINE MONTHS ENDEDOCTOBER 31, 2021 (DOLLARS IN THOUSANDS)  \
4                                                 nan         
5                                             $879881         
6                                               37305         
7                                             $917186         
8                                                 nan         
9                                                 96%         
10                                                  4         
11                         

[6 rows x 24 columns]
HEADERSSSSSSSSS ['0:2']
{0: [1, 2], 3: [4, 5], 6: [7, 8], 9: [10, 11], 12: [13, 14], 15: [16, 17], 18: [19, 20], 21: [22, 23]}

FINAL REPORT
                  METRIC  \
4    SALES AND MARKETING   
5  PERCENTAGE OF REVENUE   

  NINE MONTHS ENDEDOCTOBER 31, 2021 (DOLLARS IN THOUSANDS)  \
4                                            $548749         
5                                                60%         

  NINE MONTHS ENDEDOCTOBER 31, 2020 (DOLLARS IN THOUSANDS)  \
4                                            $312177         
5                                                52%         

  NAN $ CHANGE (DOLLARS IN THOUSANDS) NAN % CHANGE (DOLLARS IN THOUSANDS)  
4                             $236572                                 76%  
5                                 nan                                 nan  

FOR TABLE 54

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  54
                           0                           1   \
0                         NaN  

{0: [1, 2], 3: [4, 5], 6: [7, 8], 9: [10, 11], 12: [13, 14], 15: [16, 17], 18: [19, 20], 21: [22, 23]}

FINAL REPORT
                                              METRIC  \
4                                   INTEREST EXPENSE   
5                     INTEREST INCOME AND OTHER, NET   
6  LOSS ON EARLY EXTINGUISHMENT AND CONVERSION OF...   
7                            INTEREST AND OTHER, NET   

  NINE MONTHS ENDEDOCTOBER 31, 2021 (DOLLARS IN THOUSANDS)  \
4                                           $(68776)         
5                                               7622         
6                                              (179)         
7                                           $(61333)         

  NINE MONTHS ENDEDOCTOBER 31, 2020 (DOLLARS IN THOUSANDS)  \
4                                           $(50063)         
5                                              10737         
6                                             (2263)         
7                                          

{0: [1, 2], 3: [4, 5], 6: [7, 8], 9: [10, 11], 12: [13, 14], 15: [16, 17], 18: [19, 20], 21: [22, 23]}

FINAL REPORT
                                               METRIC  \
4                                        GROSS PROFIT   
5                                                 ADD   
6   STOCK-BASED COMPENSATION EXPENSE INCLUDED IN C...   
8                AMORTIZATION OF ACQUIRED INTANGIBLES   
9        ACQUISITION AND INTEGRATION-RELATED EXPENSES   
10                              NON-GAAP GROSS PROFIT   
11                                       GROSS MARGIN   
12                              NON-GAAP GROSS MARGIN   

   THREE MONTHS ENDED OCTOBER 31, 2021 (DOLLARS IN THOUSANDS)  \
4                                             $241006           
5                                                 nan           
6                                               16831           
8                                               11335           
9                                           

{0: [1, 2], 3: [4, 5], 6: [7, 8], 9: [10, 11], 12: [13, 14], 15: [16, 17], 18: [19, 20], 21: [22, 23]}

FINAL REPORT
                                               METRIC  \
4           NET CASH PROVIDED BY OPERATING ACTIVITIES   
5                                                LESS   
6                 PURCHASES OF PROPERTY AND EQUIPMENT   
7       CAPITALIZATION OF INTERNAL-USE SOFTWARE COSTS   
9                                      FREE CASH FLOW   
10  NET CASH PROVIDED BY (USED IN) INVESTING ACTIV...   
11          NET CASH PROVIDED BY FINANCING ACTIVITIES   
12                              FREE CASH FLOW MARGIN   

   THREE MONTHS ENDED OCTOBER 31, 2021 (DOLLARS IN THOUSANDS)  \
4                                              $37120           
5                                                 nan           
6                                              (1766)           
7                                              (1970)           
9                                           

In [264]:
#url = "https://www.sec.gov/Archives/edgar/data/320193/000032019321000105/aapl-20210925_htm.xml"
#url = "https://www.sec.gov/Archives/edgar/data/1506293/000150629321000233/pins-20210930_htm.xml"
#url = "https://www.sec.gov/Archives/edgar/data/1506293/000162828019006928/pins-20190331.xml"
#url = "https://www.sec.gov/Archives/edgar/data/1585521/000158552121000295/zm-20211031_htm.xml"
url = "https://www.sec.gov/Archives/edgar/data/1404655/000119312519139680/d745582dex991.htm"
source = getPgSource(url)

In [104]:
tag = "us-gaap:revenuefromcontractwithcustomerexcludingassessedtax"
#tag = "us-gaap:earningspersharediluted"
#tag = "us-gaap:earningspersharebasicanddiluted"
smy = "2020-02"
emy = "2021-01"
#smy = "2021-07"
#emy = "2021-09"
if source:
    sreport = xbrltojson(source)
    if sreport:
        val = getTagValue(sreport, tag, smy, emy)
        print(val)

2651368000


In [63]:
#url = "https://www.sec.gov/Archives/edgar/data/1506293/000162828019006928/pins-10q_20190331.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1506293/000150629321000233/pins-20210930.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1506293/000150629321000025/pins-20201231.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1506293/000150629320000152/pins-20200630.htm"
#url = "https://www.sec.gov/ix?doc=/Archives/edgar/data/1535527/000153552721000028/crwd-20211031.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1535527/000153552721000028/crwd-20211031.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1506293/000150629319000020/pins-10q20190930.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1585521/000158552121000295/zm-20211031.htm"
url = "https://www.sec.gov/ix?doc=/Archives/edgar/data/0001441683/000144168321000085/appn-20210930.htm"
source = getPgSource(url)

In [64]:
getRiskFactors(source)

Item 1A. RISK FACTORS
RISKS COUNT 1


{'COUNT': 1}

In [265]:
allTables = getAllTables(url, "EDGAR")

NUMBER OF TABLES 34

FOR TABLE 0

TABLE DESCRIPTION:  REVENUE 
ORIGINAL TABLE  0
    0  1   2                                                  3
0 NaN  ● NaN  Total revenue was $151.8 million, up 33% compa...
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 1

TABLE DESCRIPTION:   
ORIGINAL TABLE  1
    0  1   2                                                  3
0 NaN  ● NaN  Subscription revenue was $144.2 million, up 33...
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 2

TABLE DESCRIPTION:   
ORIGINAL TABLE  2
    0  1   2                                                  3
0 NaN  ● NaN  Professional services and other revenue was $7...
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 3

TABLE DESCRIPTION:  OPERATING INCOME (LOSS) 
ORIGINAL TABLE  3
    0  1   2                                                  3
0 NaN  ● NaN  GAAP operating margin was (6.0%), compared to ...
HEADERSSSSSSSSS []
INVALID TABLE, HEADER NOT FOUND

FOR TABLE 4

TABL

{1: [2], 3: [4], 5: [6]}

FINAL REPORT
                                               METRIC  \
3                                            REVENUES   
4                                        SUBSCRIPTION   
5                     PROFESSIONAL SERVICES AND OTHER   
7                                       TOTAL REVENUE   
9                                    COST OF REVENUES   
10                                       SUBSCRIPTION   
11                    PROFESSIONAL SERVICES AND OTHER   
13                             TOTAL COST OF REVENUES   
15                                       GROSS PROFIT   
17                                 OPERATING EXPENSES   
18                           RESEARCH AND DEVELOPMENT   
19                                SALES AND MARKETING   
20                         GENERAL AND ADMINISTRATIVE   
22                           TOTAL OPERATING EXPENSES   
24                               LOSS FROM OPERATIONS   
26                                      OTHER EXP

HEADERSSSSSSSSS ['0:1', '10:10']
{3: [4], 5: [6]}
EXCEPTION: 2
Traceback (most recent call last):
  File "c:\users\ankan\appdata\local\programs\python\python37\lib\site-packages\pandas\core\indexes\base.py", line 2895, in get_loc
    return self._engine.get_loc(casted_key)
  File "pandas\_libs\index.pyx", line 70, in pandas._libs.index.IndexEngine.get_loc
  File "pandas\_libs\index.pyx", line 101, in pandas._libs.index.IndexEngine.get_loc
  File "pandas\_libs\hashtable_class_helper.pxi", line 1032, in pandas._libs.hashtable.Int64HashTable.get_item
  File "pandas\_libs\hashtable_class_helper.pxi", line 1039, in pandas._libs.hashtable.Int64HashTable.get_item
KeyError: 2

The above exception was the direct cause of the following exception:

Traceback (most recent call last):
  File "<ipython-input-198-781d29c5995c>", line 241, in getOneTable
    report[mgclmn] = report[mgclmn] + report[i]
  File "c:\users\ankan\appdata\local\programs\python\python37\lib\site-packages\pandas\core\frame.py"

{1: [2], 3: [4], 5: [6], 7: [8], 9: [10], 11: [12], 13: [14], 15: [16], 17: [18], 19: [20], 21: [22], 23: [24], 25: [26], 27: [28], 29: [30], 31: [32], 33: [34], 35: [36], 37: [38]}

FINAL REPORT
                                         METRIC  \
4                                  GAAP EXPENSE   
5                      STOCK-BASED COMPENSATION   
6    AMORTIZATION OF ACQUIRED INTANGIBLE ASSETS   
7                  ACQUISITION RELATED EXPENSES   
9                              NON-GAAP EXPENSE   
12      GAAP EXPENSE AS A PERCENTAGE OF REVENUE   
13  NON-GAAP EXPENSE AS A PERCENTAGE OF REVENUE   

   THREE MONTHS ENDED MARCH 31, 2019 COS,SUBSCRIPTION  \
4                                              $21301   
5                                                (614   
6                                                (800   
7                                                 nan   
9                                              $19887   
12                                              14.0%

{1: [1], 3: [4], 5: [5]}

FINAL REPORT
                                    METRIC THREE MONTHS ENDED JUNE 30, 2019  \
29                GAAPOPERATINGINCOMERANGE                ($20730)-($19730)   
30                 STOCK-BASEDCOMPENSATION                            29100   
31  AMORTIZATIONOFACQUIREDINTANGIBLEASSETS                              800   
32            ACQUISITION RELATED EXPENSES                               30   
34         NON-GAAP OPERATING INCOME RANGE                    $9200 -$10200   

   YEAR ENDEDDECEMBER 31, 2019  
29           ($58730)-($56730)  
30                      105500  
31                        3100  
32                         130  
34               $50000-$52000  

FOR TABLE 27

TABLE DESCRIPTION: 
ORIGINAL TABLE  27
                                                    0  \
0                                                 NaN   
1   Reconciliation of forecasted non-GAAP net inco...   
2                                                 NaN   
3     

In [80]:
storeEdgarTxt(source, None)

Table of Contents
Table of Contents
SECTION*** UNITED STATES
SECTION*** SECURITIES AND EXCHANGE COMMISSION
SECTION*** Washington, D.C. 20549
SECTION*** FORM 10-Q
☒QUARTERLY REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934
SECTION*** For the quarterly period ended October 31, 2021
☐TRANSITION REPORT PURSUANT TO SECTION 13 OR 15(d) OF THE SECURITIES EXCHANGE ACT OF 1934
SECTION*** Commission File Number 001-38865
SECTION*** Zoom Video Communications, Inc.
SECTION*** (Exact name of registrant as specified in its Charter)
Delaware61-1648780(State or other jurisdictionof incorporation or organization)(I.R.S. EmployerIdentification No.)
SECTION*** San Jose, California 95113
SECTION*** (Address of principal executive offices and Zip Code)
SECTION*** (888) 799-9666
SECTION*** (Registrant’s telephone number, including area code)
Securities registered pursuant to Section 12(b) of the Act:
Title of each classTrading Symbol(s)Name of each exchange on which registeredCl

In [159]:
#url = "https://www.sec.gov/Archives/edgar/data/1261333/000126133321000209/q322ex-991er.htm"
#url = "https://www.sec.gov/Archives/edgar/data/1506293/000150629321000231/q3-21xshareholderletter.htm"
url = "https://www.sec.gov/Archives/edgar/data/1713683/000171368319000049/zs-10312019991.htm"
allTables = getAllTables(url, "EDGAR")
#source = getPgSource(url)

NUMBER OF TABLES 10

FOR TABLE 0

TABLE DESCRIPTION: NONE
ORIGINAL TABLE  0
                 0                1                2  \
0              NaN              NaN              NaN   
1            Date:            Date:            Date:   
2            Time:            Time:            Time:   
3         Webcast:         Webcast:         Webcast:   
4  Dial-in number:  Dial-in number:  Dial-in number:   

                              3                             4  \
0                           NaN                           NaN   
1     Tuesday, December 3, 2019     Tuesday, December 3, 2019   
2                  1:30 p.m. PT                  1:30 p.m. PT   
3       https://ir.zscaler.com/       https://ir.zscaler.com/   
4  334-777-6978 or 800-367-2403  334-777-6978 or 800-367-2403   

                              5  
0                           NaN  
1     Tuesday, December 3, 2019  
2                  1:30 p.m. PT  
3       https://ir.zscaler.com/  
4  334-777-6978 or 800-367

{1: [2], 3: [4, 5], 6: [7, 8], 9: [10, 11]}

FINAL REPORT
                                               METRIC  \
8                CASH FLOWS FROM OPERATING ACTIVITIES   
9                                            NET LOSS   
10  ADJUSTMENTS TO RECONCILE NET LOSS TO CASH PROV...   
11              DEPRECIATION AND AMORTIZATION EXPENSE   
12  AMORTIZATION EXPENSE OF ACQUIRED INTANGIBLE AS...   
13  AMORTIZATION OF DEFERRED CONTRACT ACQUISITION ...   
14  AMORTIZATION OF OPERATING LEASE RIGHT-OF-USE A...   
15                   STOCK-BASED COMPENSATION EXPENSE   
16                              DEFERRED INCOME TAXES   
17  ACCRETION OF PURCHASED DISCOUNTS, NET OF AMORT...   
18                                              OTHER   
19  CHANGES IN OPERATING ASSETS AND LIABILITIES, N...   
20                                ACCOUNTS RECEIVABLE   
21                DEFERRED CONTRACT ACQUISITION COSTS   
22  PREPAID EXPENSES, OTHER CURRENT AND NONCURRENT...   
23                            


FINAL REPORT
                                               METRIC  \
9              NON-GAAP NET INCOME PER SHARE, DILUTED   
10                                      GAAP NET LOSS   
11                   STOCK-BASED COMPENSATION EXPENSE   
12                        LITIGATION-RELATED EXPENSES   
13  AMORTIZATION EXPENSE OF ACQUIRED INTANGIBLE AS...   
14                        PROVISION FOR INCOME TAXES    
15                       NON-GAAP NET INCOME, DILUTED   
17                   GAAP NET LOSS PER SHARE, DILUTED   
18                   STOCK-BASED COMPENSATION EXPENSE   
19                        LITIGATION-RELATED EXPENSES   
20  AMORTIZATION EXPENSE OF ACQUIRED INTANGIBLE AS...   
22                        PROVISION FOR INCOME TAXES    
23            NON-GAAP NET INCOME PER SHARE, DILUTED    
24  WEIGHTED-AVERAGE SHARES USED IN COMPUTING NON-...   

   NAN THREE MONTHS ENDED OCTOBER 31, 2018  
9                                      nan  
10                                  -$75

In [266]:
allTables

{'TOTAL': 34,
 'PARSESUCCESS': [21, 22, 23, 25, 26, 27],
 'PARSEFAIL': [0,
  1,
  2,
  3,
  4,
  5,
  6,
  7,
  8,
  9,
  10,
  11,
  12,
  13,
  14,
  15,
  16,
  17,
  18,
  19,
  20,
  24,
  28,
  29,
  30,
  31,
  32,
  33],
 0: {'ORIGINAL': '[{"0":null,"1":"\\u25cf","2":null,"3":"Total revenue was $151.8\\u00a0million, up 33% compared to Q1\\u201918."}]'},
 1: {'ORIGINAL': '[{"0":null,"1":"\\u25cf","2":null,"3":"Subscription revenue was $144.2\\u00a0million, up 33% compared to Q1\\u201918."}]'},
 2: {'ORIGINAL': '[{"0":null,"1":"\\u25cf","2":null,"3":"Professional services and other revenue was $7.6\\u00a0million, up 27% compared to Q1\\u201918."}]'},
 3: {'ORIGINAL': '[{"0":null,"1":"\\u25cf","2":null,"3":"GAAP operating margin was (6.0%), compared to (9.9%) in Q1\\u201918."}]'},
 4: {'ORIGINAL': '[{"0":null,"1":"\\u25cf","2":null,"3":"Non-GAAP operating margin was 8.6%, an improvement of approximately 3.7 percentage points from 4.9% in Q1\\u201918."}]'},
 5: {'ORIGINAL': '[{"0":

In [181]:
html_code = """<a><c>text2<br></c>text3</a>"""
soup = BeautifulSoup(html_code, 'html.parser')
print(soup.a.findChildren(), (soup.a.find(text=True, recursive=False)))

[<c>text2<br/></c>, <br/>] text3


In [71]:
#import pdfplumber
pfile = "../../Summary/Supplement/Q4-2021-Investor-Presentation.pdf"
#with pdfplumber.open(pfile) as pdf:
#    first_page = pdf.pages[9]
#    print(first_page.extract_text())

In [72]:
from pdfminer3.layout import LAParams, LTTextBox
from pdfminer3.pdfpage import PDFPage
from pdfminer3.pdfinterp import PDFResourceManager
from pdfminer3.pdfinterp import PDFPageInterpreter
from pdfminer3.converter import PDFPageAggregator
from pdfminer3.converter import TextConverter
import io

resource_manager = PDFResourceManager()
fake_file_handle = io.StringIO()
converter = TextConverter(resource_manager, fake_file_handle, laparams=LAParams())
page_interpreter = PDFPageInterpreter(resource_manager, converter)

with open(pfile, 'rb') as fh:

    for page in PDFPage.get_pages(fh,
                                  caching=True,
                                  check_extractable=True):
        page_interpreter.process_page(page)

    text = fake_file_handle.getvalue()

# close open handles
converter.close()
fake_file_handle.close()

print(text)

Investor Presentation

December 31, 2021

© Copyright Cloudﬂare, Inc.
© Copyright Cloudﬂare, Inc.

Safe Harbor

This presentation and the accompanying oral commentary have been prepared by Cloudflare, Inc. (“Cloudflare”) for informational purposes only and not for any other purpose. Nothing contained in this 
presentation is, or should be construed as, a recommendation, promise, or representation by the presenter or Cloudflare or any officer, director, employee, agent, or advisor of Cloudflare. This presentation 
does not purport to be all-inclusive or to contain all of the information you may desire. Information provided in this presentation and the accompanying oral commentary speak only as of the date set forth on 
the cover page of this presentation.
This presentation and the accompanying oral commentary contain express and implied “forward-looking” statements within the meaning of the federal securities laws, and these statements involve 
substantial risks, assumptions, and uncer

In [4]:
import fitz # PyMuPDF
import io
from PIL import Image

pdf_file = fitz.open(pfile)

page_index = 2
page = pdf_file[page_index]
image_list = page.get_images()
if image_list:
    print(f"[+] Found a total of {len(image_list)} images in page {page_index}")
else:
    print("[!] No images found on page", page_index)

for image_index, img in enumerate(page.get_images(), start=1):
    # get the XREF of the image
    xref = img[0]
    # extract the image bytes
    base_image = pdf_file.extract_image(xref)
    image_bytes = base_image["image"]
    # get the image extension
    image_ext = base_image["ext"]
    # load it to PIL
    image = Image.open(io.BytesIO(image_bytes))
    #image.show()

[+] Found a total of 3 images in page 2


In [208]:
from pptx import Presentation
from pptx.enum.shapes import MSO_SHAPE_TYPE
pfile = "../../Summary/Supplement/Q4-2021-Investor-Presentation-converted.pptx"
prs = Presentation(pfile)

text_runs = []
cnt = 0 
for slide in prs.slides:
    cnt = cnt + 1
    print("\nCNTTTTTTTTTTTTTTT", cnt)
    for shape in slide.shapes:
        #if not shape.has_text_frame:
        #    continue
        txt = "None"
        if hasattr(shape, "text"):
            txt = shape.text
        print('id: %s, height: %s, width: %s, left: %s'%(shape.shape_id, round(shape.height.inches,2), round(shape.width.inches,2), \
              round(shape.left.inches,2)), shape.shape_type, shape.name, txt) 
        
        if(shape.shape_type == MSO_SHAPE_TYPE.GROUP):
            print("FOUNDDDD")
            gshp = shape
            for shp in gshp.shapes:
                print('id: %s, height: %s, width: %s, left: %s'%(shp.shape_id, round(shp.height.inches,2), round(shp.width.inches,2), \
                      round(shp.left.inches,2)), shp.shape_type, shp.name, txt) 
                if(shp.has_text_frame):
                    print("GTEXTTTTT", shp.text)
                if(shp.has_chart):
                    print("CHARTTTTT")
        
        if shape.has_chart:
            print("FOUNDDDD")
        
        if shape.has_text_frame:
            text = (shape.text_frame.text)
            text = text.replace("\n"," ")
            text = text.replace("\r"," ")
            #print(text)
        if shape.has_table:
            print("FOUND", cnt)
            tbl = (shape.table)
            #for cell in tbl.iter_cells():
            #    print(cell.text)
        #for paragraph in shape.text_frame.paragraphs:
        #    for run in paragraph.runs:
        #        text_runs.append(run.text)
#print(text_runs)


CNTTTTTTTTTTTTTTT 1
id: 2, height: 0.09, width: 0.87, left: 0.85 TEXT_BOX (17) object 2 © Copyright Cloudﬂare, Inc.
id: 3, height: 5.62, width: 10.0, left: 0.0 AUTO_SHAPE (1) object 3 
id: 4, height: 5.62, width: 10.0, left: 0.0 FREEFORM (5) object 4 
id: 5, height: 0.17, width: 0.52, left: 0.26 AUTO_SHAPE (1) object 5 
id: 6, height: 0.11, width: 0.9, left: 0.84 TEXT_BOX (17) object 6 © Copyright Cloudﬂare, Inc.
id: 7, height: 0.67, width: 2.01, left: 0.76 AUTO_SHAPE (1) object 7 
id: 8, height: 0.28, width: 1.97, left: 0.72 TEXT_BOX (17) object 8 December 31, 2021
id: 9, height: 1.51, width: 5.0, left: 3.75 AUTO_SHAPE (1) object 9 
id: 10, height: 3.87, width: 5.44, left: 4.56 AUTO_SHAPE (1) object 10 
id: 11, height: 0.88, width: 7.47, left: 0.72 TEXT_BOX (17) object 11 Investor Presentation

CNTTTTTTTTTTTTTTT 2
id: 2, height: 0.17, width: 0.52, left: 0.26 AUTO_SHAPE (1) object 2 
id: 3, height: 0.11, width: 0.9, left: 0.84 TEXT_BOX (17) object 3 © Copyright Cloudﬂare, Inc.
id: 4, 

id: 10, height: 0.98, width: 6.6, left: 2.62 FREEFORM (5) object 10 
id: 11, height: 2.47, width: 2.1, left: 7.12 GROUP (6) object 11 None
FOUNDDDD
id: 12, height: 1.71, width: 2.09, left: 7.13 FREEFORM (5) object 12 None
GTEXTTTTT 
id: 13, height: 1.71, width: 2.09, left: 7.13 FREEFORM (5) object 13 None
GTEXTTTTT 
id: 14, height: 0.36, width: 0.0, left: 8.17 FREEFORM (5) object 14 None
GTEXTTTTT 
id: 15, height: 0.36, width: 0.36, left: 7.21 AUTO_SHAPE (1) object 15 None
GTEXTTTTT 
id: 16, height: 2.46, width: 6.44, left: 0.53 GROUP (6) object 16 None
FOUNDDDD
id: 17, height: 1.7, width: 4.35, left: 2.62 FREEFORM (5) object 17 None
GTEXTTTTT 
id: 18, height: 1.54, width: 2.0, left: 2.7 FREEFORM (5) object 18 None
GTEXTTTTT 
id: 19, height: 1.54, width: 2.0, left: 2.7 FREEFORM (5) object 19 None
GTEXTTTTT 
id: 20, height: 1.54, width: 2.0, left: 4.87 FREEFORM (5) object 20 None
GTEXTTTTT 
id: 21, height: 0.0, width: 2.06, left: 0.56 FREEFORM (5) object 21 None
GTEXTTTTT 
id: 22, heigh

id: 36, height: 0.12, width: 0.12, left: 7.97 FREEFORM (5) object 36 None
GTEXTTTTT 
id: 37, height: 0.12, width: 0.12, left: 5.37 FREEFORM (5) object 37 None
GTEXTTTTT 
id: 38, height: 0.13, width: 0.12, left: 5.4 FREEFORM (5) object 38 None
GTEXTTTTT 
id: 39, height: 1.0, width: 0.83, left: 4.5 FREEFORM (5) object 39 None
GTEXTTTTT 
id: 40, height: 0.4, width: 0.51, left: 4.69 TEXT_BOX (17) object 40 Global  Scale
id: 41, height: 0.4, width: 1.14, left: 4.38 TEXT_BOX (17) object 41 Helping Build a  Better Internet
id: 42, height: 4.07, width: 6.95, left: 1.49 GROUP (6) object 42 None
FOUNDDDD
id: 43, height: 0.62, width: 0.62, left: 1.49 AUTO_SHAPE (1) object 43 None
GTEXTTTTT 
id: 44, height: 0.53, width: 0.53, left: 7.91 AUTO_SHAPE (1) object 44 None
GTEXTTTTT 
id: 45, height: 0.69, width: 0.69, left: 4.6 AUTO_SHAPE (1) object 45 None
GTEXTTTTT 
id: 46, height: 0.69, width: 0.69, left: 4.6 AUTO_SHAPE (1) object 46 None
GTEXTTTTT 
id: 47, height: 0.4, width: 0.37, left: 3.12 AUTO_SH

id: 11, height: 1.3, width: 1.3, left: 7.46 FREEFORM (5) object 11 None
GTEXTTTTT 
id: 12, height: 0.69, width: 0.76, left: 7.73 TEXT_BOX (17) object 12 Extend our  serverless  platform  strategy
id: 13, height: 2.32, width: 8.4, left: 0.79 GROUP (6) object 13 None
FOUNDDDD
id: 14, height: 0.0, width: 8.32, left: 0.79 FREEFORM (5) object 14 None
GTEXTTTTT 
id: 15, height: 0.05, width: 0.06, left: 9.12 FREEFORM (5) object 15 None
GTEXTTTTT 
id: 16, height: 0.05, width: 0.06, left: 9.12 FREEFORM (5) object 16 None
GTEXTTTTT 
id: 17, height: 1.3, width: 1.3, left: 1.33 FREEFORM (5) object 17 None
GTEXTTTTT 
id: 18, height: 0.56, width: 1.66, left: 3.18 TEXT_BOX (17) object 18 Upgrading to premium plans
Increased usage
Adding products
id: 19, height: 0.74, width: 1.7, left: 1.36 TEXT_BOX (17) object 19 Grow awareness
Field sales
International coverage
Expand channel partnerships
id: 20, height: 0.36, width: 0.88, left: 1.54 TEXT_BOX (17) object 20 Acquire new  customers
id: 21, height: 1.3

id: 37, height: 0.21, width: 0.19, left: 7.91 TEXT_BOX (17) object 37 17
id: 38, height: 0.21, width: 0.18, left: 7.24 TEXT_BOX (17) object 38 11
id: 39, height: 0.17, width: 0.88, left: 7.65 TEXT_BOX (17) object 39 72% CAGR
id: 40, height: 1.91, width: 1.73, left: 7.34 GROUP (6) object 40 None
FOUNDDDD
id: 41, height: 1.77, width: 1.6, left: 7.35 FREEFORM (5) object 41 None
GTEXTTTTT 
id: 42, height: 0.17, width: 0.16, left: 8.9 AUTO_SHAPE (1) object 42 None
GTEXTTTTT 
id: 43, height: 1.8, width: 1.67, left: 0.85 GROUP (6) object 43 None
FOUNDDDD
id: 44, height: 1.67, width: 1.55, left: 0.86 FREEFORM (5) object 44 None
GTEXTTTTT 
id: 45, height: 0.17, width: 0.17, left: 2.35 AUTO_SHAPE (1) object 45 None
GTEXTTTTT 
id: 46, height: 0.17, width: 0.9, left: 4.22 TEXT_BOX (17) object 46 65% CAGR
id: 47, height: 1.8, width: 1.67, left: 4.05 GROUP (6) object 47 None
FOUNDDDD
id: 48, height: 1.67, width: 1.55, left: 4.07 FREEFORM (5) object 48 None
GTEXTTTTT 
id: 49, height: 0.17, width: 0.1

id: 58, height: 0.22, width: 0.48, left: 6.67 TEXT_BOX (17) object 58 (4)%
id: 59, height: 0.22, width: 0.34, left: 8.18 TEXT_BOX (17) object 59 1%
id: 60, height: 0.33, width: 1.1, left: 4.83 FREEFORM (5) object 60 
id: 61, height: 0.24, width: 0.39, left: 5.19 TEXT_BOX (17) object 61 15%
id: 62, height: 0.4, width: 1.1, left: 4.83 FREEFORM (5) object 62 
id: 63, height: 0.24, width: 0.42, left: 5.17 TEXT_BOX (17) object 63 20%
id: 64, height: 0.96, width: 1.1, left: 4.83 FREEFORM (5) object 64 
id: 65, height: 0.24, width: 0.42, left: 5.17 TEXT_BOX (17) object 65 45%

CNTTTTTTTTTTTTTTT 28
id: 2, height: 0.17, width: 0.52, left: 0.26 AUTO_SHAPE (1) object 2 
id: 3, height: 0.11, width: 0.9, left: 0.84 TEXT_BOX (17) object 3 © Copyright Cloudﬂare, Inc.
id: 4, height: 0.0, width: 4.45, left: 2.77 FREEFORM (5) object 4 
id: 5, height: 0.47, width: 1.26, left: 2.0 TEXT_BOX (17) object 5 $205.0 - 206.0
48% - 49%
id: 6, height: 0.47, width: 0.9, left: 2.18 TEXT_BOX (17) object 6 $0.5 - $1.5